In [1]:
import numpy as np
import os
import pandas as pd
import arcpy

# Import the required ArcGIS API for Python modules
import arcgis
from arcgis.gis import GIS
gis = arcgis.GIS()
from arcgis.geoanalytics import manage_data

from IPython.display import display, Markdown

In [2]:
dirWork         = os.getcwd()
year            = '2019'
dirInput        = os.path.join(dirWork, r'data\data' + year                       )
dirIntermediate = os.path.join(dirWork, 'intermediate\intermediate' + year + '\SL')
dirResults      = os.path.join(dirWork, r'results\results' + year + '\SL'         )

print("Working Directory: "      + dirWork        )
print("Input Directory: "        + dirInput       )
print("Intermediate Directory: " + dirIntermediate)
print("Results Directory: "      + dirResults     )

Working Directory: c:\Users\cday\Documents\projects\Census-LEHD-Commute-Patterns
Input Directory: c:\Users\cday\Documents\projects\Census-LEHD-Commute-Patterns\data\data2019
Intermediate Directory: c:\Users\cday\Documents\projects\Census-LEHD-Commute-Patterns\intermediate\intermediate2019\SL
Results Directory: c:\Users\cday\Documents\projects\Census-LEHD-Commute-Patterns\results\results2019\SL


In [3]:
dirIntermediate

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\intermediate\\intermediate2019\\SL'

In [4]:
#input filenames
fname_CityTownship_csv        = os.path.join(dirInput, 'citytownship.csv'                                         )
fname_CityTownship_shp        = os.path.join(dirInput, 'Municipalities_Township' + r'\Municipalities_Township.shp') 
fname_SLCommutePatterns_csv = os.path.join(dirInput, 'sl_at_blockgroup_level' + year + '.csv'                   )
#fname_UofUManualAllocation_csv= os.path.join(dirInput, '490351108004_Manual_Allocation.csv'                      )
fname_BlockGroups_shp         = os.path.join(dirInput, 'tl_2020_49_bg' + r'\tl_2020_49_sd_bg.shp'                 )
fname_Counties_AGRC_shp       = os.path.join(dirInput, 'Utah_County_Boundaries-shp' + r'\Counties.shp'            )
fname_SLCommutePatterns_csv

#intermediate
fname_CityTownshipCounty_BlockGroups_shp = os.path.join(dirIntermediate, 'citytownshipcounty_blockgroup_intersect.shp')
fname_CityTownshipWCodes_shp             = os.path.join(dirIntermediate, 'Municipalities_Townships_withCodes.shp')
fname_CountyWCodes_shp                   = os.path.join(dirIntermediate, 'Counties_withCodes.shp')
fname_CityTownshipWCodesUnionCounty_shp  = os.path.join(dirIntermediate, 'Municipalities_Townships_withCodes_Counties.shp')
fname_CityTownshipCountyWCodes_shp       = os.path.join(dirIntermediate, 'Municipalities_Townships_Counties_withCodes.shp')

#display(dirIntermediate)

#results geodatabase

fname_CityTownshipJSON = os.path.join(dirResults, "sl_citytownshipdata.json")

gdb_SLCommutePatterns = "SLCommutePatterns.gdb"
fname_SLCommutePatterns_gdb = os.path.join(dirResults, gdb_SLCommutePatterns)

fname_CityTownshipWCodes = os.path.join(fname_SLCommutePatterns_gdb, 'Municipalities_and_Townships')
#fname_CityTownshipCounty = os.path.join(fname_SLCommutePatterns_gdb, 'Municipalities_Townships_Counties')

fname_BlockGroupsWCommutePatterns_Number = os.path.join(fname_SLCommutePatterns_gdb, 'SL_BlockGroup_CommutePatterns_Number')
fname_BlockGroupsWCommutePatterns_Percent_SA = os.path.join(fname_SLCommutePatterns_gdb, 'SL_BlockGroup_CommutePatterns_Percent_SelectedArea')
fname_BlockGroupsWCommutePatterns_Percent_MU = os.path.join(fname_SLCommutePatterns_gdb, 'SL_BlockGroup_CommutePatterns_Percent_MapUnit')

fname_TractsWCommutePatterns_Number = os.path.join(fname_SLCommutePatterns_gdb, 'SL_Tract_CommutePatterns_Number')
fname_TractsWCommutePatterns_Percent_SA = os.path.join(fname_SLCommutePatterns_gdb, 'SL_Tract_CommutePatterns_Percent_SelectedArea')
fname_TractsWCommutePatterns_Percent_MU = os.path.join(fname_SLCommutePatterns_gdb, 'SL_Tract_CommutePatterns_Percent_MapUnit')

fname_SDWCommutePatterns_Number = os.path.join(fname_SLCommutePatterns_gdb, 'SL_SD_CommutePatterns_Number')
fname_SDWCommutePatterns_Percent_SA = os.path.join(fname_SLCommutePatterns_gdb, 'SL_SD_CommutePatterns_Percent_SelectedArea')
fname_SDWCommutePatterns_Percent_MU = os.path.join(fname_SLCommutePatterns_gdb, 'SL_SD_CommutePatterns_Percent_MapUnit')

fname_CitiesWCommutePatterns_Number = os.path.join(fname_SLCommutePatterns_gdb, 'SL_City_CommutePatterns_Number')
fname_CitiesWCommutePatterns_Percent_SA = os.path.join(fname_SLCommutePatterns_gdb, 'SL_City_CommutePatterns_Percent_SelectedArea')
fname_CitiesWCommutePatterns_Percent_MU = os.path.join(fname_SLCommutePatterns_gdb, 'SL_City_CommutePatterns_Percent_MapUnit')

fname_Counties = os.path.join(fname_SLCommutePatterns_gdb, 'Counties')

def deleteIfExists(obj):
    if arcpy.Exists(obj): arcpy.Delete_management(obj)

#if results geodatabase doesn't exist, create it
print("Checking if " + fname_SLCommutePatterns_gdb + " exists...")
if not arcpy.Exists(os.path.join(dirResults, gdb_SLCommutePatterns)):
    print("Creating " + fname_SLCommutePatterns_gdb + "...")
    arcpy.management.CreateFileGDB(dirResults, gdb_SLCommutePatterns)
else:
    print(gdb_SLCommutePatterns + " exists...")

#print(AnalysisAreasInput)

Checking if c:\Users\cday\Documents\projects\Census-LEHD-Commute-Patterns\results\results2019\SL\SLCommutePatterns.gdb exists...
Creating c:\Users\cday\Documents\projects\Census-LEHD-Commute-Patterns\results\results2019\SL\SLCommutePatterns.gdb...


# Create Cities/Townships Feature Class with 3-Digit Code and County FIPS

In [5]:
#read in city/township shapefile, SHORTDESC is common field between this and CODE3 dataset
sdf_CityTownship = pd.DataFrame.spatial.from_featureclass(fname_CityTownship_shp)
display(sdf_CityTownship)

FID COUNTYNBR                              NAME  COUNTYSEAT  \
0      0        03                            Newton           0   
1      1        12                            Eureka           0   
2      2        29                        Huntsville           0   
3      3        27                        Springdale           0   
4      4        23                       Grantsville           0   
..   ...       ...                               ...         ...   
253  253        18          COPPERTON METRO TOWNSHIP           0   
254  254        18             KEARNS METRO TOWNSHIP           0   
255  255        18              MAGNA METRO TOWNSHIP           0   
256  256        18  EMIGRATION CANYON METRO TOWNSHIP           0   
257  257        18         WHITE CITY METRO TOWNSHIP           0   

             SHORTDESC    UPDATED   FIPS  ENTITYNBR SALESTAXID  IMSCOLOR  \
0               NEWTON 2018-09-19  54550     3100.0        047         2   
1               EUREKA 2018-09-19  24080     3010.0        009         2   
2           HUNTSVILLE 2014-10-15  37060     3030.0        019         4   
3           SPRINGDALE 2014-10-15  71840     3100.0        023         2   
4          GRANTSVILLE 2020-06-05  31120     3010.0        023         2   
..                 ...        ...    ...        ...        ...       ...   
253          Copperton 2016-12-27  15720        0.0                    0   
254             Kearns 2016-12-27  40470        0.0                    0   
255              Magna 2018-11-14  47290        0.0                    0   
256  Emigration Canyon 2016-12-27  22875        0.0                    0   
257         White City 2016-12-27  84050        0.0                    0   

               MINNAME  POPLASTCEN  POPLASTEST     GNIS  \
0                              801         813  1430705   
1                              693         695  1437974   
2           Huntsville         602         638  1428949   
3           Springdale         569         609  1432867   
4                             9152       11568  1428338   
..                 ...         ...         ...      ...   
253          Copperton         822         835            
254             Kearns       35769       36330            
255              Magna       26513       26949            
256  Emigration Canyon        1568        1592            
257         White City        5686        5768            

                                   GlobalID  SHAPE_Leng  SHAPE_Area  \
0    {1C320704-F3E4-4D4F-A542-F6FFE3C36900}    0.071275    0.000240   
1    {E1F6AAAD-E49E-4820-A270-D3E7C2131A80}    0.100706    0.000395   
2    {E9A934D8-FE13-4A6D-925E-73A9988E3F17}    0.126158    0.000246   
3    {E6E76C45-D141-47DF-9C96-D3D46F15A2B9}    0.193621    0.001208   
4    {5F5B6417-7EF9-49B5-A689-CBF42953DC9D}    0.772545    0.010742   
..                                      ...         ...         ...   
253  {B3F64B90-565B-44B4-8C7B-87000672B734}    0.067294    0.000086   
254  {75A0B23A-775B-44DC-BCCA-4E504BF9E548}    0.185692    0.001277   
255  {28F85E1F-72D3-43E5-BBF4-F85CC28898D5}    0.756349    0.010342   
256  {29B91C07-4DE5-4395-8337-6E13304256BB}    0.350202    0.005034   
257  {2C41A42F-87EE-4D97-AED2-6619D82F72AF}    0.147366    0.000241   

                                                 SHAPE  
0    {"rings": [[[-112.00138477499996, 41.855487523...  
1    {"rings": [[[-112.09987515199998, 39.957670251...  
2    {"rings": [[[-111.76117535999998, 41.253396941...  
3    {"rings": [[[-112.97934207899999, 37.197581387...  
4    {"rings": [[[-112.37537669199997, 40.593511564...  
..                                                 ...  
253  {"rings": [[[-112.09934129299995, 40.562296682...  
254  {"rings": [[[-111.98660579699998, 40.667567316...  
255  {"rings": [[[-112.10619664199999, 40.691640141...  
256  {"rings": [[[-111.74338063899995, 40.818777216...  
257  {"rings": [[[-111.86273107599999, 40.581548957...  

[258 rows x 18 columns]

In [6]:
#rename METRO TOWNSHIPs to match CODE3 dataset
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'WHITE CITY METRO TOWNSHIP'       , 'SHORTDESC'] = "WHITE CITY METRO TOWNSHIP"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'EMIGRATION CANYON METRO TOWNSHIP', 'SHORTDESC'] = "EMIGRATION CANYON METRO TOWNSHIP"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'COPPERTON METRO TOWNSHIP'        , 'SHORTDESC'] = "COPPERTON METRO TOWNSHIP"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'MAGNA METRO TOWNSHIP'            , 'SHORTDESC'] = "MAGNA METRO TOWNSHIP"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'KEARNS METRO TOWNSHIP'           , 'SHORTDESC'] = "KEARNS METRO TOWNSHIP"

#give townships a better name
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'WHITE CITY METRO TOWNSHIP'       , 'NAME'] = "White City"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'EMIGRATION CANYON METRO TOWNSHIP', 'NAME'] = "Emigration Canyon"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'COPPERTON METRO TOWNSHIP'        , 'NAME'] = "Copperton"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'MAGNA METRO TOWNSHIP'            , 'NAME'] = "Magna"
sdf_CityTownship.loc[sdf_CityTownship.NAME == 'KEARNS METRO TOWNSHIP'           , 'NAME'] = "Kearns"

In [7]:
#read in township codes data
df_CityTownshipCodes = pd.read_csv(fname_CityTownship_csv)

#consolidate Hideout
df_CityTownshipCodes = df_CityTownshipCodes.loc[df_CityTownshipCodes.SHORTDESC != 'HIDEOUT (WASATCH)']
df_CityTownshipCodes = df_CityTownshipCodes.loc[df_CityTownshipCodes.SHORTDESC != 'HIDEOUT (SUMMIT)']

# get wfrc city/townships only
wfrc_towns  = ["AFK","ALA","ALP","BDL","BGM","BNT","BRT","CDF","CEN","CHA","CHL","CLF","CLI","CMT","COA","CWH","DAN","DRA","EAG","ELK","EMT","FAR","FCS","FFD","FRR","FTH","GLA","GOS","GRL","HAR","HDT","HDT","HEB","HER","HGH","HNF","HOL","HOO","HVL","IND","INT","KAY","KMS","KMT","LAY","LEH","LIN","MAP","MID","MLC","MMT","MRG","MSL","MUR","MWY","NOG","NSL","OGD","OKL","ORM","PAY","PGR","PLN","PRK","PRY","PVO","PVW","ROY","RVD","RVT","SAN","SAQ","SAR","SFK","SJC","SLC","SLM","SOG","SPV","SSL","SUN","SWE","SYR","TAY","TOO","UIN","VIN","WAT","WBG","WDL","WEB","WHT","WHV","WIL","WJC","WPT","WVC","WXC"]
df_CityTownshipCodes = df_CityTownshipCodes[df_CityTownshipCodes['CODE3'].isin(wfrc_towns)].reset_index(drop=True)

df_CityTownshipCodes

SHORTDESC CODE3
0          AMERICAN FORK   AFK
1                   ALTA   ALA
2                 ALPINE   ALP
3      BLUFFDALE (SL CO)   BDL
4    BLUFFDALE (UTAH CO)   BDL
..                   ...   ...
96          WILLARD CITY   WIL
97      WEST JORDAN CITY   WJC
98            WEST POINT   WPT
99      WEST VALLEY CITY   WVC
100     WOODS CROSS CITY   WXC

[101 rows x 2 columns]

In [8]:
#join spatial data frame to data frame with codes using SHORTDESC field as key between two
sdf_CityTownshipWCodes = pd.DataFrame.merge(sdf_CityTownship, df_CityTownshipCodes, on='SHORTDESC')

#export to intermediate location so that it can be used in dissolve function later (to remove cities that span counties)
sdf_CityTownshipWCodes.spatial.to_featureclass(fname_CityTownshipWCodes_shp, sanitize_columns=False)

display(sdf_CityTownshipWCodes)

FID COUNTYNBR               NAME  COUNTYSEAT  \
0      2        29         Huntsville           0   
1      4        23        Grantsville           0   
2      5        18          Bluffdale           0   
3      7        18           Herriman           0   
4     13        18       Taylorsville           0   
..   ...       ...                ...         ...   
96   253        18          Copperton           0   
97   254        18             Kearns           0   
98   255        18              Magna           0   
99   256        18  Emigration Canyon           0   
100  257        18         White City           0   

                            SHORTDESC    UPDATED   FIPS  ENTITYNBR SALESTAXID  \
0                          HUNTSVILLE 2014-10-15  37060     3030.0        019   
1                         GRANTSVILLE 2020-06-05  31120     3010.0        023   
2                   BLUFFDALE (SL CO) 2018-11-15  06810     3020.0        019   
3                       HERRIMAN TOWN 2019-11-22  34970     3035.0        060   
4                   TAYLORSVILLE CITY 2014-09-15  75360     3105.0        142   
..                                ...        ...    ...        ...        ...   
96           COPPERTON METRO TOWNSHIP 2016-12-27  15720        0.0              
97              KEARNS METRO TOWNSHIP 2016-12-27  40470        0.0              
98               MAGNA METRO TOWNSHIP 2018-11-14  47290        0.0              
99   EMIGRATION CANYON METRO TOWNSHIP 2016-12-27  22875        0.0              
100         WHITE CITY METRO TOWNSHIP 2016-12-27  84050        0.0              

     IMSCOLOR            MINNAME  POPLASTCEN  POPLASTEST     GNIS  \
0           4         Huntsville         602         638  1428949   
1           2                           9152       11568  1428338   
2           4                           7693       14699  1425844   
3           1                          22018       44877  1428675   
4           4       Taylorsville       59989       60192  1433206   
..        ...                ...         ...         ...      ...   
96          0          Copperton         822         835            
97          0             Kearns       35769       36330            
98          0              Magna       26513       26949            
99          0  Emigration Canyon        1568        1592            
100         0         White City        5686        5768            

                                   GlobalID  SHAPE_Leng  SHAPE_Area  \
0    {E9A934D8-FE13-4A6D-925E-73A9988E3F17}    0.126158    0.000246   
1    {5F5B6417-7EF9-49B5-A689-CBF42953DC9D}    0.772545    0.010742   
2    {E52CE320-1532-4A57-8DB9-DFA819FBB85B}    0.303290    0.002868   
3    {3E78F48D-80B9-44DA-AC9F-836A7B4F1B8E}    0.617524    0.005943   
4    {3ADD19D5-EF23-4257-8048-E355AE283BC6}    0.303444    0.002991   
..                                      ...         ...         ...   
96   {B3F64B90-565B-44B4-8C7B-87000672B734}    0.067294    0.000086   
97   {75A0B23A-775B-44DC-BCCA-4E504BF9E548}    0.185692    0.001277   
98   {28F85E1F-72D3-43E5-BBF4-F85CC28898D5}    0.756349    0.010342   
99   {29B91C07-4DE5-4395-8337-6E13304256BB}    0.350202    0.005034   
100  {2C41A42F-87EE-4D97-AED2-6619D82F72AF}    0.147366    0.000241   

                                                 SHAPE CODE3  
0    {"rings": [[[-111.76117535999998, 41.253396941...   HVL  
1    {"rings": [[[-112.37537669199997, 40.593511564...   GRL  
2    {"rings": [[[-111.94473146099995, 40.497759794...   BDL  
3    {"rings": [[[-112.06032590299998, 40.481954434...   HER  
4    {"rings": [[[-111.92081851599994, 40.685958404...   TAY  
..                                                 ...   ...  
96   {"rings": [[[-112.09934129299995, 40.562296682...   CMT  
97   {"rings": [[[-111.98660579699998, 40.667567316...   KMT  
98   {"rings": [[[-112.10619664199999, 40.691640141...   MMT  
99   {"rings": [[[-111.74338063899995, 40.818777216...   EMT  
100  {"rings": [[[-1

In [9]:
#dissolve by code, due to some cities spanning counties and having multiple records in codes and/or munis/townships
deleteIfExists(fname_CityTownshipWCodes)
arcpy.management.Dissolve(fname_CityTownshipWCodes_shp, fname_CityTownshipWCodes, ['CODE3'], [['NAME','FIRST'], ['COUNTYNBR','FIRST']])

sdf_CityTownshipWCodes = pd.DataFrame.spatial.from_featureclass(fname_CityTownshipWCodes)
sdf_CityTownshipWCodes = sdf_CityTownshipWCodes.rename(columns={"code3":"CODE3", "FIRST_name":"FIRST_NAME", "FIRST_countynbr":"FIRST_COUNTYNBR"})

display(sdf_CityTownshipWCodes)

OBJECTID CODE3        FIRST_NAME FIRST_COUNTYNBR  \
0          1   AFK     American Fork              25   
1          2   ALA              Alta              18   
2          3   ALP            Alpine              25   
3          4   BDL         Bluffdale              18   
4          5   BGM      Brigham City              02   
..       ...   ...               ...             ...   
92        93   WIL           Willard              02   
93        94   WJC       West Jordan              18   
94        95   WPT        West Point              06   
95        96   WVC  West Valley City              18   
96        97   WXC       Woods Cross              06   

                                                SHAPE  
0   {"rings": [[[-111.77435121873373, 40.353624868...  
1   {"rings": [[[-111.59946851855727, 40.577431980...  
2   {"rings": [[[-111.75455302160464, 40.479513910...  
3   {"rings": [[[-111.9704071902396, 40.5008379065...  
4   {"rings": [[[-112.01898409573937, 41.535781784...  
..                                                ...  
92  {"rings": [[[-112.02999503963935, 41.391465965...  
93  {"rings": [[[-112.00475852158849, 40.638664299...  
94  {"rings": [[[-112.10779328273378, 41.143687479...  
95  {"rings": [[[-111.9626132723846, 40.7260972067...  
96  {"rings": [[[-111.89260269236036, 40.866220107...  

[97 rows x 5 columns]

In [10]:
df_CityTownship_NameCode = sdf_CityTownshipWCodes[['FIRST_NAME','CODE3','FIRST_COUNTYNBR']].copy()
df_CityTownship_NameCode = df_CityTownship_NameCode.sort_values(by=['FIRST_NAME'])

df_CityTownship_NameCode.columns = ('NAME','CODE3','COUNTYNBR')

display(df_CityTownship_NameCode)

#df_CityTownship_NameCode.to_json(os.path.join(dirResults, "citytownshipdata.json"),orient='records')
#export after adding workers and residents columns from data

NAME CODE3 COUNTYNBR
2             Alpine   ALP        25
1               Alta   ALA        18
0      American Fork   AFK        25
3          Bluffdale   BDL        18
5          Bountiful   BNT        06
..               ...   ...       ...
95  West Valley City   WVC        18
90        White City   WHT        18
92           Willard   WIL        02
88    Woodland Hills   WDL        25
96       Woods Cross   WXC        06

[97 rows x 3 columns]

In [11]:
#explicit definition of county for cross-county cities
df_CityTownship_NameCode.loc[((df_CityTownship_NameCode['CODE3'] == 'BDL')), 'COUNTYNBR'] = '18'
df_CityTownship_NameCode.loc[((df_CityTownship_NameCode['CODE3'] == 'DRA')), 'COUNTYNBR'] = '18'
df_CityTownship_NameCode.loc[((df_CityTownship_NameCode['CODE3'] == 'HDT')), 'COUNTYNBR'] = '26'
df_CityTownship_NameCode.loc[((df_CityTownship_NameCode['CODE3'] == 'PRK')), 'COUNTYNBR'] = '22'

#read in county dataset
sdf_CountiesAGRC = pd.DataFrame.spatial.from_featureclass(fname_Counties_AGRC_shp)
sdf_CountiesAGRC['FIPS'   ] = sdf_CountiesAGRC['FIPS'].astype(int)
sdf_CountiesAGRC['zCOFIPS'] = 'z' + sdf_CountiesAGRC['FIPS'].astype(str).str.zfill(2) #add 'z' instead of 0, so that columns names won't start with number, and so sorts at end
sdf_CountiesAGRC['CO_NAME'] = sdf_CountiesAGRC['NAME'].str.title() + ' County'
display(sdf_CountiesAGRC)

#join by COUNTYNBR to get CO_FIPS
df_CityTownship_NameCode_wCOFIPS = pd.DataFrame.merge(df_CityTownship_NameCode,sdf_CountiesAGRC,on='COUNTYNBR')
display(df_CityTownship_NameCode_wCOFIPS)


df_CityTownship_NameCode = df_CityTownship_NameCode_wCOFIPS[['NAME_x','CODE3','zCOFIPS']]
df_CityTownship_NameCode.columns = ('NAME','CODE3','zCOFIPS')

display(df_CityTownship_NameCode)

FID  OBJECTID COUNTYNBR     ENTITYNBR  ENTITYYR        NAME  FIPS  \
0     0         1        03  2.010031e+09    2010.0       CACHE     5   
1     1         2        07  2.010071e+09    2010.0    DUCHESNE    13   
2     2         3        06  2.010061e+09    2010.0       DAVIS    11   
3     3         4        14  2.010141e+09    2010.0     MILLARD    27   
4     4         5        26  2.010261e+09    2010.0     WASATCH    51   
5     5         6        02  2.010021e+09    2010.0   BOX ELDER     3   
6     6         7        29  2.010291e+09    2010.0       WEBER    57   
7     7         8        12  2.010121e+09    2010.0        JUAB    23   
8     8         9        20  2.010201e+09    2010.0     SANPETE    39   
9     9        10        27  2.010271e+09    2010.0  WASHINGTON    53   
10   10        11        10  2.010101e+09    2010.0       GRAND    19   
11   11        12        17  2.010171e+09    2010.0        RICH    33   
12   12        13        04  2.010041e+09    2010.0      CARBON     7   
13   13        14        05  2.010051e+09    2010.0     DAGGETT     9   
14   14        15        01  2.010011e+09    2010.0      BEAVER     1   
15   15        16        21  2.010211e+09    2010.0      SEVIER    41   
16   16        17        09  2.010091e+09    2010.0    GARFIELD    17   
17   17        18        23  2.010231e+09    2010.0      TOOELE    45   
18   18        19        22  2.010221e+09    2010.0      SUMMIT    43   
19   19        20        16  2.010161e+09    2010.0       PIUTE    31   
20   20        21        24  2.010241e+09    2010.0      UINTAH    47   
21   21        22        11  2.010111e+09    2010.0        IRON    21   
22   22        23        08  2.010081e+09    2010.0       EMERY    15   
23   23        24        28  2.010281e+09    2010.0       WAYNE    55   
24   24        25        19  2.006191e+09    2006.0    SAN JUAN    37   
25   25        26        15  2.010151e+09    2010.0      MORGAN    29   
26   26        27        13  2.010131e+09    2010.0        KANE    25   
27   27        28        18  2.010181e+09    2010.0   SALT LAKE    35   
28   28        29        25  2.010251e+09    2010.0        UTAH    49   

   STATEPLANE  POP_LASTCE  POP_CURRES                                GlobalID  \
0       North      112656      128289  {59BEE5FF-00D6-414A-8CD9-3B9CF5FA25FB}   
1     Central       18607       19938  {AAE112BD-8D24-46EE-98CD-6689B87A14D1}   
2       North      306479      355481  {66DDE457-AF53-4B6D-9A7D-25F29FCCF626}   
3     Central       12503       13188  {DE7E933D-7233-4FBE-8D0C-5E0826EF05D7}   
4     Central       23530       34091  {1BAA04F5-D976-4917-BBF2-BE9C0F868C55}   
5       North       49975       56046  {2F4FBEBE-32DB-4A2D-A6D1-277679BDF193}   
6       North      231236      260213  {7F2E8776-C886-4F23-9D40-B861B1FB5391}   
7     Central       10246       12017  {7A6D2476-AE18-48E8-820B-CE97B805879F}   
8     Central       27822       30939  {323210BE-8E14-49FE-96FE-1C571E744993}   
9       South      138115      177556  {A13328EF-DD99-45B8-897C-A9FE2418E7CA}   
10    Central        9225        9754  {6246AFC5-101A-4D5B-8355-1910ED7CF71D}   
11      North        2264        2483  {0362BF2D-2424-4C0C-AF74-7FC49DDAF467}   
12    Central       21403       20463  {F9F3A18C-023D-42E3-AB18-3168BA3C9446}   
13      North        1059         950  {A1C114E4-6F14-452C-8157-F199752416CE}   
14      South        6629        6710  {14543D4C-CB01-4B05-AB19-DA399ABFD0ED}   
15    Central       20802       21620  {C9ECC2C2-7282-4B4E-9B47-D53CBB880820}   
16      South        5172        5051  {579769A4-4616-4A9B-92F0-9CFB2AEFD176}   
17    Central       58218       72259  {197FEA12-E2B4-4514-9A3C-963D8244A1E3}   
18      North       36324       42145  {EE2B9872-701C-470A-A300-1DB609C67F24}   
19      South        1556        1479  {E4A8F0F6-AE75-4DAA-AF72-298AC8274F7D}   
20    Central       32588       35734  {8FAEFFAA-95C1-404A-8862-3CCC91A0C412}   
21      South       46163      

NAME_x CODE3 COUNTYNBR  FID  OBJECTID     ENTITYNBR  ENTITYYR  \
0           Alpine   ALP        25   28        29  2.010251e+09    2010.0   
1    American Fork   AFK        25   28        29  2.010251e+09    2010.0   
2       Cedar Fort   CDF        25   28        29  2.010251e+09    2010.0   
3      Cedar Hills   CHL        25   28        29  2.010251e+09    2010.0   
4   Eagle Mountain   EAG        25   28        29  2.010251e+09    2010.0   
..             ...   ...       ...  ...       ...           ...       ...   
92      West Haven   WHV        29    6         7  2.010291e+09    2010.0   
93     Grantsville   GRL        23   17        18  2.010231e+09    2010.0   
94          Tooele   TOO        23   17        18  2.010231e+09    2010.0   
95          Morgan   MRG        15   25        26  2.010151e+09    2010.0   
96       Santaquin   SAQ        12    7         8  2.010121e+09    2010.0   

    NAME_y  FIPS STATEPLANE  POP_LASTCE  POP_CURRES  \
0     UTAH    49    Central      516564      636235   
1     UTAH    49    Central      516564      636235   
2     UTAH    49    Central      516564      636235   
3     UTAH    49    Central      516564      636235   
4     UTAH    49    Central      516564      636235   
..     ...   ...        ...         ...         ...   
92   WEBER    57      North      231236      260213   
93  TOOELE    45    Central       58218       72259   
94  TOOELE    45    Central       58218       72259   
95  MORGAN    29      North        9469       12124   
96    JUAB    23    Central       10246       12017   

                                  GlobalID FIPS_STR  COLOR4  SHAPE_Leng  \
0   {33E4105B-187C-4C0B-8F1C-D091F44BEFB1}    49049       3    5.073804   
1   {33E4105B-187C-4C0B-8F1C-D091F44BEFB1}    49049       3    5.073804   
2   {33E4105B-187C-4C0B-8F1C-D091F44BEFB1}    49049       3    5.073804   
3   {33E4105B-187C-4C0B-8F1C-D091F44BEFB1}    49049       3    5.073804   
4   {33E4105B-187C-4C0B-8F1C-D091F44BEFB1}    49049       3    5.073804   
..                                     ...      ...     ...         ...   
92  {7F2E8776-C886-4F23-9D40-B861B1FB5391}    49057       1    2.973528   
93  {197FEA12-E2B4-4514-9A3C-963D8244A1E3}    49045       2    6.105650   
94  {197FEA12-E2B4-4514-9A3C-963D8244A1E3}    49045       2    6.105650   
95  {08CCA506-439E-4F9E-8302-50A6B9468EF5}    49029       2    2.862360   
96  {7A6D2476-AE18-48E8-820B-CE97B805879F}    49023       4    6.802360   

    SHAPE_Area                                              SHAPE zCOFIPS  \
0     0.586227  {'rings': [[[-111.59404929699997, 40.577075300...     z49   
1     0.586227  {'rings': [[[-111.59404929699997, 40.577075300...     z49   
2     0.586227  {'rings': [[[-111.59404929699997, 40.577075300...     z49   
3     0.586227  {'rings': [[[-111.59404929699997, 40.577075300...     z49   
4     0.586227  {'rings': [[[-111.59404929699997, 40.577075300...     z49   
..         ...                                                ...     ...   
92    0.183659  {'rings': [[[-111.92092166399999, 41.138676415...     z57   
93    2.003307  {'rings': [[[-112.44788691599996, 41.017030151...     z45   
94    2.003307  {'rings': [[[-112.44788691599996, 41.017030151...     z45   
95    0.169567  {'rings': [[[-111.51438719299995, 40.803633660...     z29   
96    0.926379  {'rings': [[[-112.17814760399995, 40.011304953...     z23   

          CO_NAME  
0     Utah County  
1     Utah County  
2     Utah County  
3     Utah County  
4     Utah County  
..            ...  
92   Weber County  
93  Tooele County  
94  Tooele County  
95  Morgan County  
96    Juab County  

[97 rows x 20 columns]

NAME CODE3 zCOFIPS
0           Alpine   ALP     z49
1    American Fork   AFK     z49
2       Cedar Fort   CDF     z49
3      Cedar Hills   CHL     z49
4   Eagle Mountain   EAG     z49
..             ...   ...     ...
92      West Haven   WHV     z57
93     Grantsville   GRL     z45
94          Tooele   TOO     z45
95          Morgan   MRG     z29
96       Santaquin   SAQ     z23

[97 rows x 3 columns]

# Add Rows for County Level Totals

In [12]:
#read in csv with commute pattern data
df_SLCommutePatterns = pd.read_csv(fname_SLCommutePatterns_csv)

In [13]:
#get all column codes for summing
dfColCodes = df_SLCommutePatterns.loc[1:1,'AFK_o':'TTL_d'].T #get all columns from AFK_x through TTL_y
dfColCodes = dfColCodes.reset_index()

#convert to list for ease of calcs in future steps
dColCodes = dfColCodes['index'].values.tolist()
dColCodes

['AFK_o',
 'ALA_o',
 'ALP_o',
 'BDL_o',
 'BGM_o',
 'BNT_o',
 'BRT_o',
 'CDF_o',
 'CEN_o',
 'CHA_o',
 'CHL_o',
 'CLF_o',
 'CLI_o',
 'CMT_o',
 'COA_o',
 'CWH_o',
 'DAN_o',
 'DRA_o',
 'EAG_o',
 'ELK_o',
 'EMT_o',
 'FAR_o',
 'FCS_o',
 'FFD_o',
 'FRR_o',
 'FTH_o',
 'GLA_o',
 'GOS_o',
 'GRL_o',
 'HAR_o',
 'HDT_o',
 'HEB_o',
 'HER_o',
 'HGH_o',
 'HNF_o',
 'HOL_o',
 'HOO_o',
 'HVL_o',
 'IND_o',
 'INT_o',
 'KAY_o',
 'KMS_o',
 'KMT_o',
 'LAY_o',
 'LEH_o',
 'LIN_o',
 'MAP_o',
 'MID_o',
 'MLC_o',
 'MMT_o',
 'MRG_o',
 'MSL_o',
 'MUR_o',
 'MWY_o',
 'NOG_o',
 'NSL_o',
 'OGD_o',
 'OKL_o',
 'ORM_o',
 'PAY_o',
 'PGR_o',
 'PLN_o',
 'PRK_o',
 'PRY_o',
 'PVO_o',
 'PVW_o',
 'ROY_o',
 'RVD_o',
 'RVT_o',
 'SAN_o',
 'SAQ_o',
 'SAR_o',
 'SFK_o',
 'SJC_o',
 'SLC_o',
 'SLM_o',
 'SOG_o',
 'SPV_o',
 'SSL_o',
 'SUN_o',
 'SWE_o',
 'SYR_o',
 'TAY_o',
 'TOO_o',
 'UIN_o',
 'VIN_o',
 'WAT_o',
 'WBG_o',
 'WDL_o',
 'WEB_o',
 'WHT_o',
 'WHV_o',
 'WIL_o',
 'WJC_o',
 'WPT_o',
 'WVC_o',
 'WXC_o',
 'TTL_o',
 'AFK_d',
 'ALA_d',


In [14]:
#normalize (melt) commute data so that columns become rows
df_SLCommutePatterns_Normalized = pd.melt(df_SLCommutePatterns, id_vars=['fakeid','GEOID'], value_vars=dColCodes)

#populate new fields with data from previous column names (ABC_x/y): CODE3 and Category (_x/_y)
df_SLCommutePatterns_Normalized['CODE3'   ] = df_SLCommutePatterns_Normalized['variable'].str[0:3]
df_SLCommutePatterns_Normalized['CATEGORY'] = df_SLCommutePatterns_Normalized['variable'].str[3:5]

#join with City/Township data using CODE3
df_SLCommutePatterns_Normalized_wCOFIPS = pd.DataFrame.merge(df_CityTownship_NameCode, df_SLCommutePatterns_Normalized, on='CODE3')
display(df_SLCommutePatterns_Normalized_wCOFIPS)

#get county totals for each GEOID by aggregating (groupby)
df_SLCommutePatterns_CountyTotals_Normalized = df_SLCommutePatterns_Normalized_wCOFIPS.groupby(['zCOFIPS','GEOID','CATEGORY'],as_index=False).agg({'value':np.sum})

#create column names for county level totals
df_SLCommutePatterns_CountyTotals_Normalized['zCOFIPS_wCat'] = df_SLCommutePatterns_CountyTotals_Normalized['zCOFIPS'] + df_SLCommutePatterns_CountyTotals_Normalized['CATEGORY']

#create pivot table to reverse normalization, returning structure to original format, but this time with county columns
df_SLCommutePatterns_CountyTotals = df_SLCommutePatterns_CountyTotals_Normalized.pivot(index='GEOID', columns='zCOFIPS_wCat')['value']

display(df_SLCommutePatterns_CountyTotals)

NAME CODE3 zCOFIPS  fakeid         GEOID variable        value  \
0          Alpine   ALP     z49     0.0        colSUM    ALP_o  2604.511849   
1          Alpine   ALP     z49     0.0  490011001001    ALP_o     0.000257   
2          Alpine   ALP     z49     0.5  490011001002    ALP_o     0.000011   
3          Alpine   ALP     z49     1.0  490011001003    ALP_o     0.004286   
4          Alpine   ALP     z49     1.5  490011002001    ALP_o     0.000000   
...           ...   ...     ...     ...           ...      ...          ...   
391875  Santaquin   SAQ     z23  1007.0  490572112021    SAQ_d     0.000000   
391876  Santaquin   SAQ     z23  1007.5  490572112022    SAQ_d     0.000000   
391877  Santaquin   SAQ     z23  1008.0  490572112023    SAQ_d     0.000372   
391878  Santaquin   SAQ     z23  1008.5  490572112024    SAQ_d     0.000000   
391879  Santaquin   SAQ     z23  1009.0  490572112025    SAQ_d     0.000000   

       CATEGORY  
0            _o  
1            _o  
2            _o  
3            _o  
4            _o  
...         ...  
391875       _d  
391876       _d  
391877       _d  
391878       _d  
391879       _d  

[391880 rows x 8 columns]

zCOFIPS_wCat         z03_d         z03_o          z11_d          z11_o  \
GEOID                                                                    
490011001001      0.003915      0.000000       0.534147       0.479252   
490011001002      0.088865      0.000000       0.148768       0.162878   
490011001003      0.000018      0.000000       0.112818       0.096642   
490011002001      0.000000      0.000000       0.000000       0.030240   
490011002002      0.000000      0.000000       0.000000       0.000000   
...                    ...           ...            ...            ...   
490572112022      0.827552      0.750548      98.977844     107.636139   
490572112023      0.200167      0.469871     139.826803     124.181867   
490572112024      1.075733      5.591411      49.249169      54.341762   
490572112025      3.982297      3.754500     350.519668     321.197959   
colSUM        12220.429052  12367.232242  182214.696600  182640.455243   

zCOFIPS_wCat        z23_d        z23_o        z29_d        z29_o  \
GEOID                                                              
490011001001     0.000000     0.000107     0.000000     0.000000   
490011001002     0.096708     0.273417     0.000000     0.000000   
490011001003     0.088005     0.000037     0.000000     0.000000   
490011002001     0.000181     0.000000     0.000000     0.000000   
490011002002     0.092176     0.000000     0.000000     0.000000   
...                   ...          ...          ...          ...   
490572112022     0.000000     0.000000     1.632154     1.961265   
490572112023     0.000372     0.000372     0.094510     0.234539   
490572112024     0.000000     0.000000     0.886773     1.571712   
490572112025     0.000000     0.000000     9.924310    10.937395   
colSUM        3532.200431  3855.754943  1597.056607  1620.540991   

zCOFIPS_wCat          z35_d          z35_o         z43_d         z43_o  \
GEOID                                                                    
490011001001       0.475007       0.399094  0.000000e+00  0.000000e+00   
490011001002       0.640374       0.421008  0.000000e+00  0.000000e+00   
490011001003       1.597659       0.950280  0.000000e+00  0.000000e+00   
490011002001       0.092357       0.476221  0.000000e+00  0.000000e+00   
490011002002       0.000000       0.170104  0.000000e+00  0.000000e+00   
...                     ...            ...           ...           ...   
490572112022      35.507995      33.167402  7.512855e-03  1.914985e-03   
490572112023      10.569544      11.201859  6.555996e-01  3.702644e-01   
490572112024      12.076661      10.396795  3.161155e-08  1.569590e-08   
490572112025      45.058153      48.389312  2.698365e-01  6.818835e-02   
colSUM        500573.996022  486874.622706  7.498754e+03  7.303340e+03   

zCOFIPS_wCat         z45_d         z45_o          z49_d          z49_o  \
GEOID                                                                    
490011001001  1.211254e-03      0.000000       0.594823       0.384696   
490011001002  5.172937e-07      0.204020       0.555480       0.733805   
490011001003  1.286816e-01      0.185661       0.635046       3.067724   
490011002001  0.000000e+00      0.000000       0.041463       0.000467   
490011002002  0.000000e+00      0.000000       0.000000       0.236247   
...                    ...           ...            ...            ...   
490572112022  1.396070e-01      0.175104       0.581036       0.153695   
490572112023  0.000000e+00      0.091835       1.067916       1.992787   
490572112024  2.032503e-02      0.024662       0.220203       0.121228   
490572112025  2.419223e+00      3.139723       0.183630       0.348688   
colSUM        2.069473e+04  21250.747571  240642.445233  240489.847844   

zCOFIPS_wCat        z51_d         z51_o          z57_d          z57_o  
GEOID                                                                  
490011001001     0.000000  2.770124e-01       0.287607       0.755224  
4900110010

In [15]:
#add county columns to original dataset
df_SLCommutePatternsWCounty = pd.DataFrame.merge(df_SLCommutePatterns, df_SLCommutePatterns_CountyTotals, on='GEOID')
df_SLCommutePatterns = df_SLCommutePatternsWCounty

df_SLCommutePatterns

fakeid         GEOID         AFK_o       ALA_o        ALP_o  \
0        0.0        colSUM  19321.473353  523.841860  2604.511849   
1        0.0  490011001001      0.000000    0.000000     0.000257   
2        0.5  490011001002      0.000000    0.000000     0.000011   
3        1.0  490011001003      0.000000    0.000000     0.004286   
4        1.5  490011002001      0.000000    0.000000     0.000000   
...      ...           ...           ...         ...          ...   
2015  1007.0  490572112021      0.000000    0.000000     0.000000   
2016  1007.5  490572112022      0.000000    0.003945     0.000000   
2017  1008.0  490572112023      0.000000    0.000000     0.000000   
2018  1008.5  490572112024      0.000000    0.000000     0.000000   
2019  1009.0  490572112025      0.000304    0.141115     0.000000   

            BDL_o        BGM_o         BNT_o       BRT_o       CDF_o  ...  \
0     8266.938860  7458.342444  18275.317561  253.510936  203.458137  ...   
1        0.000000     0.000000      0.090484    0.000000    0.000000  ...   
2        0.000000     0.000000      0.020942    0.000000    0.000000  ...   
3        0.000000     0.000000      0.070895    0.000000    0.000000  ...   
4        0.030068     0.000000      0.000000    0.000000    0.000000  ...   
...           ...          ...           ...         ...         ...  ...   
2015     0.000000     0.707739      1.469189    0.000000    0.000000  ...   
2016     0.000029     0.722970      4.057913    0.000042    0.000027  ...   
2017     0.004723     0.295544      1.471707    0.000000    0.000000  ...   
2018     0.000000     0.337605      1.772527    0.000000    0.000000  ...   
2019     0.001051     0.356567      3.674272    0.001489    0.000003  ...   

             z43_d         z43_o         z45_d         z45_o          z49_d  \
0     7.498754e+03  7.303340e+03  2.069473e+04  21250.747571  240642.445233   
1     0.000000e+00  0.000000e+00  1.211254e-03      0.000000       0.594823   
2     0.000000e+00  0.000000e+00  5.172937e-07      0.204020       0.555480   
3     0.000000e+00  0.000000e+00  1.286816e-01      0.185661       0.635046   
4     0.000000e+00  0.000000e+00  0.000000e+00      0.000000       0.041463   
...            ...           ...           ...           ...            ...   
2015  0.000000e+00  0.000000e+00  2.818853e-05      0.000034       0.261782   
2016  7.512855e-03  1.914985e-03  1.396070e-01      0.175104       0.581036   
2017  6.555996e-01  3.702644e-01  0.000000e+00      0.091835       1.067916   
2018  3.161155e-08  1.569590e-08  2.032503e-02      0.024662       0.220203   
2019  2.698365e-01  6.818835e-02  2.419223e+00      3.139723       0.183630   

              z49_o        z51_d         z51_o          z57_d          z57_o  
0     240489.847844  9926.238295  1.024189e+04  115701.705183  115748.237583  
1          0.384696     0.000000  2.770124e-01       0.287607       0.755224  
2          0.733805     0.000000  0.000000e+00       0.150587       0.277037  
3          3.067724     0.000000  5.632197e-05       0.087222       0.000000  
4          0.000467     0.000000  3.169502e-07       0.000000       0.000000  
...             ...          ...           ...            ...            ...  
2015       0.253967     0.000002  1.335132e-01     341.075856     365.827074  
2016       0.153695     0.012609  1.506464e-02     411.250849     362.241415  
2017       1.992787     0.001115  7.433862e-04     208.528425     186.145289  
2018       0.121228     0.000000  1.731968e-02     247.661368     242.210634  
2019       0.348688     0.449289  5.388594e-01     435.359470     465.803583  

[2020 rows x 218 columns]

In [16]:
#remove UofU displaced block group
#superceeded by manual reallocation prior to data input prep
#
display(df_SLCommutePatterns[df_SLCommutePatterns['GEOID']=='490351108004'])

#
#df_SLCommutePatterns = df_SLCommutePatterns[df_SLCommutePatterns['GEOID'] != '490351108004']

#display(df_SLCommutePatterns[df_SLCommutePatterns['GEOID']=='490351108004'])

fakeid         GEOID     AFK_o     ALA_o   ALP_o     BDL_o     BGM_o  \
631   315.0  490351108004  6.021197  1.406079  0.2876  0.717715  0.469219   

        BNT_o    BRT_o     CDF_o  ...     z43_d     z43_o     z45_d     z45_o  \
631  3.482683  0.54317  0.000465  ...  0.095407  0.001233  0.595935  0.116303   

         z49_d      z49_o     z51_d     z51_o     z57_d     z57_o  
631  22.913372  25.319559  0.093681  0.093709  0.646418  2.171377  

[1 rows x 218 columns]

# Quick JSON export with some summary stats

In [17]:
#use row with "colSUM" as GEOID as total
df_SLCommutePatterns_ColSum = df_SLCommutePatterns[df_SLCommutePatterns['GEOID'] == 'colSUM']
df_SLCommutePatterns_ColSum

fakeid   GEOID         AFK_o      ALA_o        ALP_o       BDL_o  \
0     0.0  colSUM  19321.473353  523.84186  2604.511849  8266.93886   

         BGM_o         BNT_o       BRT_o       CDF_o  ...        z43_d  \
0  7458.342444  18275.317561  253.510936  203.458137  ...  7498.754345   

         z43_o         z45_d         z45_o          z49_d          z49_o  \
0  7303.340251  20694.734122  21250.747571  240642.445233  240489.847844   

         z51_d         z51_o          z57_d          z57_o  
0  9926.238295  10241.892995  115701.705183  115748.237583  

[1 rows x 218 columns]

In [18]:
#prepare area columns for json
df_people = df_SLCommutePatterns_ColSum.loc[:,'AFK_o':'z57_d'].T #transpose
df_people = df_people.reset_index()
df_people['CATEGORY'] = df_people['index'].str[3:5]
df_people['index']    = df_people['index'].str[:3]
df_people

index              0 CATEGORY
0     AFK   19321.473353       _o
1     ALA     523.841860       _o
2     ALP    2604.511849       _o
3     BDL    8266.938860       _o
4     BGM    7458.342444       _o
..    ...            ...      ...
210   z49  240642.445233       _d
211   z49  240489.847844       _o
212   z51    9926.238295       _d
213   z51   10241.892995       _o
214   z57  115701.705183       _d

[215 rows x 3 columns]

In [19]:
#prepare x columns
df_people_x = df_people[df_people['CATEGORY'] == '_o']
df_people_x.columns = ('CODE3','people_o','CATEGORY')

df_people_x['CODE3'] = df_people_x['CODE3'].str[:3]

df_people_x = df_people_x.drop_duplicates() #some duplicate columns in dataset
display(df_people_x)

#prepare y columns
df_people_y = df_people[df_people['CATEGORY'] == '_d']
df_people_y.columns = ('CODE3','people_d','CATEGORY')

df_people_y['CODE3'] = df_people_y['CODE3'].str[:3]

df_people_y = df_people_y.drop_duplicates() #some duplicate columns in dataset
display(df_people_y)

df_people_x = df_people_x.drop(['CATEGORY'], axis=1)
df_people_y = df_people_y.drop(['CATEGORY'], axis=1)

#combine city/township data with x and y
df_CityTownship_People = pd.DataFrame.merge(df_CityTownship_NameCode,df_people_x, on='CODE3', how='right')
df_CityTownship_People = pd.DataFrame.merge(df_CityTownship_People  ,df_people_y, on='CODE3', how='right')                                           


C:\Users\cday\AppData\Local\ESRI\conda\envs\arcgispro-py3-clone\lib\site-packages\ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """


CODE3       people_o CATEGORY
0     AFK   19321.473353       _o
1     ALA     523.841860       _o
2     ALP    2604.511849       _o
3     BDL    8266.938860       _o
4     BGM    7458.342444       _o
..    ...            ...      ...
205   z35  486874.622706       _o
207   z43    7303.340251       _o
209   z45   21250.747571       _o
211   z49  240489.847844       _o
213   z51   10241.892995       _o

[107 rows x 3 columns]

C:\Users\cday\AppData\Local\ESRI\conda\envs\arcgispro-py3-clone\lib\site-packages\ipykernel_launcher.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


CODE3       people_d CATEGORY
98    AFK   20402.297786       _d
99    ALA     561.397393       _d
100   ALP    2514.357129       _d
101   BDL    8498.143397       _d
102   BGM    7500.359599       _d
..    ...            ...      ...
206   z43    7498.754345       _d
208   z45   20694.734122       _d
210   z49  240642.445233       _d
212   z51    9926.238295       _d
214   z57  115701.705183       _d

[108 rows x 3 columns]

In [20]:
#define county dataframe
df_CoNames = sdf_CountiesAGRC[['zCOFIPS','CO_NAME']]

#prepare dataframe for export to JSON, combining city/township
df_CityTownship_Export = pd.DataFrame.merge(df_CityTownship_People, df_CoNames, left_on='CODE3', right_on='zCOFIPS', how='left')

#for any null values, replace with zero(0)
df_CityTownship_Export = df_CityTownship_Export.fillna(0)

#Get city/township name and county name into one field
df_CityTownship_Export.loc[df_CityTownship_Export.CO_NAME != 0, 'NAME'] = df_CityTownship_Export['CO_NAME']

#filter by only 4 columns for export
df_CityTownship_Export = df_CityTownship_Export[['NAME','CODE3','people_o','people_d']]

#change TTL (total) row to Counties subhead for correct positioning in dropdown

#don't include total row
df_CityTownship_Export = df_CityTownship_Export[df_CityTownship_Export['CODE3'] != 'TTL']

#df_CityTownship_Export.loc[((df_CityTownship_Export['CODE3'] == 'TTL')), 'NAME' ] = '---COUNTIES---'
#df_CityTownship_Export.loc[((df_CityTownship_Export['CODE3'] == 'TTL')), 'CODE3'] = 'y000'

#create a first letter field for sorting, to preserve COUNTIES with (z..) at bottom of sort, so can't use name as first sort
#df_CityTownship_Export['firstletter'] = df_CityTownship_Export['CODE3'].str[0:1]
#df_CityTownship_Export = df_CityTownship_Export.sort_values(by=['firstletter','NAME'])
df_CityTownship_Export = df_CityTownship_Export.sort_values(by=['NAME'])

#filter again by only 4 columns for export
df_CityTownship_Export = df_CityTownship_Export[['NAME','CODE3','people_o','people_d']]

#rename columns with 'label' and 'value' to work better in javascript dojo convention
df_CityTownship_Export.columns = ('label','value','people_o','people_d')

#let's see what we got!!
display(df_CityTownship_Export)
    
#export to JSON
df_CityTownship_Export.to_json(fname_CityTownshipJSON,orient='records')

label value      people_o      people_d
2             Alpine   ALP   2604.511849   2514.357129
1               Alta   ALA    523.841860    561.397393
0      American Fork   AFK  19321.473353  20402.297786
3          Bluffdale   BDL   8266.938860   8498.143397
5          Bountiful   BNT  18275.317561  18192.471673
..               ...   ...           ...           ...
95  West Valley City   WVC  53678.222795  56087.338119
90        White City   WHT   3621.257510   3557.872367
92           Willard   WIL   1511.696157   1492.720362
88    Woodland Hills   WDL    479.936375    397.172954
96       Woods Cross   WXC   6269.603179   6244.375235

[107 rows x 4 columns]

# Update ColCodes with Counties for summing

In [21]:
#get all column codes for summing
dfColCodesWCounty = df_SLCommutePatterns.loc[1:1,'AFK_o':'z57_d'].T
dfColCodesWCounty = dfColCodesWCounty.reset_index()
dColCodesWCounty = dfColCodesWCounty['index'].values.tolist()
dColCodesWCounty

['AFK_o',
 'ALA_o',
 'ALP_o',
 'BDL_o',
 'BGM_o',
 'BNT_o',
 'BRT_o',
 'CDF_o',
 'CEN_o',
 'CHA_o',
 'CHL_o',
 'CLF_o',
 'CLI_o',
 'CMT_o',
 'COA_o',
 'CWH_o',
 'DAN_o',
 'DRA_o',
 'EAG_o',
 'ELK_o',
 'EMT_o',
 'FAR_o',
 'FCS_o',
 'FFD_o',
 'FRR_o',
 'FTH_o',
 'GLA_o',
 'GOS_o',
 'GRL_o',
 'HAR_o',
 'HDT_o',
 'HEB_o',
 'HER_o',
 'HGH_o',
 'HNF_o',
 'HOL_o',
 'HOO_o',
 'HVL_o',
 'IND_o',
 'INT_o',
 'KAY_o',
 'KMS_o',
 'KMT_o',
 'LAY_o',
 'LEH_o',
 'LIN_o',
 'MAP_o',
 'MID_o',
 'MLC_o',
 'MMT_o',
 'MRG_o',
 'MSL_o',
 'MUR_o',
 'MWY_o',
 'NOG_o',
 'NSL_o',
 'OGD_o',
 'OKL_o',
 'ORM_o',
 'PAY_o',
 'PGR_o',
 'PLN_o',
 'PRK_o',
 'PRY_o',
 'PVO_o',
 'PVW_o',
 'ROY_o',
 'RVD_o',
 'RVT_o',
 'SAN_o',
 'SAQ_o',
 'SAR_o',
 'SFK_o',
 'SJC_o',
 'SLC_o',
 'SLM_o',
 'SOG_o',
 'SPV_o',
 'SSL_o',
 'SUN_o',
 'SWE_o',
 'SYR_o',
 'TAY_o',
 'TOO_o',
 'UIN_o',
 'VIN_o',
 'WAT_o',
 'WBG_o',
 'WDL_o',
 'WEB_o',
 'WHT_o',
 'WHV_o',
 'WIL_o',
 'WJC_o',
 'WPT_o',
 'WVC_o',
 'WXC_o',
 'TTL_o',
 'AFK_d',
 'ALA_d',


# Add Unincorporated County Areas to Cities/Townships

In [22]:
#filter county dataset with only what we want
sdf_CountiesWCodes = sdf_CountiesAGRC[['zCOFIPS','CO_NAME','SHAPE']]
sdf_CountiesWCodes.columns = ('CODE3','FIRST_NAME','SHAPE')
display(sdf_CountiesWCodes)

#export a couple county spatial dataframes
sdf_CountiesWCodes.spatial.to_featureclass(fname_CountyWCodes_shp, sanitize_columns=False) #as shapefile for future use
sdf_CountiesWCodes.spatial.to_featureclass(fname_Counties, sanitize_columns=False) #for gdb for use in web app

CODE3         FIRST_NAME                                              SHAPE
0    z05       Cache County  {"rings": [[[-112.15617197899996, 41.997725941...
1    z13    Duchesne County  {"rings": [[[-110.25173670299995, 40.832347463...
2    z11       Davis County  {"rings": [[[-111.92092166399999, 41.138676415...
3    z27     Millard County  {"rings": [[[-112.23854898599996, 39.553633436...
4    z51     Wasatch County  {"rings": [[[-111.39572506599995, 40.690187842...
5    z03   Box Elder County  {"rings": [[[-113.47488592699995, 41.993309448...
6    z57       Weber County  {"rings": [[[-111.92092166399999, 41.138676415...
7    z23        Juab County  {"rings": [[[-112.17814760399995, 40.011304953...
8    z39     Sanpete County  {"rings": [[[-111.60347983999998, 39.812889279...
9    z53  Washington County  {"rings": [[[-113.47458777999998, 37.607168207...
10   z19       Grand County  {"rings": [[[-109.05510868899995, 39.498702060...
11   z33        Rich County  {"rings": [[[-111.04672602399995, 42.001708362...
12   z07      Carbon County  {"rings": [[[-111.05121454599998, 39.814071497...
13   z09     Daggett County  {"rings": [[[-109.05002513499994, 40.999895250...
14   z01      Beaver County  {"rings": [[[-112.51540546399997, 38.572850827...
15   z41      Sevier County  {"rings": [[[-111.84900514399999, 39.044355246...
16   z17    Garfield County  {"rings": [[[-112.26560199199997, 38.149879660...
17   z45      Tooele County  {"rings": [[[-112.44788691599996, 41.017030151...
18   z43      Summit County  {"rings": [[[-109.99967939799996, 40.997456621...
19   z31       Piute County  {"rings": [[[-112.33023683099998, 38.510834361...
20   z47      Uintah County  {"rings": [[[-109.04897471299995, 40.662656164...
21   z21        Iron County  {"rings": [[[-113.36588561299999, 38.148691452...
22   z15       Emery County  {"rings": [[[-111.24394073999997, 39.703588004...
23   z55       Wayne County  {"rings": [[[-111.70753983999998, 38.510152783...
24   z37    San Juan County  {"rings": [[[-109.77115733799997, 36.998238968...
25   z29      Morgan County  {"rings": [[[-111.51438719299995, 40.803633660...
26   z25        Kane County  {"rings": [[[-111.84536734499994, 37.535799155...
27   z35   Salt Lake County  {"rings": [[[-111.96851544299994, 40.871938834...
28   z49        Utah County  {"rings": [[[-111.59404929699997, 40.577075300...

C:\Users\cday\AppData\Local\ESRI\conda\envs\arcgispro-py3-clone\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\SL\\SLCommutePatterns.gdb\\Counties'

In [23]:
deleteIfExists(fname_CityTownshipWCodesUnionCounty_shp)

print ("Unioning city/township with county...")

#intersection parcels with analysis area types
arcpy.analysis.Union([fname_CityTownshipWCodes,fname_CountyWCodes_shp], fname_CityTownshipWCodesUnionCounty_shp)

sdf_CityTownshipWCodesCounty = pd.DataFrame.spatial.from_featureclass(fname_CityTownshipWCodesUnionCounty_shp)
sdf_CityTownshipWCodesCounty = sdf_CityTownshipWCodesCounty.rename(columns={"code3":"CODE3", "FIRST_name":"FIRST_NAME", "FIRST_coun":"FIRST_COUN", "first_na_1":"FIRST_NA_1", "code3_1":"CODE3_1"})
sdf_CityTownshipWCodesCounty

Unioning city/township with county...


FID  FID_Munici CODE3        FIRST_NAME FIRST_COUN  Shape_Leng  \
0      0          -1                                       0.000000   
1      1          -1                                       0.000000   
2      2          -1                                       0.000000   
3      3          -1                                       0.000000   
4      4          -1                                       0.000000   
..   ...         ...   ...               ...        ...         ...   
154  154          75   SLC    Salt Lake City         18    1.346029   
155  155          50   MMT             Magna         18    0.756349   
156  156          96   WVC  West Valley City         18    0.614523   
157  157          70   SAN             Sandy         18    1.239008   
158  158          91   WHT        White City         18    0.147366   

     Shape_Area  FID_Counti  Id CODE3_1        FIRST_NA_1  \
0      0.000000           0   0     z05      Cache County   
1      0.000000           1   0     z13   Duchesne County   
2      0.000000           2   0     z11      Davis County   
3      0.000000           3   0     z27    Millard County   
4      0.000000           4   0     z51    Wasatch County   
..          ...         ...  ..     ...               ...   
154    0.030613          27   0     z35  Salt Lake County   
155    0.010342          27   0     z35  Salt Lake County   
156    0.009884          27   0     z35  Salt Lake County   
157    0.006653          27   0     z35  Salt Lake County   
158    0.000241          27   0     z35  Salt Lake County   

                                                 SHAPE  
0    {"rings": [[[-111.50779761699998, 41.999560240...  
1    {"rings": [[[-109.99900220099995, 40.813577918...  
2    {"rings": [[[-112.10299823793908, 41.152736052...  
3    {"rings": [[[-112.01601400799998, 39.314566632...  
4    {"rings": [[[-111.38703771390648, 40.657177632...  
..                                                 ...  
154  {"rings": [[[-112.10123724564913, 40.775409823...  
155  {"rings": [[[-112.06310238736523, 40.703812554...  
156  {"rings": [[[-112.06310238736523, 40.703812554...  
157  {"rings": [[[-111.86188875086515, 40.580804996...  
158  {"rings": [[[-111.86188875086515, 40.580804996...  

[159 rows x 12 columns]

In [24]:
sdf_CityTownshipWCodesCounty.loc[((sdf_CityTownshipWCodesCounty['FID_Munici'] == -1)), 'CODE3'     ] = sdf_CityTownshipWCodesCounty['CODE3_1'   ]
sdf_CityTownshipWCodesCounty.loc[((sdf_CityTownshipWCodesCounty['FID_Munici'] == -1)), 'FIRST_NAME'] = sdf_CityTownshipWCodesCounty['FIRST_NA_1'] + ' Unincorporated'

sdf_CityTownshipWCodesCounty = sdf_CityTownshipWCodesCounty[['FID_Munici','CODE3','FIRST_NAME','SHAPE']]

sdf_CityTownshipWCodesCounty.spatial.to_featureclass(fname_CityTownshipCountyWCodes_shp, sanitize_columns=False)
sdf_CityTownshipWCodesCounty

C:\Users\cday\AppData\Local\ESRI\conda\envs\arcgispro-py3-clone\lib\site-packages\pandas\core\indexing.py:1720: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self._setitem_single_column(loc, value, pi)


FID_Munici CODE3                      FIRST_NAME  \
0            -1   z05     Cache County Unincorporated   
1            -1   z13  Duchesne County Unincorporated   
2            -1   z11     Davis County Unincorporated   
3            -1   z27   Millard County Unincorporated   
4            -1   z51   Wasatch County Unincorporated   
..          ...   ...                             ...   
154          75   SLC                  Salt Lake City   
155          50   MMT                           Magna   
156          96   WVC                West Valley City   
157          70   SAN                           Sandy   
158          91   WHT                      White City   

                                                 SHAPE  
0    {"rings": [[[-111.50779761699998, 41.999560240...  
1    {"rings": [[[-109.99900220099995, 40.813577918...  
2    {"rings": [[[-112.10299823793908, 41.152736052...  
3    {"rings": [[[-112.01601400799998, 39.314566632...  
4    {"rings": [[[-111.38703771390648, 40.657177632...  
..                                                 ...  
154  {"rings": [[[-112.10123724564913, 40.775409823...  
155  {"rings": [[[-112.06310238736523, 40.703812554...  
156  {"rings": [[[-112.06310238736523, 40.703812554...  
157  {"rings": [[[-111.86188875086515, 40.580804996...  
158  {"rings": [[[-111.86188875086515, 40.580804996...  

[159 rows x 4 columns]

# Calculate Percent

In [25]:
#read block group shapefile
sdf_BlockGroups = pd.DataFrame.spatial.from_featureclass(fname_BlockGroups_shp)
sdf_SLCommutePatterns = pd.DataFrame.merge(sdf_BlockGroups, df_SLCommutePatterns, on='GEOID')
display(sdf_BlockGroups)

FID STATEFP COUNTYFP TRACTCE  DISTSML BLKGRPCE         GEOID  \
0        0      49      035  111306     75.0        1  490351113061   
1        1      49      035  111306     75.0        2  490351113062   
2        2      49      035  111400     47.0        1  490351114001   
3        3      49      035  111400     56.0        2  490351114002   
4        4      49      035  111400     56.0        3  490351114003   
...    ...     ...      ...     ...      ...      ...           ...   
2015  2015      49      057  200900     16.0        2  490572009002   
2016  2016      49      057  201200     15.0        1  490572012001   
2017  2017      49      057  201200     15.0        2  490572012002   
2018  2018      49      057  201301     16.0        2  490572013012   
2019  2019      49      057  201301     16.0        1  490572013011   

           NAMELSAD  MTFCC FUNCSTAT     ALAND  AWATER     INTPTLAT  \
0     Block Group 1  G5030        S  877837.0     0.0  +40.6094422   
1     Block Group 2  G5030        S  653262.0     0.0  +40.6068923   
2     Block Group 1  G5030        S  381555.0     0.0  +40.7219003   
3     Block Group 2  G5030        S  308108.0     0.0  +40.7155063   
4     Block Group 3  G5030        S  422651.0     0.0  +40.7087113   
...             ...    ...      ...       ...     ...          ...   
2015  Block Group 2  G5030        S  347700.0     0.0  +41.2248269   
2016  Block Group 1  G5030        S  752190.0     0.0  +41.2121869   
2017  Block Group 2  G5030        S  437903.0     0.0  +41.2123035   
2018  Block Group 2  G5030        S  326205.0     0.0  +41.2163706   
2019  Block Group 1  G5030        S  432925.0     0.0  +41.2162428   

          INTPTLON  CENTROID_X  CENTROID_Y     BGAcres  \
0     -111.8259365 -111.825937   40.609442  216.771411   
1     -111.8144187 -111.814419   40.606892  161.314487   
2     -111.8796932 -111.879693   40.721900   94.222093   
3     -111.8797286 -111.879729   40.715506   76.084072   
4     -111.8797335 -111.879733   40.708711  104.369581   
...            ...         ...         ...         ...   
2015  -111.9636889 -111.963689   41.224827   85.863927   
2016  -111.9783667 -111.978367   41.212187  185.752109   
2017  -111.9706612 -111.970661   41.212304  108.139051   
2018  -111.9635764 -111.963576   41.216371   80.555404   
2019  -111.9538634 -111.953863   41.216243  106.909485   

                                                  SHAPE  
0     {"rings": [[[429468.0213051503, 4496405.233871...  
1     {"rings": [[[430494.91099986027, 4495540.43917...  
2     {"rings": [[[425457.5579433697, 4507873.987348...  
3     {"rings": [[[425448.36375707807, 4507253.27157...  
4     {"rings": [[[425435.2029181655, 4506380.698648...  
...                                                 ...  
2015  {"rings": [[[418807.4658959587, 4564213.682993...  
2016  {"rings": [[[417490.98019006505, 4562356.17136...  
2017  {"rings": [[[418380.1807087121, 4562347.716705...  
2018  {"rings": [[[418871.13447070273, 4563020.29370...  
2019  {"rings": [[[419571.11778565514, 4563028.08038...  

[2020 rows x 18 columns]

In [26]:
pd.set_option('display.max_columns', None)
df_SLCommutePatterns.loc[1:,'AFK_o':]

AFK_o     ALA_o     ALP_o     BDL_o     BGM_o     BNT_o     BRT_o  \
1     0.000000  0.000000  0.000257  0.000000  0.000000  0.090484  0.000000   
2     0.000000  0.000000  0.000011  0.000000  0.000000  0.020942  0.000000   
3     0.000000  0.000000  0.004286  0.000000  0.000000  0.070895  0.000000   
4     0.000000  0.000000  0.000000  0.030068  0.000000  0.000000  0.000000   
5     0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
...        ...       ...       ...       ...       ...       ...       ...   
2015  0.000000  0.000000  0.000000  0.000000  0.707739  1.469189  0.000000   
2016  0.000000  0.003945  0.000000  0.000029  0.722970  4.057913  0.000042   
2017  0.000000  0.000000  0.000000  0.004723  0.295544  1.471707  0.000000   
2018  0.000000  0.000000  0.000000  0.000000  0.337605  1.772527  0.000000   
2019  0.000304  0.141115  0.000000  0.001051  0.356567  3.674272  0.001489   

         CDF_o     CEN_o         CHA_o  CHL_o      CLF_o      CLI_o     CMT_o  \
1     0.000000  0.000000  0.000000e+00    0.0   0.109435   0.000004  0.000000   
2     0.000000  0.000000  0.000000e+00    0.0   0.075209   0.000000  0.000000   
3     0.000000  0.000000  0.000000e+00    0.0   0.000000   0.000000  0.000000   
4     0.000000  0.000000  0.000000e+00    0.0   0.000171   0.000000  0.000000   
5     0.000000  0.000000  0.000000e+00    0.0   0.000000   0.000000  0.000000   
...        ...       ...           ...    ...        ...        ...       ...   
2015  0.000000  1.203822  4.639387e-07    0.0   9.299255  12.898820  0.000000   
2016  0.000027  0.290676  3.763200e-08    0.0  19.681726   4.185575  0.000000   
2017  0.000000  0.152344  0.000000e+00    0.0  19.136311   4.682718  0.000002   
2018  0.000000  0.221432  6.018426e-08    0.0   9.817794   2.890089  0.000000   
2019  0.000003  2.117892  1.346101e-06    0.0  41.277369  23.686467  0.000000   

         COA_o     CWH_o     DAN_o     DRA_o         EAG_o     ELK_o  \
1     0.000000  0.000000  0.000000  0.005516  0.000000e+00  0.001663   
2     0.000000  0.000000  0.000000  0.066844  0.000000e+00  0.000069   
3     0.000000  0.000000  0.000000  0.145306  0.000000e+00  0.027759   
4     0.000000  0.000000  0.000000  0.000004  9.462107e-07  0.000000   
5     0.000000  0.000000  0.000000  0.000000  0.000000e+00  0.000000   
...        ...       ...       ...       ...           ...       ...   
2015  0.000000  0.066765  0.066755  0.060859  1.215142e-01  0.000000   
2016  0.000000  0.098751  0.000000  0.226183  5.883515e-05  0.000000   
2017  0.000234  0.000848  0.000372  0.805934  0.000000e+00  0.000000   
2018  0.000000  0.033807  0.008660  0.092855  6.310917e-02  0.000000   
2019  0.000148  0.343757  0.000006  0.323684  1.178887e-05  0.000000   

             EMT_o     FAR_o         FCS_o  FFD_o     FRR_o     FTH_o  \
1     0.000000e+00  0.092357  0.000000e+00    0.0  0.000000  0.000000   
2     0.000000e+00  0.000037  0.000000e+00    0.0  0.000000  0.000000   
3     0.000000e+00  0.000014  0.000000e+00    0.0  0.000000  0.000000   
4     0.000000e+00  0.000000  0.000000e+00    0.0  0.000000  0.000000   
5     0.000000e+00  0.000000  0.000000e+00    0.0  0.000000  0.000000   
...            ...       ...           ...    ...       ...       ...   
2015  0.000000e+00  7.454653  0.000000e+00    0.0  2.861549  0.273476   
2016  8.764125e-08  5.927967  4.782054e-08    0.0  2.101352  0.243675   
2017  6.536512e-08  9.573085  0.000000e+00    0.0  0.347175  1.244274   
2018  0.000000e+00  5.357735  0.000000e+00    0.0  1.803734  0.152200   
2019  3.112299e-06  6.148050  1.710496e-06    0.0  3.509323  0.947172   

         GLA_o  GOS_o         GRL_o     HAR_o         HDT_o         HEB_o  \
1     0.000105    0.0  0.000000e+00  0.000000  9.233732e-02  9.233732e-02   
2     0.175336    0.0  1.450618e-01  0.000000  0.000000e+00  0.000000e+00   
3     0.000037    0.0  1.320082e-01  0.000000  1.877396e-05  1.877396e-05   
4     0.000000    0.0  0.000000e+00  0.000000  1.

In [27]:
sdf_SLCommutePatterns

FID STATEFP COUNTYFP TRACTCE  DISTSML BLKGRPCE         GEOID  \
0        0      49      035  111306     75.0        1  490351113061   
1        1      49      035  111306     75.0        2  490351113062   
2        2      49      035  111400     47.0        1  490351114001   
3        3      49      035  111400     56.0        2  490351114002   
4        4      49      035  111400     56.0        3  490351114003   
...    ...     ...      ...     ...      ...      ...           ...   
2014  2015      49      057  200900     16.0        2  490572009002   
2015  2016      49      057  201200     15.0        1  490572012001   
2016  2017      49      057  201200     15.0        2  490572012002   
2017  2018      49      057  201301     16.0        2  490572013012   
2018  2019      49      057  201301     16.0        1  490572013011   

           NAMELSAD  MTFCC FUNCSTAT     ALAND  AWATER     INTPTLAT  \
0     Block Group 1  G5030        S  877837.0     0.0  +40.6094422   
1     Block Group 2  G5030        S  653262.0     0.0  +40.6068923   
2     Block Group 1  G5030        S  381555.0     0.0  +40.7219003   
3     Block Group 2  G5030        S  308108.0     0.0  +40.7155063   
4     Block Group 3  G5030        S  422651.0     0.0  +40.7087113   
...             ...    ...      ...       ...     ...          ...   
2014  Block Group 2  G5030        S  347700.0     0.0  +41.2248269   
2015  Block Group 1  G5030        S  752190.0     0.0  +41.2121869   
2016  Block Group 2  G5030        S  437903.0     0.0  +41.2123035   
2017  Block Group 2  G5030        S  326205.0     0.0  +41.2163706   
2018  Block Group 1  G5030        S  432925.0     0.0  +41.2162428   

          INTPTLON  CENTROID_X  CENTROID_Y     BGAcres  \
0     -111.8259365 -111.825937   40.609442  216.771411   
1     -111.8144187 -111.814419   40.606892  161.314487   
2     -111.8796932 -111.879693   40.721900   94.222093   
3     -111.8797286 -111.879729   40.715506   76.084072   
4     -111.8797335 -111.879733   40.708711  104.369581   
...            ...         ...         ...         ...   
2014  -111.9636889 -111.963689   41.224827   85.863927   
2015  -111.9783667 -111.978367   41.212187  185.752109   
2016  -111.9706612 -111.970661   41.212304  108.139051   
2017  -111.9635764 -111.963576   41.216371   80.555404   
2018  -111.9538634 -111.953863   41.216243  106.909485   

                                                  SHAPE  fakeid     AFK_o  \
0     {'rings': [[[429468.0213051503, 4496405.233871...   334.0  2.525157   
1     {'rings': [[[430494.91099986027, 4495540.43917...   334.5  0.085405   
2     {'rings': [[[425457.5579433697, 4507873.987348...   335.0  0.093099   
3     {'rings': [[[425448.36375707807, 4507253.27157...   335.5  0.000000   
4     {'rings': [[[425435.2029181655, 4506380.698648...   336.0  0.000871   
...                                                 ...     ...       ...   
2014  {'rings': [[[418807.4658959587, 4564213.682993...   943.5  0.074016   
2015  {'rings': [[[417490.98019006505, 4562356.17136...   945.5  0.000000   
2016  {'rings': [[[418380.1807087121, 4562347.716705...   946.0  0.000056   
2017  {'rings': [[[418871.13447070273, 4563020.29370...   947.0  0.000000   
2018  {'rings': [[[419571.11778565514, 4563028.08038...   946.5  0.000000   

             ALA_o         ALP_o     BDL_o     BGM_o     BNT_o         BRT_o  \
0     1.760730e+01  2.349950e-05  0.450531  0.000000  0.000704  4.542110e+00   
1     3.471416e-01  1.557094e-05  0.382356  0.000000  0.279684  1.582900e-01   
2     3.668585e-01  2.899146e-08  0.003307  0.001955  0.264861  3.668585e-01   
3     6.253149e-05  0.000000e+00  0.282998  0.092145  0.094257  6.252114e-05   
4     2.067668e-03  5.884806e-04  0.030444  0.092052  0.270309  1.962506e-03   
...            ...           ...       ...       ...       ...           ...   
2014  0.000000e+00  1.080807e-01  0.000821  0.729139  0.338937  0.000000e+00   
2015  0.000000e+00  1.160767e-04  0.000000  3.20039

In [28]:
df_SLCommutePatterns.iloc[0,2:218]

AFK_o     19321.473353
ALA_o        523.84186
ALP_o      2604.511849
BDL_o       8266.93886
BGM_o      7458.342444
             ...      
z49_o    240489.847844
z51_d      9926.238295
z51_o     10241.892995
z57_d    115701.705183
z57_o    115748.237583
Name: 0, Length: 216, dtype: object

In [29]:
#initialize Percent_SA distribution dataframe
df_SLCommutePatterns_Percent_SA = df_SLCommutePatterns

#divide columns AFK_x and after by first row (totals) and columns 2:218
df_SLCommutePatterns_Percent_SA.loc[1:,'AFK_o':] = df_SLCommutePatterns.loc[1:,'AFK_o':].div(df_SLCommutePatterns.iloc[0,2:218])
df_SLCommutePatterns_Percent_SA.loc[1:,'AFK_o':] = df_SLCommutePatterns.loc[1:,'AFK_o':] * 100
df_SLCommutePatterns_Percent_SA

fakeid         GEOID         AFK_o      ALA_o        ALP_o       BDL_o  \
0        0.0        colSUM  19321.473353  523.84186  2604.511849  8266.93886   
1        0.0  490011001001           0.0        0.0      0.00001         0.0   
2        0.5  490011001002           0.0        0.0          0.0         0.0   
3        1.0  490011001003           0.0        0.0     0.000165         0.0   
4        1.5  490011002001           0.0        0.0          0.0    0.000364   
...      ...           ...           ...        ...          ...         ...   
2015  1007.0  490572112021           0.0        0.0          0.0         0.0   
2016  1007.5  490572112022           0.0   0.000753          0.0         0.0   
2017  1008.0  490572112023           0.0        0.0          0.0    0.000057   
2018  1008.5  490572112024           0.0        0.0          0.0         0.0   
2019  1009.0  490572112025      0.000002   0.026938          0.0    0.000013   

            BGM_o         BNT_o       BRT_o       CDF_o        CEN_o  \
0     7458.342444  18275.317561  253.510936  203.458137  5952.214861   
1             0.0      0.000495         0.0         0.0          0.0   
2             0.0      0.000115         0.0         0.0          0.0   
3             0.0      0.000388         0.0         0.0          0.0   
4             0.0           0.0         0.0         0.0          0.0   
...           ...           ...         ...         ...          ...   
2015     0.009489      0.008039         0.0         0.0     0.020225   
2016     0.009693      0.022204    0.000016    0.000013     0.004883   
2017     0.003963      0.008053         0.0         0.0     0.002559   
2018     0.004527      0.009699         0.0         0.0      0.00372   
2019     0.004781      0.020105    0.000588    0.000002     0.035582   

           CHA_o        CHL_o         CLF_o        CLI_o       CMT_o  \
0     499.575395  3776.864189  25389.854474  8962.938187  466.569589   
1            0.0          0.0      0.000431          0.0         0.0   
2            0.0          0.0      0.000296          0.0         0.0   
3            0.0          0.0           0.0          0.0         0.0   
4            0.0          0.0      0.000001          0.0         0.0   
...          ...          ...           ...          ...         ...   
2015         0.0          0.0      0.036626     0.143913         0.0   
2016         0.0          0.0      0.077518     0.046699         0.0   
2017         0.0          0.0       0.07537     0.052245    0.000001   
2018         0.0          0.0      0.038668     0.032245         0.0   
2019         0.0          0.0      0.162574     0.264271         0.0   

          COA_o         CWH_o       DAN_o         DRA_o         EAG_o  \
0     650.39774  11919.721509  809.028142  29047.052891  11138.542663   
1           0.0           0.0         0.0      0.000019           0.0   
2           0.0           0.0         0.0       0.00023           0.0   
3           0.0           0.0         0.0        0.0005           0.0   
4           0.0           0.0         0.0           0.0           0.0   
...         ...           ...         ...           ...           ...   
2015        0.0       0.00056    0.008251       0.00021      0.001091   
2016        0.0      0.000828         0.0      0.000779      0.000001   
2017   0.000036      0.000007    0.000046      0.002775           0.0   
2018        0.0      0.000284     0.00107       0.00032      0.000567   
2019   0.000023      0.002884    0.000001      0.001114           0.0   

            ELK_o      EMT_o       FAR_o       FCS_o       FFD_o        FRR_o  \
0     1090.700184  265.93917  9816.12987  926.243146  125.510335  4217.509196   
1        0.000152        0.0    0.000941         0.0         0.0          0.0   
2        0.000006        0.0         0.0         0.0         0.0          0.0   
3        0.002545        0.0         0.0         0.0         0.0          0.0   
4             0.0        0.0     

In [30]:
sdf_BlockGroups = pd.DataFrame.spatial.from_featureclass(fname_BlockGroups_shp)
sdf_SLCommutePatterns_Percent_SA = pd.DataFrame.merge(sdf_BlockGroups, df_SLCommutePatterns_Percent_SA, on='GEOID')
sdf_SLCommutePatterns_Percent_SA

FID STATEFP COUNTYFP TRACTCE  DISTSML BLKGRPCE         GEOID  \
0        0      49      035  111306     75.0        1  490351113061   
1        1      49      035  111306     75.0        2  490351113062   
2        2      49      035  111400     47.0        1  490351114001   
3        3      49      035  111400     56.0        2  490351114002   
4        4      49      035  111400     56.0        3  490351114003   
...    ...     ...      ...     ...      ...      ...           ...   
2014  2015      49      057  200900     16.0        2  490572009002   
2015  2016      49      057  201200     15.0        1  490572012001   
2016  2017      49      057  201200     15.0        2  490572012002   
2017  2018      49      057  201301     16.0        2  490572013012   
2018  2019      49      057  201301     16.0        1  490572013011   

           NAMELSAD  MTFCC FUNCSTAT     ALAND  AWATER     INTPTLAT  \
0     Block Group 1  G5030        S  877837.0     0.0  +40.6094422   
1     Block Group 2  G5030        S  653262.0     0.0  +40.6068923   
2     Block Group 1  G5030        S  381555.0     0.0  +40.7219003   
3     Block Group 2  G5030        S  308108.0     0.0  +40.7155063   
4     Block Group 3  G5030        S  422651.0     0.0  +40.7087113   
...             ...    ...      ...       ...     ...          ...   
2014  Block Group 2  G5030        S  347700.0     0.0  +41.2248269   
2015  Block Group 1  G5030        S  752190.0     0.0  +41.2121869   
2016  Block Group 2  G5030        S  437903.0     0.0  +41.2123035   
2017  Block Group 2  G5030        S  326205.0     0.0  +41.2163706   
2018  Block Group 1  G5030        S  432925.0     0.0  +41.2162428   

          INTPTLON  CENTROID_X  CENTROID_Y     BGAcres  \
0     -111.8259365 -111.825937   40.609442  216.771411   
1     -111.8144187 -111.814419   40.606892  161.314487   
2     -111.8796932 -111.879693   40.721900   94.222093   
3     -111.8797286 -111.879729   40.715506   76.084072   
4     -111.8797335 -111.879733   40.708711  104.369581   
...            ...         ...         ...         ...   
2014  -111.9636889 -111.963689   41.224827   85.863927   
2015  -111.9783667 -111.978367   41.212187  185.752109   
2016  -111.9706612 -111.970661   41.212304  108.139051   
2017  -111.9635764 -111.963576   41.216371   80.555404   
2018  -111.9538634 -111.953863   41.216243  106.909485   

                                                  SHAPE  fakeid     AFK_o  \
0     {'rings': [[[429468.0213051503, 4496405.233871...   334.0  0.013069   
1     {'rings': [[[430494.91099986027, 4495540.43917...   334.5  0.000442   
2     {'rings': [[[425457.5579433697, 4507873.987348...   335.0  0.000482   
3     {'rings': [[[425448.36375707807, 4507253.27157...   335.5       0.0   
4     {'rings': [[[425435.2029181655, 4506380.698648...   336.0  0.000005   
...                                                 ...     ...       ...   
2014  {'rings': [[[418807.4658959587, 4564213.682993...   943.5  0.000383   
2015  {'rings': [[[417490.98019006505, 4562356.17136...   945.5       0.0   
2016  {'rings': [[[418380.1807087121, 4562347.716705...   946.0       0.0   
2017  {'rings': [[[418871.13447070273, 4563020.29370...   947.0       0.0   
2018  {'rings': [[[419571.11778565514, 4563028.08038...   946.5       0.0   

         ALA_o     ALP_o     BDL_o     BGM_o     BNT_o     BRT_o CDF_o  \
0     3.361186  0.000001   0.00545       0.0  0.000004  1.791682   0.0   
1     0.066268  0.000001  0.004625       0.0   0.00153  0.062439   0.0   
2     0.070032       0.0   0.00004  0.000026  0.001449  0.144711   0.0   
3     0.000012       0.0  0.003423  0.001235  0.000516  0.000025   0.0   
4     0.000395  0.000023  0.000368  0.001234  0.001479  0.000774   0.0   
...        ...       ...       ...       ...       ...       ...   ...   
2014       0.0   0.00415   0.00001  0.009776  0.001855       0.0   0.0   
2015       0.0  0.000004       0.0   0.04291  0.002803       0.0   0.0   
2016       0.0       0.0 

In [31]:
sdf_SLCommutePatterns_Percent_SA.sum()

FID                                                   2037947
STATEFP     4949494949494949494949494949494949494949494949...
COUNTYFP    0350350350350350350350570350350350350570570570...
TRACTCE     1113061113061114001114001114001114001114002002...
DISTSML                                              163121.0
                                  ...                        
z49_o                                                   100.0
z51_d                                                   100.0
z51_o                                                   100.0
z57_d                                                   100.0
z57_o                                                   100.0
Length: 234, dtype: object

In [32]:
##create map centered on Salt Lake
##map_areas = gis.map('Salt Lake')
#
##define sdf layer
##sdf_SDCommutePatterns_Percent_SA.spatial.plot(map_widget = map_areas,
#                            renderer_type='s',
#                            cmap = 'RdPu',  # use a red to purple color map
#                            symbol_type='simple',
#                            outline_style='s',
#                            outline_color=[0,0,0,255],
#                            line_width=1.0)
#
##display map
#map_areas

In [33]:
#export to GDB
deleteIfExists(fname_BlockGroupsWCommutePatterns_Number)
sdf_SLCommutePatterns.spatial.to_featureclass(fname_BlockGroupsWCommutePatterns_Number, sanitize_columns=False)


'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\SL\\SLCommutePatterns.gdb\\SL_BlockGroup_CommutePatterns_Number'

In [34]:
deleteIfExists(fname_BlockGroupsWCommutePatterns_Percent_SA)
sdf_SLCommutePatterns_Percent_SA.spatial.to_featureclass(fname_BlockGroupsWCommutePatterns_Percent_SA, sanitize_columns=False)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\SL\\SLCommutePatterns.gdb\\SL_BlockGroup_CommutePatterns_Percent_SelectedArea'

# Group by Tract

In [35]:
#input filenames
fname_Tracts_shp = os.path.join(dirInput, 'Utah_Census_Tracts_2020' + r'\CensusTracts2020.shp')

In [36]:
#read tract shapefile
sdf_Tracts = pd.DataFrame.spatial.from_featureclass(fname_Tracts_shp)
sdf_Tracts

FID  OBJECTID STATEFP20 COUNTYFP20 TRACTCE20      GEOID20   NAME20  \
0      0         1        49        049    000901  49049000901     9.01   
1      1         2        49        049    002500  49049002500       25   
2      2         3        49        049    003401  49049003401    34.01   
3      3         4        49        049    010210  49049010210   102.10   
4      4         5        49        049    000505  49049000505     5.05   
..   ...       ...       ...        ...       ...          ...      ...   
711  711       712        49        035    111701  49035111701  1117.01   
712  712       713        49        035    111903  49035111903  1119.03   
713  713       714        49        035    111905  49035111905  1119.05   
714  714       715        49        035    113309  49035113309  1133.09   
715  715       716        49        015    976500  49015976500     9765   

       NAMELSAD20 MTFCC20 FUNCSTAT20       ALAND20    AWATER20   INTPTLAT20  \
0    Census Tract   G5020          S  1.686016e+06         0.0  +40.3051285   
1    Census Tract   G5020          S  1.034541e+06         0.0  +40.2296149   
2    Census Tract   G5020          S  9.085765e+06     23788.0  +40.0560227   
3    Census Tract   G5020          S  1.581048e+07         0.0  +40.4005884   
4    Census Tract   G5020          S  3.919712e+06         0.0  +40.3700595   
..            ...     ...        ...           ...         ...          ...   
711  Census Tract   G5020          S  1.358256e+06         0.0  +40.6934670   
712  Census Tract   G5020          S  2.072253e+06         0.0  +40.6806830   
713  Census Tract   G5020          S  1.167718e+06         0.0  +40.6765749   
714  Census Tract   G5020          S  1.867612e+06         0.0  +40.6881369   
715  Census Tract   G5020          S  8.782568e+09  14165655.0  +38.9311083   

       INTPTLON20     SHAPE_Leng    SHAPE_Area  \
0    -111.6922978    7129.054778  2.902253e+06   
1    -111.6497278    5588.845931  1.776891e+06   
2    -111.7122570   18878.825275  1.556674e+07   
3    -111.7306856   26101.425584  2.729233e+07   
4    -111.7070846   12562.893900  6.760193e+06   
..            ...            ...           ...   
711  -111.8826082    6277.757800  2.365082e+06   
712  -111.8627470    7592.371898  3.606962e+06   
713  -111.8744366    8615.733516  2.032283e+06   
714  -111.9693980    8501.284969  3.251486e+06   
715  -110.6644589  917894.696612  1.454313e+10   

                                                 SHAPE  
0    {"rings": [[[-12434548.4857, 4911361.749799997...  
1    {"rings": [[[-12429589.868, 4898990.177699998]...  
2    {"rings": [[[-12439397.559799999, 4872289.2984...  
3    {"rings": [[[-12442557.703499999, 4926512.4487...  
4    {"rings": [[[-12437368.7665, 4920654.352499999...  
..                                                 ...  
711  {"rings": [[[-12455347.0952, 4966754.840000004...  
712  {"rings": [[[-12453471.3611, 4964642.738300003...  
713  {"rings": [[[-12454528.1172, 4964343.751500003...  
714  {"rings": [[[-12465233.158599999, 4967696.3889...  
715  {"rings": [[[-12390649.8356, 4669994.337099999...  

[716 rows x 17 columns]

In [37]:
#calculate tract stats
df_SLCommutePatterns_tract = sdf_SLCommutePatterns.groupby(['STATEFP','COUNTYFP','TRACTCE'])[dColCodesWCounty].apply(lambda x : x.astype(int).sum())
df_SLCommutePatterns_tract = df_SLCommutePatterns_tract.reset_index()
display(df_SLCommutePatterns_tract)

#caclulate tract Percent_SA stats
df_SLCommutePatterns_Percent_SA_tract = sdf_SLCommutePatterns_Percent_SA.groupby(['STATEFP','COUNTYFP','TRACTCE'])[dColCodesWCounty].apply(lambda x : x.astype(float).sum())
df_SLCommutePatterns_Percent_SA_tract = df_SLCommutePatterns_Percent_SA_tract.reset_index()
display(df_SLCommutePatterns_Percent_SA_tract)


#df_test = df_SLCommutePatterns / df_SLCommutePatterns_ColSum

STATEFP COUNTYFP TRACTCE  AFK_o  ALA_o  ALP_o  BDL_o  BGM_o  BNT_o  BRT_o  \
0        49      001  100100      0      0      0      0      0      0      0   
1        49      001  100200      0      0      0      0      0      0      0   
2        49      003  960100      0      0      0      0     77      0      0   
3        49      003  960200      0      0      0      0    201      0      0   
4        49      003  960301      0      0      0      0     83      0      0   
..      ...      ...     ...    ...    ...    ...    ...    ...    ...    ...   
711      49      057  210900      0      0      0      8      6      6      0   
712      49      057  211000      0      0      0      0      0      1      0   
713      49      057  211100      0      0      0      0     15     12      0   
714      49      057  211201      2      0      0      0      3      5      0   
715      49      057  211202      0      0      0      0      0     10      0   

     CDF_o  CEN_o  CHA_o  CHL_o  CLF_o  CLI_o  CMT_o  COA_o  CWH_o  DAN_o  \
0        0      0      0      0      0      0      0      0      0      0   
1        0      0      0      0      0      0      0      0      0      0   
2        0      0      0      0     10      4      0      0      2      0   
3        0      0      0      0     16      0      0      0      0      0   
4        0      0      0      0      4      0      0      0      0      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
711      0      2      0      0    127     42      0      0      1      0   
712      0      0      0      0     32      7      0      0      0      0   
713      0      6      0      0     99     61      0      0      0      0   
714      0      1      0      0     89     10      0      1      1      0   
715      0      3      0      0     97     45      0      0      0      0   

     DRA_o  EAG_o  ELK_o  EMT_o  FAR_o  FCS_o  FFD_o  FRR_o  FTH_o  GLA_o  \
0        0      0      0      0      0      0      0      0      0      0   
1        0      0      0      0      0      0      0      0      0      0   
2        0      0      0      0      3      0      0      2      0      0   
3        5      0      0      0      0      0      0      8      0      0   
4        0      0      0      0      0      0      0      3      0      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
711      0      6      0      0     12      0      0     27      4      0   
712      0      0      0      0      4      0      0     15      1      0   
713      1      0      0      0     12      0      0     19      2      0   
714      1      0      0      0      8      0      0     13      8      0   
715      0      0      0      0     32      0      0      8      1      0   

     GOS_o  GRL_o  HAR_o  HDT_o  HEB_o  HER_o  HGH_o  HNF_o  HOL_o  HOO_o  \
0        0      0      0      0      0      0      0      0      0      0   
1        0      0      0      0      0      0      0      0      0      0   
2        0      0      7      0      0      0      0      0      0      2   
3        0      0     13      0      0      0      0      0      0      0   
4        0      0      1      0      0      0      0      0      0      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
711      0      0     38      0      0      0      0      0      0     21   
712      0      0     19      0      0      0      0      0      0      2   
713      0      0     26      0      0      0      0      0      0     68   
714      0      0     19      0      0      0      0      9      1     13   
715      0      0      9      0      0      0      0      0      0     18   

     HVL_o  IND_o  INT_o  KAY_o  KMS_o  KMT_o  LAY_o  LEH_o  LIN_o  MAP_o  \
0        0      0      0      0      0      0      0      0      0      0   
1        0      0      0      0      0      0      0      0      0      0   
2        5      0      0 

STATEFP COUNTYFP TRACTCE         AFK_o         ALA_o     ALP_o  \
0        49      001  100100  0.000000e+00  0.000000e+00  0.000175   
1        49      001  100200  0.000000e+00  0.000000e+00  0.000000   
2        49      003  960100  8.653800e-08  0.000000e+00  0.000000   
3        49      003  960200  2.074252e-08  4.741781e-06  0.000000   
4        49      003  960301  0.000000e+00  0.000000e+00  0.000000   
..      ...      ...     ...           ...           ...       ...   
711      49      057  210900  1.136667e-05  1.912162e-06  0.000015   
712      49      057  211000  2.047836e-04  0.000000e+00  0.003546   
713      49      057  211100  2.045731e-04  6.078907e-08  0.000000   
714      49      057  211201  1.227498e-02  1.125900e-05  0.000000   
715      49      057  211202  1.572907e-06  2.769152e-02  0.000000   

            BDL_o     BGM_o     BNT_o         BRT_o     CDF_o         CEN_o  \
0    0.000000e+00  0.000000  0.000998  0.000000e+00  0.000000  0.000000e+00   
1    1.117181e-03  0.000000  0.000000  0.000000e+00  0.000000  0.000000e+00   
2    0.000000e+00  1.050440  0.001021  0.000000e+00  0.000000  7.638602e-09   
3    1.143160e-03  2.743626  0.013652  9.798170e-06  0.000000  2.345971e-02   
4    0.000000e+00  1.141130  0.000071  0.000000e+00  0.000000  1.438366e-03   
..            ...       ...       ...           ...       ...           ...   
711  1.105610e-01  0.103693  0.049099  3.951192e-06  0.045378  6.096933e-02   
712  3.309191e-09  0.000152  0.013401  0.000000e+00  0.000000  9.422459e-03   
713  3.947389e-03  0.225976  0.079370  3.078461e-08  0.000000  1.660714e-01   
714  1.187306e-03  0.048713  0.036165  2.455483e-07  0.000000  3.475636e-02   
715  7.018876e-05  0.032453  0.068101  6.039264e-04  0.000015  6.696947e-02   

            CHA_o         CHL_o     CLF_o         CLI_o         CMT_o  \
0    0.000000e+00  0.000000e+00  0.000727  4.428195e-08  0.000000e+00   
1    0.000000e+00  0.000000e+00  0.000002  0.000000e+00  0.000000e+00   
2    0.000000e+00  4.444701e-07  0.044094  4.614786e-02  0.000000e+00   
3    0.000000e+00  0.000000e+00  0.070338  3.964599e-03  2.978508e-03   
4    0.000000e+00  0.000000e+00  0.020692  1.530081e-02  0.000000e+00   
..            ...           ...       ...           ...           ...   
711  5.628525e-12  0.000000e+00  0.515098  5.003939e-01  1.180965e-01   
712  1.939330e-05  0.000000e+00  0.132307  9.130714e-02  0.000000e+00   
713  1.213852e-07  0.000000e+00  0.403090  7.064673e-01  0.000000e+00   
714  1.126138e-10  0.000000e+00  0.356351  1.243738e-01  1.729853e-04   
715  3.818954e-07  0.000000e+00  0.390756  5.393730e-01  5.180706e-07   

            COA_o         CWH_o         DAN_o         DRA_o         EAG_o  \
0    0.000000e+00  0.000000e+00  0.000000e+00  7.493548e-04  0.000000e+00   
1    0.000000e+00  0.000000e+00  0.000000e+00  4.001598e-08  2.609258e-08   
2    0.000000e+00  2.000240e-02  0.000000e+00  1.275043e-03  0.000000e+00   
3    0.000000e+00  1.549648e-03  0.000000e+00  1.846045e-02  6.637784e-08   
4    0.000000e+00  5.294854e-10  0.000000e+00  3.179555e-04  8.290967e-04   
..            ...           ...           ...           ...           ...   
711  4.324591e-02  1.711032e-02  5.001007e-07  7.578755e-03  5.609633e-02   
712  4.547223e-09  7.754946e-04  6.415075e-12  5.826599e-04  0.000000e+00   
713  3.069984e-06  9.898588e-04  1.227237e-02  7.580140e-03  4.838261e-07   
714  1.917189e-01  1.071983e-02  0.000000e+00  6.658914e-03  0.000000e+00   
715  5.869966e-05  4.563253e-03  9.368332e-03  5.196792e-03  1.658152e-03   

        ELK_o     EMT_o     FAR_o         FCS_o  FFD_o     FRR_o     FTH_o  \
0    0.002704  0.000000  0.000941  0.000000e+00    0.0  0.000000  0.000000   
1    0.000000  0.000000  0.000000  0.000000e+00    0.0  0.000000  0.000000   
2    0.000000  0.000038  0.030905  0.000000e+00    0.0  0.074329  0.005852   
3    0.000000  0.000001  0.022408  0.000000e+00    0.0  0.229465  0.000186   
4    0.000000  0.00000

In [38]:
df_SLCommutePatterns_Percent_SA_tract.sum()

STATEFP     4949494949494949494949494949494949494949494949...
COUNTYFP    0010010030030030030030030030030030030030030050...
TRACTCE     1001001002009601009602009603019603029604009605...
AFK_o                                                   100.0
ALA_o                                                   100.0
                                  ...                        
z49_d                                                   100.0
z49_o                                                   100.0
z51_d                                                   100.0
z51_o                                                   100.0
z57_d                                                   100.0
Length: 218, dtype: object

In [39]:
sdf_SLCommutePatterns_tract = pd.DataFrame.merge(sdf_Tracts, df_SLCommutePatterns_tract, left_on=['STATEFP20','COUNTYFP20','TRACTCE20'], right_on=['STATEFP','COUNTYFP',"TRACTCE"])
display(sdf_SLCommutePatterns_tract)

sdf_SLCommutePatterns_Percent_SA_tract = pd.DataFrame.merge(sdf_Tracts, df_SLCommutePatterns_Percent_SA_tract, left_on=['STATEFP20','COUNTYFP20','TRACTCE20'], right_on=['STATEFP','COUNTYFP',"TRACTCE"])
display(sdf_SLCommutePatterns_Percent_SA_tract)

FID  OBJECTID STATEFP20 COUNTYFP20 TRACTCE20      GEOID20   NAME20  \
0      0         1        49        049    000901  49049000901     9.01   
1      1         2        49        049    002500  49049002500       25   
2      2         3        49        049    003401  49049003401    34.01   
3      3         4        49        049    010210  49049010210   102.10   
4      4         5        49        049    000505  49049000505     5.05   
..   ...       ...       ...        ...       ...          ...      ...   
711  711       712        49        035    111701  49035111701  1117.01   
712  712       713        49        035    111903  49035111903  1119.03   
713  713       714        49        035    111905  49035111905  1119.05   
714  714       715        49        035    113309  49035113309  1133.09   
715  715       716        49        015    976500  49015976500     9765   

       NAMELSAD20 MTFCC20 FUNCSTAT20       ALAND20    AWATER20   INTPTLAT20  \
0    Census Tract   G5020          S  1.686016e+06         0.0  +40.3051285   
1    Census Tract   G5020          S  1.034541e+06         0.0  +40.2296149   
2    Census Tract   G5020          S  9.085765e+06     23788.0  +40.0560227   
3    Census Tract   G5020          S  1.581048e+07         0.0  +40.4005884   
4    Census Tract   G5020          S  3.919712e+06         0.0  +40.3700595   
..            ...     ...        ...           ...         ...          ...   
711  Census Tract   G5020          S  1.358256e+06         0.0  +40.6934670   
712  Census Tract   G5020          S  2.072253e+06         0.0  +40.6806830   
713  Census Tract   G5020          S  1.167718e+06         0.0  +40.6765749   
714  Census Tract   G5020          S  1.867612e+06         0.0  +40.6881369   
715  Census Tract   G5020          S  8.782568e+09  14165655.0  +38.9311083   

       INTPTLON20     SHAPE_Leng    SHAPE_Area  \
0    -111.6922978    7129.054778  2.902253e+06   
1    -111.6497278    5588.845931  1.776891e+06   
2    -111.7122570   18878.825275  1.556674e+07   
3    -111.7306856   26101.425584  2.729233e+07   
4    -111.7070846   12562.893900  6.760193e+06   
..            ...            ...           ...   
711  -111.8826082    6277.757800  2.365082e+06   
712  -111.8627470    7592.371898  3.606962e+06   
713  -111.8744366    8615.733516  2.032283e+06   
714  -111.9693980    8501.284969  3.251486e+06   
715  -110.6644589  917894.696612  1.454313e+10   

                                                 SHAPE STATEFP COUNTYFP  \
0    {'rings': [[[-12434548.4857, 4911361.749799997...      49      049   
1    {'rings': [[[-12429589.868, 4898990.177699998]...      49      049   
2    {'rings': [[[-12439397.559799999, 4872289.2984...      49      049   
3    {'rings': [[[-12442557.703499999, 4926512.4487...      49      049   
4    {'rings': [[[-12437368.7665, 4920654.352499999...      49      049   
..                                                 ...     ...      ...   
711  {'rings': [[[-12455347.0952, 4966754.840000004...      49      035   
712  {'rings': [[[-12453471.3611, 4964642.738300003...      49      035   
713  {'rings': [[[-12454528.1172, 4964343.751500003...      49      035   
714  {'rings': [[[-12465233.158599999, 4967696.3889...      49      035   
715  {'rings': [[[-12390649.8356, 4669994.337099999...      49      015   

    TRACTCE  AFK_o  ALA_o  ALP_o  BDL_o  BGM_o  BNT_o  BRT_o  CDF_o  CEN_o  \
0    000901     96      0      2      8      0      0      0      0      0   
1    002500     33      0      1      4      0      0      0      0      0   
2    003401     18      0      0      0      0      0      0      0      0   
3    010210    342      0     66     10      0      1      0      0      1   
4    000505    109      0      3      1      0      0      0      0      0   
..      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
711  111701      0      0      0      1      0      1      0      0      1   
712  111903     10      0    

FID  OBJECTID STATEFP20 COUNTYFP20 TRACTCE20      GEOID20   NAME20  \
0      0         1        49        049    000901  49049000901     9.01   
1      1         2        49        049    002500  49049002500       25   
2      2         3        49        049    003401  49049003401    34.01   
3      3         4        49        049    010210  49049010210   102.10   
4      4         5        49        049    000505  49049000505     5.05   
..   ...       ...       ...        ...       ...          ...      ...   
711  711       712        49        035    111701  49035111701  1117.01   
712  712       713        49        035    111903  49035111903  1119.03   
713  713       714        49        035    111905  49035111905  1119.05   
714  714       715        49        035    113309  49035113309  1133.09   
715  715       716        49        015    976500  49015976500     9765   

       NAMELSAD20 MTFCC20 FUNCSTAT20       ALAND20    AWATER20   INTPTLAT20  \
0    Census Tract   G5020          S  1.686016e+06         0.0  +40.3051285   
1    Census Tract   G5020          S  1.034541e+06         0.0  +40.2296149   
2    Census Tract   G5020          S  9.085765e+06     23788.0  +40.0560227   
3    Census Tract   G5020          S  1.581048e+07         0.0  +40.4005884   
4    Census Tract   G5020          S  3.919712e+06         0.0  +40.3700595   
..            ...     ...        ...           ...         ...          ...   
711  Census Tract   G5020          S  1.358256e+06         0.0  +40.6934670   
712  Census Tract   G5020          S  2.072253e+06         0.0  +40.6806830   
713  Census Tract   G5020          S  1.167718e+06         0.0  +40.6765749   
714  Census Tract   G5020          S  1.867612e+06         0.0  +40.6881369   
715  Census Tract   G5020          S  8.782568e+09  14165655.0  +38.9311083   

       INTPTLON20     SHAPE_Leng    SHAPE_Area  \
0    -111.6922978    7129.054778  2.902253e+06   
1    -111.6497278    5588.845931  1.776891e+06   
2    -111.7122570   18878.825275  1.556674e+07   
3    -111.7306856   26101.425584  2.729233e+07   
4    -111.7070846   12562.893900  6.760193e+06   
..            ...            ...           ...   
711  -111.8826082    6277.757800  2.365082e+06   
712  -111.8627470    7592.371898  3.606962e+06   
713  -111.8744366    8615.733516  2.032283e+06   
714  -111.9693980    8501.284969  3.251486e+06   
715  -110.6644589  917894.696612  1.454313e+10   

                                                 SHAPE STATEFP COUNTYFP  \
0    {'rings': [[[-12434548.4857, 4911361.749799997...      49      049   
1    {'rings': [[[-12429589.868, 4898990.177699998]...      49      049   
2    {'rings': [[[-12439397.559799999, 4872289.2984...      49      049   
3    {'rings': [[[-12442557.703499999, 4926512.4487...      49      049   
4    {'rings': [[[-12437368.7665, 4920654.352499999...      49      049   
..                                                 ...     ...      ...   
711  {'rings': [[[-12455347.0952, 4966754.840000004...      49      035   
712  {'rings': [[[-12453471.3611, 4964642.738300003...      49      035   
713  {'rings': [[[-12454528.1172, 4964343.751500003...      49      035   
714  {'rings': [[[-12465233.158599999, 4967696.3889...      49      035   
715  {'rings': [[[-12390649.8356, 4669994.337099999...      49      015   

    TRACTCE     AFK_o         ALA_o     ALP_o     BDL_o     BGM_o  \
0    000901  0.505507  1.080681e-11  0.164670  0.119604  0.000000   
1    002500  0.186154  8.903830e-03  0.087534  0.070732  0.000000   
2    003401  0.098001  0.000000e+00  0.018588  0.002927  0.001238   
3    010210  1.778786  2.847868e-02  2.591938  0.135831  0.000004   
4    000505  0.571633  9.767451e-11  0.156923  0.027452  0.000000   
..      ...       ...           ...       ...       ...       ...   
711  111701  0.005147  9.445542e-02  0.000076  0.036537  0.000003   
712  111903  0.059897  1.155177e-01  0.172260  0.117866  0.028385   
713  111905  0.004037  2.217234e

In [40]:
sdf_SLCommutePatterns_tract.sum()


FID                                                      255970
OBJECTID                                                 256686
STATEFP20     4949494949494949494949494949494949494949494949...
COUNTYFP20    0490490490490490490490510130490490490490490490...
TRACTCE20     0009010025000034010102100005050005070102099601...
                                    ...                        
z49_d                                                    239774
z49_o                                                    239607
z51_d                                                      9499
z51_o                                                      9852
z57_d                                                    115029
Length: 234, dtype: object

In [41]:
sdf_SLCommutePatterns_Percent_SA_tract.sum()

FID                                                      255970
OBJECTID                                                 256686
STATEFP20     4949494949494949494949494949494949494949494949...
COUNTYFP20    0490490490490490490490510130490490490490490490...
TRACTCE20     0009010025000034010102100005050005070102099601...
                                    ...                        
z49_d                                                     100.0
z49_o                                                     100.0
z51_d                                                     100.0
z51_o                                                     100.0
z57_d                                                     100.0
Length: 234, dtype: object

In [42]:
sdf_SLCommutePatterns_tract.spatial.to_featureclass(fname_TractsWCommutePatterns_Number, sanitize_columns=False)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\SL\\SLCommutePatterns.gdb\\SL_Tract_CommutePatterns_Number'

In [43]:
sdf_SLCommutePatterns_Percent_SA_tract.spatial.to_featureclass(fname_TractsWCommutePatterns_Percent_SA, sanitize_columns=False)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\SL\\SLCommutePatterns.gdb\\SL_Tract_CommutePatterns_Percent_SelectedArea'

# Group by Small District

In [44]:
#input filenames
fname_SL_shp = os.path.join(dirInput, 'Dist_Small' + r'\Dist_Small_Counties.shp')

In [45]:
sdf_SL = pd.DataFrame.spatial.from_featureclass(fname_SL_shp)
sdf_SL

FID  DISTSML                         DSML_NAME STATEFP20 COUNTYFP20  \
0      0      1.0           1.1: Brigham City North        49        003   
1      1      2.0    2.1: Brigham City West of I-15        49        003   
2      2      3.0  3.1: Brigham City West and Perry        49        003   
3      3      4.0          3.2: Brigham City Center        49        003   
4      4      5.0                      4.1: Willard        49        003   
..   ...      ...                               ...       ...        ...   
150  150    151.0  99.1: Outside WFRC Modeling Area        49        031   
151  151    152.0  99.1: Outside WFRC Modeling Area        49        021   
152  152    153.0  99.1: Outside WFRC Modeling Area        49        055   
153  153    154.0  99.1: Outside WFRC Modeling Area        49        037   
154  154    155.0  99.1: Outside WFRC Modeling Area        49        025   

                                                 SHAPE  
0    {"rings": [[[412988.500000001, 4605724.4], [41...  
1    {"rings": [[[408196.8937999996, 4599532.781500...  
2    {"rings": [[[413636.79999999964, 4598064.69999...  
3    {"rings": [[[415302.1999999995, 4598736.699999...  
4    {"rings": [[[412551.0000000001, 4588753.600000...  
..                                                 ...  
150  {"rings": [[[384022.18659999967, 4263333.3738]...  
151  {"rings": [[[292688.5865000002, 4224956.9639],...  
152  {"rings": [[[438313.3267000001, 4262656.513800...  
153  {"rings": [[[609343.4170000004, 4095382.083499...  
154  {"rings": [[[425313.8965999996, 4154648.073699...  

[155 rows x 6 columns]

In [46]:
#calculate small district stats
df_SLCommutePatterns_sd = sdf_SLCommutePatterns.groupby(['STATEFP','COUNTYFP','DISTSML'])[dColCodesWCounty].apply(lambda x : x.astype(int).sum())
df_SLCommutePatterns_sd = df_SLCommutePatterns_sd.reset_index()
display(df_SLCommutePatterns_sd)

#caclulate tract Percent_SA stats
df_SLCommutePatterns_Percent_SA_sd = sdf_SLCommutePatterns_Percent_SA.groupby(['STATEFP','COUNTYFP','DISTSML'])[dColCodesWCounty].apply(lambda x : x.astype(float).sum())
df_SLCommutePatterns_Percent_SA_sd = df_SLCommutePatterns_Percent_SA_sd.reset_index()
display(df_SLCommutePatterns_Percent_SA_sd)


#df_test = df_SLCommutePatterns / df_SLCommutePatterns_ColSum

STATEFP COUNTYFP  DISTSML  AFK_o  ALA_o  ALP_o  BDL_o  BGM_o  BNT_o  \
0        49      001    149.0      0      0      0      0      0      0   
1        49      003      1.0      0      0      0      0    290      0   
2        49      003      2.0      0      0      0      0    111      0   
3        49      003      3.0      0      0      0      0   1516      4   
4        49      003      4.0      0      0      0      0   2532      1   
..      ...      ...      ...    ...    ...    ...    ...    ...    ...   
143      49      057     17.0      1      0      0      0     49     41   
144      49      057     18.0      2      0      0      8     20     37   
145      49      057     19.0      0      0      0      0      6     31   
146      49      057    124.0      0      0      0      0      5      1   
147      49      057    147.0      0      0      0      0      4      3   

     BRT_o  CDF_o  CEN_o  CHA_o  CHL_o  CLF_o  CLI_o  CMT_o  COA_o  CWH_o  \
0        0      0      0      0      0      0      0      0      0      0   
1        0      0      0      0      0     10      0      0      0      0   
2        0      0      1      0      0     13      0      0      0      0   
3        0      0      3      0      0     72      0      0      0      0   
4        0      0      0      0      0     32      1      0      0      3   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
143      0      0     16      0      0    614    287      0      0      0   
144      0      0     10      0      0    395    189      0      1      2   
145      0      0     14      0      0     63     30      0      0      1   
146      0      0      0      0      0     18     12      0      0      0   
147      0      0      0      0      0     42      3      0      0      0   

     DAN_o  DRA_o  EAG_o  ELK_o  EMT_o  FAR_o  FCS_o  FFD_o  FRR_o  FTH_o  \
0        0      0      0      0      0      0      0      0      0      0   
1        0      0      0      0      0      0      0      0      4      0   
2        0      0      0      0      0      0      0      0     17      3   
3        0      0      0      0      0     12      0      0     32      3   
4        0      0      0      0      0      1      0      0     46      2   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
143      0      4      2      0      0     68      0      0     97     14   
144      0      1      6      0      0     63      0      0     98     39   
145      0      0      0      0      0     39      0      0     12     15   
146      0      0      0      0      0      0      0      0     39      1   
147      0      0      0      0      0     15      0      0     24      1   

     GLA_o  GOS_o  GRL_o  HAR_o  HDT_o  HEB_o  HER_o  HGH_o  HNF_o  HOL_o  \
0        0      0      0      0      0      0      0      0      0      0   
1        0      0      0      1      0      0      0      0      0      0   
2        0      0      0     10      0      0      0      0      0      0   
3        0      0      0     33      0      0      0      0      0      0   
4        0      0      0     41      0      0      0      0      0      3   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
143      0      0      0    114      0      0      0      0      0      1   
144      0      0      0    139      0      0      0      0      1      1   
145      0      0      0     17      0      0      0      0      0      0   
146      0      0      0     11      0      0      0      0      0      0   
147      0      0      0     36      0      0      0      0      0      0   

     HOO_o  HVL_o  IND_o  INT_o  KAY_o  KMS_o  KMT_o  LAY_o  LEH_o  LIN_o  \
0        0      0      0      0      0      0      0      0      0      0   
1        0      0      0      0      0      0      0      5      0      0   
2        4      0      0      0      3      0      0      7      0      0   
3        1      0   

STATEFP COUNTYFP  DISTSML     AFK_o     ALA_o     ALP_o         BDL_o  \
0        49      001    149.0  0.000000  0.000000  0.000175  1.117181e-03   
1        49      003      1.0  0.000002  0.000000  0.000000  2.245136e-05   
2        49      003      2.0  0.000007  0.000036  0.000000  0.000000e+00   
3        49      003      3.0  0.002389  0.017575  0.000000  1.184656e-05   
4        49      003      4.0  0.001909  0.022279  0.000000  9.295255e-04   
..      ...      ...      ...       ...       ...       ...           ...   
143      49      057     17.0  0.013832  0.027695  0.004643  1.122730e-02   
144      49      057     18.0  0.013070  0.004604  0.007352  1.151546e-01   
145      49      057     19.0  0.001415  0.000000  0.003623  2.637330e-08   
146      49      057    124.0  0.000000  0.000000  0.000000  1.160834e-03   
147      49      057    147.0  0.002264  0.018019  0.000213  2.627258e-03   

         BGM_o         BNT_o     BRT_o     CDF_o     CEN_o         CHA_o  \
0     0.000000  9.976353e-04  0.000000  0.000000  0.000000  0.000000e+00   
1     3.893680  8.415699e-07  0.000000  0.000000  0.000001  0.000000e+00   
2     1.497573  6.346649e-04  0.000018  0.000000  0.016963  0.000000e+00   
3    20.366925  2.760228e-02  0.008901  0.000000  0.079360  1.848701e-02   
4    34.016280  1.604369e-02  0.027925  0.000401  0.018508  2.515279e-04   
..         ...           ...       ...       ...       ...           ...   
143   0.732048  2.764647e-01  0.000604  0.000015  0.393701  9.864138e-04   
144   0.330192  2.429912e-01  0.009491  0.045379  0.232912  1.126138e-10   
145   0.083372  1.717146e-01  0.000000  0.000000  0.241963  0.000000e+00   
146   0.071606  7.673879e-03  0.000000  0.000000  0.003105  0.000000e+00   
147   0.086522  2.625549e-02  0.013664  0.000000  0.020062  8.954389e-04   

            CHL_o     CLF_o         CLI_o         CMT_o         COA_o  \
0    0.000000e+00  0.000729  4.428195e-08  0.000000e+00  0.000000e+00   
1    0.000000e+00  0.043182  2.424798e-05  0.000000e+00  1.352508e-05   
2    1.038561e-07  0.051531  8.411420e-03  6.482835e-05  1.732887e-07   
3    7.360062e-03  0.291707  2.362739e-02  0.000000e+00  0.000000e+00   
4    0.000000e+00  0.145864  3.819123e-02  0.000000e+00  0.000000e+00   
..            ...       ...           ...           ...           ...   
143  1.454973e-02  2.456978  3.304086e+00  1.164740e-03  7.323482e-03   
144  1.195848e-05  1.591248  2.186017e+00  2.169032e-01  2.137320e-01   
145  1.116546e-02  0.251769  3.452673e-01  0.000000e+00  1.379255e-02   
146  0.000000e+00  0.072286  1.385464e-01  0.000000e+00  0.000000e+00   
147  0.000000e+00  0.173610  7.516363e-02  2.903438e-08  5.604302e-02   

        CWH_o     DAN_o     DRA_o         EAG_o     ELK_o         EMT_o  \
0    0.000000  0.000000  0.000749  2.609258e-08  0.002704  0.000000e+00   
1    0.000000  0.000000  0.000006  0.000000e+00  0.000000  0.000000e+00   
2    0.001065  0.000000  0.000953  0.000000e+00  0.000000  1.350901e-06   
3    0.004430  0.000000  0.000966  0.000000e+00  0.000000  3.670218e-06   
4    0.031272  0.000000  0.001656  1.656715e-03  0.000000  6.110963e-05   
..        ...       ...       ...           ...       ...           ...   
143  0.027081  0.021652  0.030660  2.087097e-02  0.008182  6.746568e-05   
144  0.028520  0.000000  0.016103  6.426458e-02  0.000000  8.231890e-05   
145  0.010520  0.000000  0.001283  1.771511e-06  0.000000  2.796133e-09   
146  0.000774  0.000000  0.000333  0.000000e+00  0.000000  0.000000e+00   
147  0.002389  0.034247  0.004251  5.782394e-03  0.000000  1.572225e-02   

        FAR_o     FCS_o  FFD_o     FRR_o     FTH_o         GLA_o     GOS_o  \
0    0.000941  0.000000    0.0  0.000000  0.000000  3.138209e-02  0.000000   
1    0.000003  0.000000    0.0  0.101048  0.000000  0.000000e+00  0.000000   
2    0.005736  0.000000    0.0  0.416792  0.095451  0.000000e+00  0.000000   
3    0.128647  0.000000    0.0  0.832508  0.108158  0.000000e+00  0.000000  

In [47]:
df_SLCommutePatterns_Percent_SA_sd.sum()

STATEFP     4949494949494949494949494949494949494949494949...
COUNTYFP    0010030030030030030030030050070090110110110110...
DISTSML                                               11772.0
AFK_o                                                   100.0
ALA_o                                                   100.0
                                  ...                        
z49_d                                                   100.0
z49_o                                                   100.0
z51_d                                                   100.0
z51_o                                                   100.0
z57_d                                                   100.0
Length: 218, dtype: object

In [48]:
sdf_SLCommutePatterns_sd = pd.DataFrame.merge(sdf_SL, df_SLCommutePatterns_sd, left_on=['STATEFP20','COUNTYFP20','DISTSML'], right_on=['STATEFP','COUNTYFP',"DISTSML"])
display(sdf_SLCommutePatterns_sd)

sdf_SLCommutePatterns_Percent_SA_sd = pd.DataFrame.merge(sdf_SL, df_SLCommutePatterns_Percent_SA_sd, left_on=['STATEFP20','COUNTYFP20','DISTSML'], right_on=['STATEFP','COUNTYFP',"DISTSML"])
display(sdf_SLCommutePatterns_Percent_SA_sd)

FID  DISTSML                         DSML_NAME STATEFP20 COUNTYFP20  \
0      0      1.0           1.1: Brigham City North        49        003   
1      1      2.0    2.1: Brigham City West of I-15        49        003   
2      2      3.0  3.1: Brigham City West and Perry        49        003   
3      3      4.0          3.2: Brigham City Center        49        003   
4      5      6.0       5.1: Mantua and Sardine Cyn        49        003   
..   ...      ...                               ...       ...        ...   
142  150    151.0  99.1: Outside WFRC Modeling Area        49        031   
143  151    152.0  99.1: Outside WFRC Modeling Area        49        021   
144  152    153.0  99.1: Outside WFRC Modeling Area        49        055   
145  153    154.0  99.1: Outside WFRC Modeling Area        49        037   
146  154    155.0  99.1: Outside WFRC Modeling Area        49        025   

                                                 SHAPE STATEFP COUNTYFP  \
0    {'rings': [[[412988.500000001, 4605724.4], [41...      49      003   
1    {'rings': [[[408196.8937999996, 4599532.781500...      49      003   
2    {'rings': [[[413636.79999999964, 4598064.69999...      49      003   
3    {'rings': [[[415302.1999999995, 4598736.699999...      49      003   
4    {'rings': [[[416806.00000000023, 4602635.50000...      49      003   
..                                                 ...     ...      ...   
142  {'rings': [[[384022.18659999967, 4263333.3738]...      49      031   
143  {'rings': [[[292688.5865000002, 4224956.9639],...      49      021   
144  {'rings': [[[438313.3267000001, 4262656.513800...      49      055   
145  {'rings': [[[609343.4170000004, 4095382.083499...      49      037   
146  {'rings': [[[425313.8965999996, 4154648.073699...      49      025   

     AFK_o  ALA_o  ALP_o  BDL_o  BGM_o  BNT_o  BRT_o  CDF_o  CEN_o  CHA_o  \
0        0      0      0      0    290      0      0      0      0      0   
1        0      0      0      0    111      0      0      0      1      0   
2        0      0      0      0   1516      4      0      0      3      0   
3        0      0      0      0   2532      1      0      0      0      0   
4        0      0      0      6    248      3      0      0      3      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
142      0      0      0      0      0      0      0      0      0      0   
143      0      0      0      0      0      0      0      0      0      0   
144      0      0      0      0      0      0      0      0      0      0   
145      0      0      0      0      0      0      0      0      0      0   
146      0      0      0      0      0      0      0      0      0      0   

     CHL_o  CLF_o  CLI_o  CMT_o  COA_o  CWH_o  DAN_o  DRA_o  EAG_o  ELK_o  \
0        0     10      0      0      0      0      0      0      0      0   
1        0     13      0      0      0      0      0      0      0      0   
2        0     72      0      0      0      0      0      0      0      0   
3        0     32      1      0      0      3      0      0      0      0   
4        0      2      0      0      0      0      0      6      0      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
142      0      0      0      0      0      0      0      0      0      0   
143      0      0      0      0      0      0      0      0      0      0   
144      0      0      0      0      0      0      0      0      0      0   
145      0      0      0      0      0      0      0      0      0      0   
146      0      0      0      0      0      0      0      0      0      0   

     EMT_o  FAR_o  FCS_o  FFD_o  FRR_o  FTH_o  GLA_o  GOS_o  GRL_o  HAR_o  \
0        0      0      0      0      4      0      0      0      0      1   
1        0      0      0      0     17      3      0      0      0     10   
2        0     12      0      0     32      3      0      0      0     33   
3        0      1      0      0  

FID  DISTSML                         DSML_NAME STATEFP20 COUNTYFP20  \
0      0      1.0           1.1: Brigham City North        49        003   
1      1      2.0    2.1: Brigham City West of I-15        49        003   
2      2      3.0  3.1: Brigham City West and Perry        49        003   
3      3      4.0          3.2: Brigham City Center        49        003   
4      5      6.0       5.1: Mantua and Sardine Cyn        49        003   
..   ...      ...                               ...       ...        ...   
142  150    151.0  99.1: Outside WFRC Modeling Area        49        031   
143  151    152.0  99.1: Outside WFRC Modeling Area        49        021   
144  152    153.0  99.1: Outside WFRC Modeling Area        49        055   
145  153    154.0  99.1: Outside WFRC Modeling Area        49        037   
146  154    155.0  99.1: Outside WFRC Modeling Area        49        025   

                                                 SHAPE STATEFP COUNTYFP  \
0    {'rings': [[[412988.500000001, 4605724.4], [41...      49      003   
1    {'rings': [[[408196.8937999996, 4599532.781500...      49      003   
2    {'rings': [[[413636.79999999964, 4598064.69999...      49      003   
3    {'rings': [[[415302.1999999995, 4598736.699999...      49      003   
4    {'rings': [[[416806.00000000023, 4602635.50000...      49      003   
..                                                 ...     ...      ...   
142  {'rings': [[[384022.18659999967, 4263333.3738]...      49      031   
143  {'rings': [[[292688.5865000002, 4224956.9639],...      49      021   
144  {'rings': [[[438313.3267000001, 4262656.513800...      49      055   
145  {'rings': [[[609343.4170000004, 4095382.083499...      49      037   
146  {'rings': [[[425313.8965999996, 4154648.073699...      49      025   

            AFK_o     ALA_o     ALP_o     BDL_o      BGM_o         BNT_o  \
0    1.578056e-06  0.000000  0.000000  0.000022   3.893680  8.415699e-07   
1    7.145945e-06  0.000036  0.000000  0.000000   1.497573  6.346649e-04   
2    2.388999e-03  0.017575  0.000000  0.000012  20.366925  2.760228e-02   
3    1.909430e-03  0.022279  0.000000  0.000930  34.016280  1.604369e-02   
4    9.926521e-07  0.004485  0.000000  0.088948   3.333037  2.393317e-02   
..            ...       ...       ...       ...        ...           ...   
142  0.000000e+00  0.000000  0.000000  0.002234   0.000000  0.000000e+00   
143  1.914718e-03  0.000005  0.000000  0.003156   0.001950  3.980073e-04   
144  0.000000e+00  0.000000  0.003546  0.000000   0.000000  0.000000e+00   
145  4.779977e-04  0.000000  0.000000  0.000000   0.000000  5.043545e-04   
146  0.000000e+00  0.000000  0.000000  0.000000   0.000000  0.000000e+00   

        BRT_o     CDF_o     CEN_o     CHA_o         CHL_o     CLF_o     CLI_o  \
0    0.000000  0.000000  0.000001  0.000000  0.000000e+00  0.043182  0.000024   
1    0.000018  0.000000  0.016963  0.000000  1.038561e-07  0.051531  0.008411   
2    0.008901  0.000000  0.079360  0.018487  7.360062e-03  0.291707  0.023627   
3    0.027925  0.000401  0.018508  0.000252  0.000000e+00  0.145864  0.038191   
4    0.000000  0.000000  0.073153  0.000000  0.000000e+00  0.013258  0.007144   
..        ...       ...       ...       ...           ...       ...       ...   
142  0.000000  0.000000  0.000000  0.000000  0.000000e+00  0.000000  0.000000   
143  0.000000  0.000000  0.001552  0.000000  1.182983e-02  0.000472  0.000000   
144  0.000000  0.000000  0.000000  0.000000  0.000000e+00  0.000001  0.000000   
145  0.000000  0.000000  0.000000  0.000000  0.000000e+00  0.000000  0.000000   
146  0.000000  0.000000  0.000000  0.000000  0.000000e+00  0.000000  0.000000   

        CMT_o         COA_o     CWH_o     DAN_o         DRA_o         EAG_o  \
0    0.000000  1.352508e-05  0.000000  0.000000  6.389825e-06  0.000000e+00   
1    0.000065  1.732887e-07  0.001065  0.000000  9.531861e-04  0.000000e+00   
2    0.000000  0.000000e+00  0.004430  0.000000  9.664702e-04  0.000

In [49]:
sdf_SLCommutePatterns_sd.sum()

FID                                                       11507
DISTSML                                                 11654.0
DSML_NAME     1.1: Brigham City North2.1: Brigham City West ...
STATEFP20     4949494949494949494949494949494949494949494949...
COUNTYFP20    0030030030030030570030570570570570570570570570...
                                    ...                        
z49_d                                                    239706
z49_o                                                    239545
z51_d                                                      9499
z51_o                                                      9852
z57_d                                                    115029
Length: 222, dtype: object

In [50]:
sdf_SLCommutePatterns_Percent_SA_sd.sum()

FID                                                       11507
DISTSML                                                 11654.0
DSML_NAME     1.1: Brigham City North2.1: Brigham City West ...
STATEFP20     4949494949494949494949494949494949494949494949...
COUNTYFP20    0030030030030030570030570570570570570570570570...
                                    ...                        
z49_d                                                 99.971368
z49_o                                                 99.974192
z51_d                                                     100.0
z51_o                                                     100.0
z57_d                                                 99.999845
Length: 222, dtype: object

In [51]:
sdf_SLCommutePatterns_sd.spatial.to_featureclass(fname_SDWCommutePatterns_Number, sanitize_columns=False)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\SL\\SLCommutePatterns.gdb\\SL_SD_CommutePatterns_Number'

In [52]:
sdf_SLCommutePatterns_Percent_SA_sd.spatial.to_featureclass(fname_SDWCommutePatterns_Percent_SA, sanitize_columns=False)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\SL\\SLCommutePatterns.gdb\\SL_SD_CommutePatterns_Percent_SelectedArea'

# Group Rows by City

In [53]:

#verify that shape exists and sdf was created correctly and get spatial reference
#print(sdf_CityTownship.iloc[0].SHAPE.spatialReference)
#print(sdf_BlockGroups.iloc[0].SHAPE.spatialReference)
#
##change projection to 26912 to match TAZ Centroids
#sdf_CityTownship.spatial.project(26912)
#sdf_BlockGroups.spatial.project(26912)
#
#print(sdf_CityTownship.iloc[0].SHAPE.spatialReference)
#print(sdf_BlockGroups.iloc[0].SHAPE.spatialReference)

print ("Calculating blockgroup acreage...")

# Execute DeleteField
arcpy.DeleteField_management(fname_BlockGroups_shp, ['BGAcres'])

arcpy.AddField_management(fname_BlockGroups_shp, "BGAcres" , "DOUBLE")
arcpy.CalculateField_management(fname_BlockGroups_shp,
                                "BGAcres",
                                "!shape.area@acres!",
                                "PYTHON_9.3")
print ("Done calculating blockgroup acreage.")


print ("Intersecting blockgroup with city/township/county...")
#intersection parcels with analysis area types
deleteIfExists(fname_CityTownshipCounty_BlockGroups_shp)
arcpy.analysis.Intersect([fname_CityTownshipCountyWCodes_shp,fname_BlockGroups_shp], fname_CityTownshipCounty_BlockGroups_shp)


print ("Calculating piece area...")
arcpy.AddField_management(fname_CityTownshipCounty_BlockGroups_shp, "PieceAcres" , "DOUBLE")
arcpy.CalculateField_management(fname_CityTownshipCounty_BlockGroups_shp,
                                "PieceAcres",
                                "!shape.area@acres!",
                                "PYTHON_9.3")
print ("Calculating Percent_SA of blockgroup...")
arcpy.AddField_management(fname_CityTownshipCounty_BlockGroups_shp, "PortionBG" , "DOUBLE")
arcpy.CalculateField_management(fname_CityTownshipCounty_BlockGroups_shp,
                                "PortionBG",
                                "!PieceAcres!/!BGAcres!",
                                "PYTHON_9.3")


print ("Done")

Calculating blockgroup acreage...
Done calculating blockgroup acreage.
Intersecting blockgroup with city/township/county...
Calculating piece area...
Calculating Percent_SA of blockgroup...
Done


In [54]:
#read newly created shapefile
sdf_CityTownshipCounty_BlockGroups = pd.DataFrame.spatial.from_featureclass(fname_CityTownshipCounty_BlockGroups_shp)


In [55]:
sdf_SLCommutePatterns_joinCity = pd.DataFrame.merge(sdf_CityTownshipCounty_BlockGroups,sdf_SLCommutePatterns,on=['GEOID','STATEFP','COUNTYFP','TRACTCE','DISTSML','BLKGRPCE','NAMELSAD','MTFCC', 'FUNCSTAT','ALAND','AWATER','INTPTLAT','INTPTLON','BGAcres'])
sdf_SLCommutePatterns_joinCity

FID_x  FID_Munici  Id  FID_Muni_1 CODE3  \
0         0           0   0          -1   z05   
1       238           5   0          -1   z03   
2       288           6   0          -1   z57   
3      2156          90   0          55   NOG   
4         1           0   0          -1   z05   
...     ...         ...  ..         ...   ...   
3622   3551         139   0          96   WVC   
3623   3552         139   0          96   WVC   
3624   3553         139   0          96   WVC   
3625   3554         139   0          96   WVC   
3626   3558         139   0          96   WVC   

                           FIRST_NAME  FID_tl_202 STATEFP COUNTYFP TRACTCE  \
0         Cache County Unincorporated          95      49      057  210101   
1     Box Elder County Unincorporated          95      49      057  210101   
2         Weber County Unincorporated          95      49      057  210101   
3                         North Ogden          95      49      057  210101   
4         Cache County Unincorporated         578      49      005  001101   
...                               ...         ...     ...      ...     ...   
3622                 West Valley City        1666      49      035  113537   
3623                 West Valley City        1673      49      035  113309   
3624                 West Valley City        1681      49      035  113409   
3625                 West Valley City        1885      49      035  113309   
3626                 West Valley City        1907      49      035  113414   

      DISTSML BLKGRPCE         GEOID       NAMELSAD  MTFCC FUNCSTAT  \
0       147.0        1  490572101011  Block Group 1  G5030        S   
1       147.0        1  490572101011  Block Group 1  G5030        S   
2       147.0        1  490572101011  Block Group 1  G5030        S   
3       147.0        1  490572101011  Block Group 1  G5030        S   
4       130.0        1  490050011011  Block Group 1  G5030        S   
...       ...      ...           ...            ...    ...      ...   
3622     43.0        1  490351135371  Block Group 1  G5030        S   
3623     43.0        1  490351133091  Block Group 1  G5030        S   
3624     37.0        3  490351134093  Block Group 3  G5030        S   
3625     43.0        2  490351133092  Block Group 2  G5030        S   
3626     37.0        1  490351134141  Block Group 1  G5030        S   

           ALAND   AWATER     INTPTLAT      INTPTLON  CENTROID_X_x  \
0     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
1     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
2     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
3     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
4      2552940.0      0.0  +41.7149272  -111.8231317   -111.823132   
...          ...      ...          ...           ...           ...   
3622    651043.0      0.0  +40.6784813  -111.9722719   -111.972272   
3623    650128.0      0.0  +40.6929994  -111.9723023   -111.972302   
3624    685688.0      0.0  +40.6858633  -112.0391343   -112.039134   
3625    649958.0      0.0  +40.6857436  -111.9722922   -111.972292   
3626    929713.0      0.0  +40.7012857  -112.0324271   -112.032427   

      CENTROID_Y_x       BGAcres    PieceAcres  PortionBG  \
0        41.372480  21464.006346      2.821747   0.000131   
1        41.372480  21464.006346      0.887017   0.000041   
2        41.372480  21464.006346  20832.493173   0.970578   
3        41.372480  21464.006346    641.857708   0.029904   
4        41.714927    630.412036    630.843690   1.000685   
...            ...           ...           ...        ...   
3622     40.678481    160.774214    160.876163   1.000634   
3623     40.692999    160.548274    160.650081   1.000634   
3624     40.685863    169.334283    169.437669   1.000611   
3625     40.685744    160.506512    160.608298   1.000634   
3626     40.701286    229.596643    229.737391   1.000613   

                                                SHAPE

In [56]:
my_list = list(sdf_SLCommutePatterns_joinCity)
my_list

['FID_x',
 'FID_Munici',
 'Id',
 'FID_Muni_1',
 'CODE3',
 'FIRST_NAME',
 'FID_tl_202',
 'STATEFP',
 'COUNTYFP',
 'TRACTCE',
 'DISTSML',
 'BLKGRPCE',
 'GEOID',
 'NAMELSAD',
 'MTFCC',
 'FUNCSTAT',
 'ALAND',
 'AWATER',
 'INTPTLAT',
 'INTPTLON',
 'CENTROID_X_x',
 'CENTROID_Y_x',
 'BGAcres',
 'PieceAcres',
 'PortionBG',
 'SHAPE_x',
 'FID_y',
 'CENTROID_X_y',
 'CENTROID_Y_y',
 'SHAPE_y',
 'fakeid',
 'AFK_o',
 'ALA_o',
 'ALP_o',
 'BDL_o',
 'BGM_o',
 'BNT_o',
 'BRT_o',
 'CDF_o',
 'CEN_o',
 'CHA_o',
 'CHL_o',
 'CLF_o',
 'CLI_o',
 'CMT_o',
 'COA_o',
 'CWH_o',
 'DAN_o',
 'DRA_o',
 'EAG_o',
 'ELK_o',
 'EMT_o',
 'FAR_o',
 'FCS_o',
 'FFD_o',
 'FRR_o',
 'FTH_o',
 'GLA_o',
 'GOS_o',
 'GRL_o',
 'HAR_o',
 'HDT_o',
 'HEB_o',
 'HER_o',
 'HGH_o',
 'HNF_o',
 'HOL_o',
 'HOO_o',
 'HVL_o',
 'IND_o',
 'INT_o',
 'KAY_o',
 'KMS_o',
 'KMT_o',
 'LAY_o',
 'LEH_o',
 'LIN_o',
 'MAP_o',
 'MID_o',
 'MLC_o',
 'MMT_o',
 'MRG_o',
 'MSL_o',
 'MUR_o',
 'MWY_o',
 'NOG_o',
 'NSL_o',
 'OGD_o',
 'OKL_o',
 'ORM_o',
 'PAY_o',
 'PG

In [57]:
#for i in dColCodes:
#    display(sdf_SLCommutePatterns_joinCity[[i]])

In [58]:
df_SLCommutePatterns_CityCalcs = sdf_SLCommutePatterns_joinCity.copy()

for i in dColCodesWCounty:
    display(i)
    
    df_SLCommutePatterns_CityCalcs[i] = df_SLCommutePatterns_CityCalcs[i] * df_SLCommutePatterns_CityCalcs['PortionBG']


'AFK_o'

'ALA_o'

'ALP_o'

'BDL_o'

'BGM_o'

...

'z49_d'

'z49_o'

'z51_d'

'z51_o'

'z57_d'

In [59]:
df_SLCommutePatterns_CityCalcs = df_SLCommutePatterns_CityCalcs.rename(columns={"first_name":"FIRST_NAME", "code3":"CODE3"})
df_SLCommutePatterns_CityCalcs

FID_x  FID_Munici  Id  FID_Muni_1 CODE3  \
0         0           0   0          -1   z05   
1       238           5   0          -1   z03   
2       288           6   0          -1   z57   
3      2156          90   0          55   NOG   
4         1           0   0          -1   z05   
...     ...         ...  ..         ...   ...   
3622   3551         139   0          96   WVC   
3623   3552         139   0          96   WVC   
3624   3553         139   0          96   WVC   
3625   3554         139   0          96   WVC   
3626   3558         139   0          96   WVC   

                           FIRST_NAME  FID_tl_202 STATEFP COUNTYFP TRACTCE  \
0         Cache County Unincorporated          95      49      057  210101   
1     Box Elder County Unincorporated          95      49      057  210101   
2         Weber County Unincorporated          95      49      057  210101   
3                         North Ogden          95      49      057  210101   
4         Cache County Unincorporated         578      49      005  001101   
...                               ...         ...     ...      ...     ...   
3622                 West Valley City        1666      49      035  113537   
3623                 West Valley City        1673      49      035  113309   
3624                 West Valley City        1681      49      035  113409   
3625                 West Valley City        1885      49      035  113309   
3626                 West Valley City        1907      49      035  113414   

      DISTSML BLKGRPCE         GEOID       NAMELSAD  MTFCC FUNCSTAT  \
0       147.0        1  490572101011  Block Group 1  G5030        S   
1       147.0        1  490572101011  Block Group 1  G5030        S   
2       147.0        1  490572101011  Block Group 1  G5030        S   
3       147.0        1  490572101011  Block Group 1  G5030        S   
4       130.0        1  490050011011  Block Group 1  G5030        S   
...       ...      ...           ...            ...    ...      ...   
3622     43.0        1  490351135371  Block Group 1  G5030        S   
3623     43.0        1  490351133091  Block Group 1  G5030        S   
3624     37.0        3  490351134093  Block Group 3  G5030        S   
3625     43.0        2  490351133092  Block Group 2  G5030        S   
3626     37.0        1  490351134141  Block Group 1  G5030        S   

           ALAND   AWATER     INTPTLAT      INTPTLON  CENTROID_X_x  \
0     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
1     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
2     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
3     86898873.0  19742.0  +41.3700825  -111.9334158   -111.919266   
4      2552940.0      0.0  +41.7149272  -111.8231317   -111.823132   
...          ...      ...          ...           ...           ...   
3622    651043.0      0.0  +40.6784813  -111.9722719   -111.972272   
3623    650128.0      0.0  +40.6929994  -111.9723023   -111.972302   
3624    685688.0      0.0  +40.6858633  -112.0391343   -112.039134   
3625    649958.0      0.0  +40.6857436  -111.9722922   -111.972292   
3626    929713.0      0.0  +40.7012857  -112.0324271   -112.032427   

      CENTROID_Y_x       BGAcres    PieceAcres  PortionBG  \
0        41.372480  21464.006346      2.821747   0.000131   
1        41.372480  21464.006346      0.887017   0.000041   
2        41.372480  21464.006346  20832.493173   0.970578   
3        41.372480  21464.006346    641.857708   0.029904   
4        41.714927    630.412036    630.843690   1.000685   
...            ...           ...           ...        ...   
3622     40.678481    160.774214    160.876163   1.000634   
3623     40.692999    160.548274    160.650081   1.000634   
3624     40.685863    169.334283    169.437669   1.000611   
3625     40.685744    160.506512    160.608298   1.000634   
3626     40.701286    229.596643    229.737391   1.000613   

                                                SHAPE

In [60]:
df_SLCommutePatterns_CityCalcsSum = df_SLCommutePatterns_CityCalcs.groupby(['CODE3','FIRST_NAME'], as_index=False)[dColCodesWCounty].apply(lambda x : x.astype(int).sum())
df_SLCommutePatterns_CityCalcsSum = df_SLCommutePatterns_CityCalcsSum.reset_index()
df_SLCommutePatterns_CityCalcsSum

index CODE3                        FIRST_NAME  AFK_o  ALA_o  ALP_o  \
0        0   AFK                     American Fork   4226      0    253   
1        1   ALA                              Alta      0      8      0   
2        2   ALP                            Alpine    282      0    366   
3        3   BDL                         Bluffdale     39      0     23   
4        4   BGM                      Brigham City      0      0      0   
..     ...   ...                               ...    ...    ...    ...   
121    121   z49        Utah County Unincorporated    953      0     88   
122    122   z51     Wasatch County Unincorporated      8      0      1   
123    123   z53  Washington County Unincorporated      0      0      0   
124    124   z55       Wayne County Unincorporated      0      0      0   
125    125   z57       Weber County Unincorporated      0      0      0   

     BDL_o  BGM_o  BNT_o  BRT_o  CDF_o  CEN_o  CHA_o  CHL_o  CLF_o  CLI_o  \
0       91      0      1      0      6      0      0    551      5      0   
1        0      0      0      3      0      0      0      0      0      0   
2       10      0      1      0      0      1      0    137      0      0   
3      636      5     13      0      0      4      0     16      5      3   
4        0   3345      2      0      0      1      0      0     39      1   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121     70      0      0      0     31      1      0    140      9      6   
122      0      0      1      0      0      0     97      0      1      0   
123      0      0      0      0      0      0      0      0      0      0   
124      0      0      0      0      0      0      0      0      0      0   
125      0     44     15      0      0      3      0      0    284     85   

     CMT_o  COA_o  CWH_o  DAN_o  DRA_o  EAG_o  ELK_o  EMT_o  FAR_o  FCS_o  \
0        0      0      6      0    376    506      4      0      4      0   
1        0      0     11      0      3      0      0      0      0      0   
2        0      0      4      0    161     29      0      0      0      0   
3        7      0     34      0    740     94      0      0      2      0   
4        0      0      3      0      0      0      0      0     10      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121      0      0     19      0    333    448    142      0      4      0   
122      6      7      2    161      5      2      1      1      0     54   
123      0      0      0      0      0      0      0      0      0      0   
124      0      0      0      0      0      0      0      0      0      0   
125      0      0      0      0      1      0      0      0     29      0   

     FFD_o  FRR_o  FTH_o  GLA_o  GOS_o  GRL_o  HAR_o  HDT_o  HEB_o  HER_o  \
0        6      0      3      3      0      0      0      0      3     82   
1        0      0      0      0      0      0      0      0      0      0   
2        0      0      0      0      1      0      0      0      0      0   
3        0      0      0      2      0      0      0      0      0    301   
4        0     58      5      0      0      0     48      0      0      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121     18      0      2    101     25      5      1      0      6     54   
122      0      0      0      0      0      0      0    103   1276      4   
123      0      0      0      0      0      0      0      0      0      0   
124      0      0      0      0      0      0      0      0      0      0   
125      0    233      6      0      0      0    220      0      0      0   

     HGH_o  HNF_o  HOL_o  HOO_o  HVL_o  IND_o  INT_o  KAY_o  KMS_o  KMT_o  \
0     1296      0      9      0      0      1      0      2      0      1   
1        0      0      4      0      0      0      0      0      0      0   
2      503      0      2      0      0      0      0      0      0      0   
3       88      0    

In [61]:
df_SLCommutePatterns_CityCalcsSum.sum()

index                                                      7875
CODE3         AFKALAALPBDLBGMBNTBRTCDFCENCHACHLCLFCLICMTCOAC...
FIRST_NAME    American ForkAltaAlpineBluffdaleBrigham CityBo...
AFK_o                                                     18616
ALA_o                                                       325
                                    ...                        
z49_d                                                    239631
z49_o                                                    239446
z51_d                                                      9453
z51_o                                                      9810
z57_d                                                    114908
Length: 218, dtype: object

In [62]:
sdf_SLCommutePatterns_joinCity_Percent_SA = pd.DataFrame.merge(sdf_CityTownshipCounty_BlockGroups,sdf_SLCommutePatterns_Percent_SA,on=['GEOID','STATEFP','COUNTYFP','TRACTCE','DISTSML','BLKGRPCE','NAMELSAD','MTFCC', 'FUNCSTAT','ALAND','AWATER','INTPTLAT','INTPTLON','BGAcres'])
sdf_SLCommutePatterns_joinCity_Percent_SA = sdf_SLCommutePatterns_joinCity_Percent_SA.rename(columns={"first_name":"FIRST_NAME", "code3":"CODE3"})
df_SLCommutePatterns_CityCalcs_Percent_SA = sdf_SLCommutePatterns_joinCity_Percent_SA.copy()

for i in dColCodesWCounty:    
    df_SLCommutePatterns_CityCalcs_Percent_SA[i] = df_SLCommutePatterns_CityCalcs_Percent_SA[i] * df_SLCommutePatterns_CityCalcs_Percent_SA['PortionBG']


display(df_SLCommutePatterns_CityCalcs_Percent_SA.sum())
    
df_SLCommutePatterns_CityCalcs_Percent_SA = df_SLCommutePatterns_CityCalcs_Percent_SA.fillna(0)
   

df_SLCommutePatterns_CityCalcsSum_Percent_SA = df_SLCommutePatterns_CityCalcs_Percent_SA.groupby(['CODE3','FIRST_NAME'], as_index=False)[dColCodesWCounty].apply(lambda x : x.astype(float).sum())
df_SLCommutePatterns_CityCalcsSum_Percent_SA = df_SLCommutePatterns_CityCalcsSum_Percent_SA.reset_index()
df_SLCommutePatterns_CityCalcsSum_Percent_SA
    
display(df_SLCommutePatterns_CityCalcsSum_Percent_SA.sum())

FID_x                                                   6578904
FID_Munici                                               251195
Id                                                            0
FID_Muni_1                                               139499
CODE3         z05z03z57NOGz05z05z05z05z05z05z05z05z05z05z03z...
                                    ...                        
z49_o                                                100.069586
z51_d                                                100.075684
z51_o                                                 100.07563
z57_d                                                100.062795
z57_o                                                251.367151
Length: 245, dtype: object

index                                                      7875
CODE3         AFKALAALPBDLBGMBNTBRTCDFCENCHACHLCLFCLICMTCOAC...
FIRST_NAME    American ForkAltaAlpineBluffdaleBrigham CityBo...
AFK_o                                                100.068682
ALA_o                                                100.067496
                                    ...                        
z49_d                                                100.069606
z49_o                                                100.069586
z51_d                                                100.075684
z51_o                                                 100.07563
z57_d                                                100.062795
Length: 218, dtype: object

In [63]:
sdf_SLCommutePatterns_City_Number = pd.DataFrame.merge(sdf_CityTownshipWCodes,df_SLCommutePatterns_CityCalcsSum,on=['CODE3','FIRST_NAME'])
sdf_SLCommutePatterns_City_Percent_SA = pd.DataFrame.merge(sdf_CityTownshipWCodes,df_SLCommutePatterns_CityCalcsSum_Percent_SA,on=['CODE3','FIRST_NAME'])

In [64]:
sdf_SLCommutePatterns_City_Number.spatial.to_featureclass(fname_CitiesWCommutePatterns_Number, sanitize_columns=False)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\SL\\SLCommutePatterns.gdb\\SL_City_CommutePatterns_Number'

In [65]:
sdf_SLCommutePatterns_City_Percent_SA.spatial.to_featureclass(fname_CitiesWCommutePatterns_Percent_SA, sanitize_columns=False)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\SL\\SLCommutePatterns.gdb\\SL_City_CommutePatterns_Percent_SelectedArea'

In [66]:
sdf_SLCommutePatterns_City_Number

OBJECTID CODE3        FIRST_NAME FIRST_COUNTYNBR  \
0          1   AFK     American Fork              25   
1          2   ALA              Alta              18   
2          3   ALP            Alpine              25   
3          4   BDL         Bluffdale              18   
4          5   BGM      Brigham City              02   
..       ...   ...               ...             ...   
92        93   WIL           Willard              02   
93        94   WJC       West Jordan              18   
94        95   WPT        West Point              06   
95        96   WVC  West Valley City              18   
96        97   WXC       Woods Cross              06   

                                                SHAPE  index  AFK_o  ALA_o  \
0   {"rings": [[[-111.77435121873373, 40.353624868...      0   4226      0   
1   {"rings": [[[-111.59946851855727, 40.577431980...      1      0      8   
2   {"rings": [[[-111.75455302160464, 40.479513910...      2    282      0   
3   {"rings": [[[-111.9704071902396, 40.5008379065...      3     39      0   
4   {"rings": [[[-112.01898409573937, 41.535781784...      4      0      0   
..                                                ...    ...    ...    ...   
92  {"rings": [[[-112.02999503963935, 41.391465965...     92      0      0   
93  {"rings": [[[-112.00475852158849, 40.638664299...     93    112      8   
94  {"rings": [[[-112.10779328273378, 41.143687479...     94      0      0   
95  {"rings": [[[-111.9626132723846, 40.7260972067...     95     63      5   
96  {"rings": [[[-111.89260269236036, 40.866220107...     96      0      0   

    ALP_o  BDL_o  BGM_o  BNT_o  BRT_o  CDF_o  CEN_o  CHA_o  CHL_o  CLF_o  \
0     253     91      0      1      0      6      0      0    551      5   
1       0      0      0      0      3      0      0      0      0      0   
2     366     10      0      1      0      0      1      0    137      0   
3      23    636      5     13      0      0      4      0     16      5   
4       0      0   3345      2      0      0      1      0      0     39   
..    ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
92      0      0     28      0      0      0      0      0      0      2   
93     14    492      0     83      6      0     34      0      4     17   
94      0      0      1     21      0      0      6      0      0    766   
95      3    214      5    350      2      1     90      0      5    172   
96      0     12      0   1572      0      0    244      0      0     69   

    CLI_o  CMT_o  COA_o  CWH_o  DAN_o  DRA_o  EAG_o  ELK_o  EMT_o  FAR_o  \
0       0      0      0      6      0    376    506      4      0      4   
1       0      0      0     11      0      3      0      0      0      0   
2       0      0      0      4      0    161     29      0      0      0   
3       3      7      0     34      0    740     94      0      0      2   
4       1      0      0      3      0      0      0      0      0     10   
..    ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
92      0      0      0      0      0      0      0      0      0      0   
93      5     83      2    463      2   1337    124      0      0     25   
94    711      0      0      2      0      1      0      0      0     28   
95     66      8      0    377      0    825    139      1      0    147   
96     22      0      0     10      0     33      7      0      1    211   

    FCS_o  FFD_o  FRR_o  FTH_o  GLA_o  GOS_o  GRL_o  HAR_o  HDT_o  HEB_o  \
0       0      6      0      3      3      0      0      0      0      3   
1       0      0      0      0      0      0      0      0      0      0   
2       0      0      0      0      0      1      0      0      0      0   
3       0      0      0      0      2      0      0      0      0      0   
4       0      0     58      5      0      0      0     48      0      0   
..    ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
92      0      0      3      0      

# Calculate Percents by Map Units

In [67]:
# prepare column list

#display(dColCodesWCounty)
dColCodesWCounty = dColCodesWCounty.copy()

dColCodesWCounty_x = [x for x in dColCodesWCounty if "d" not in x]
dColCodesWCounty_y = [x for x in dColCodesWCounty if "o" not in x]

#remove and append to make sure at end
dColCodesWCounty_x.remove('TTL_o')
dColCodesWCounty_y.remove('TTL_d')
dColCodesWCounty_x.append('TTL_o')
dColCodesWCounty_y.append('TTL_d')

display(dColCodesWCounty_x)
display(dColCodesWCounty_y)

dColCodesNoTotal_x = [x for x in dColCodes if "d" not in x]
dColCodesNoTotal_x.remove('TTL_o')

dColCodesNoTotal_x = [x for x in dColCodes if "o" not in x]
dColCodesNoTotal_x.remove('TTL_d')

['AFK_o',
 'ALA_o',
 'ALP_o',
 'BDL_o',
 'BGM_o',
 'BNT_o',
 'BRT_o',
 'CDF_o',
 'CEN_o',
 'CHA_o',
 'CHL_o',
 'CLF_o',
 'CLI_o',
 'CMT_o',
 'COA_o',
 'CWH_o',
 'DAN_o',
 'DRA_o',
 'EAG_o',
 'ELK_o',
 'EMT_o',
 'FAR_o',
 'FCS_o',
 'FFD_o',
 'FRR_o',
 'FTH_o',
 'GLA_o',
 'GOS_o',
 'GRL_o',
 'HAR_o',
 'HDT_o',
 'HEB_o',
 'HER_o',
 'HGH_o',
 'HNF_o',
 'HOL_o',
 'HOO_o',
 'HVL_o',
 'IND_o',
 'INT_o',
 'KAY_o',
 'KMS_o',
 'KMT_o',
 'LAY_o',
 'LEH_o',
 'LIN_o',
 'MAP_o',
 'MID_o',
 'MLC_o',
 'MMT_o',
 'MRG_o',
 'MSL_o',
 'MUR_o',
 'MWY_o',
 'NOG_o',
 'NSL_o',
 'OGD_o',
 'OKL_o',
 'ORM_o',
 'PAY_o',
 'PGR_o',
 'PLN_o',
 'PRK_o',
 'PRY_o',
 'PVO_o',
 'PVW_o',
 'ROY_o',
 'RVD_o',
 'RVT_o',
 'SAN_o',
 'SAQ_o',
 'SAR_o',
 'SFK_o',
 'SJC_o',
 'SLC_o',
 'SLM_o',
 'SOG_o',
 'SPV_o',
 'SSL_o',
 'SUN_o',
 'SWE_o',
 'SYR_o',
 'TAY_o',
 'TOO_o',
 'UIN_o',
 'VIN_o',
 'WAT_o',
 'WBG_o',
 'WDL_o',
 'WEB_o',
 'WHT_o',
 'WHV_o',
 'WIL_o',
 'WJC_o',
 'WPT_o',
 'WVC_o',
 'WXC_o',
 'z03_o',
 'z11_o',
 'z23_o',


['AFK_d',
 'ALA_d',
 'ALP_d',
 'BDL_d',
 'BGM_d',
 'BNT_d',
 'BRT_d',
 'CDF_d',
 'CEN_d',
 'CHA_d',
 'CHL_d',
 'CLF_d',
 'CLI_d',
 'CMT_d',
 'COA_d',
 'CWH_d',
 'DAN_d',
 'DRA_d',
 'EAG_d',
 'ELK_d',
 'EMT_d',
 'FAR_d',
 'FCS_d',
 'FFD_d',
 'FRR_d',
 'FTH_d',
 'GLA_d',
 'GOS_d',
 'GRL_d',
 'HAR_d',
 'HDT_d',
 'HEB_d',
 'HER_d',
 'HGH_d',
 'HNF_d',
 'HOL_d',
 'HOO_d',
 'HVL_d',
 'IND_d',
 'INT_d',
 'KAY_d',
 'KMS_d',
 'KMT_d',
 'LAY_d',
 'LEH_d',
 'LIN_d',
 'MAP_d',
 'MID_d',
 'MLC_d',
 'MMT_d',
 'MRG_d',
 'MSL_d',
 'MUR_d',
 'MWY_d',
 'NOG_d',
 'NSL_d',
 'OGD_d',
 'OKL_d',
 'ORM_d',
 'PAY_d',
 'PGR_d',
 'PLN_d',
 'PRK_d',
 'PRY_d',
 'PVO_d',
 'PVW_d',
 'ROY_d',
 'RVD_d',
 'RVT_d',
 'SAN_d',
 'SAQ_d',
 'SAR_d',
 'SFK_d',
 'SJC_d',
 'SLC_d',
 'SLM_d',
 'SOG_d',
 'SPV_d',
 'SSL_d',
 'SUN_d',
 'SWE_d',
 'SYR_d',
 'TAY_d',
 'TOO_d',
 'UIN_d',
 'VIN_d',
 'WAT_d',
 'WBG_d',
 'WDL_d',
 'WEB_d',
 'WHT_d',
 'WHV_d',
 'WIL_d',
 'WJC_d',
 'WPT_d',
 'WVC_d',
 'WXC_d',
 'z03_d',
 'z11_d',
 'z23_d',


In [68]:
# block group
sdf_SLCommutePatterns_Percent_MU = sdf_SLCommutePatterns.copy()
sdf_SLCommutePatterns_tract_Percent_MU  = sdf_SLCommutePatterns_tract.copy()
sdf_SLCommutePatterns_sd_Percent_MU  = sdf_SLCommutePatterns_sd.copy()
sdf_SLCommutePatterns_City_Percent_MU  = sdf_SLCommutePatterns_City_Number.copy()

for x in dColCodesWCounty_x:   
    #display(x)
    sdf_SLCommutePatterns_Percent_MU      [x] = sdf_SLCommutePatterns_Percent_MU      [x] / sdf_SLCommutePatterns_Percent_MU      ['TTL_o'] * 100
    sdf_SLCommutePatterns_tract_Percent_MU[x] = sdf_SLCommutePatterns_tract_Percent_MU[x] / sdf_SLCommutePatterns_tract_Percent_MU['TTL_o'] * 100
    sdf_SLCommutePatterns_sd_Percent_MU   [x] = sdf_SLCommutePatterns_sd_Percent_MU   [x] / sdf_SLCommutePatterns_sd_Percent_MU   ['TTL_o'] * 100
    sdf_SLCommutePatterns_City_Percent_MU [x] = sdf_SLCommutePatterns_City_Percent_MU [x] / sdf_SLCommutePatterns_City_Percent_MU ['TTL_o'] * 100

for y in dColCodesWCounty_y:   
    #display(y)
    sdf_SLCommutePatterns_Percent_MU      [y] = sdf_SLCommutePatterns_Percent_MU      [y] / sdf_SLCommutePatterns_Percent_MU      ['TTL_d'] * 100
    sdf_SLCommutePatterns_tract_Percent_MU[y] = sdf_SLCommutePatterns_tract_Percent_MU[y] / sdf_SLCommutePatterns_tract_Percent_MU['TTL_d'] * 100
    sdf_SLCommutePatterns_sd_Percent_MU   [y] = sdf_SLCommutePatterns_sd_Percent_MU   [y] / sdf_SLCommutePatterns_sd_Percent_MU   ['TTL_d'] * 100    
    sdf_SLCommutePatterns_City_Percent_MU [y] = sdf_SLCommutePatterns_City_Percent_MU [y] / sdf_SLCommutePatterns_City_Percent_MU ['TTL_d'] * 100
    

In [69]:
#check that everything is near 100 (subtracting out non-city areas)
display(sdf_SLCommutePatterns_Percent_MU      .loc[:,dColCodesNoTotal_x].sum(axis=1))
display(sdf_SLCommutePatterns_tract_Percent_MU.loc[:,dColCodesNoTotal_x].sum(axis=1))
display(sdf_SLCommutePatterns_sd_Percent_MU   .loc[:,dColCodesNoTotal_x].sum(axis=1))
display(sdf_SLCommutePatterns_City_Percent_MU .loc[:,dColCodesNoTotal_x].sum(axis=1))

0       83.144813
1       88.156999
2       94.112900
3       94.397985
4       96.132334
          ...    
2014    79.214037
2015    84.028761
2016    82.451240
2017    82.735612
2018    84.781923
Length: 2019, dtype: float64

0      88.262911
1      80.329041
2      72.869955
3      81.793893
4      82.037037
         ...    
711    93.181818
712    90.677374
713    89.419355
714    93.160691
715     0.000000
Length: 716, dtype: float64

0      55.771195
1      71.462545
2      68.096345
3      65.017422
4      62.428571
         ...    
142     0.000000
143     0.000000
144     0.000000
145     0.000000
146     0.000000
Length: 147, dtype: float64

0     78.495597
1     63.157895
2     79.298677
3     89.590294
4     64.166052
        ...    
92    60.199005
93    92.252791
94    83.161004
95    91.980899
96    88.233786
Length: 97, dtype: float64

In [70]:
#export to GDB
deleteIfExists(fname_BlockGroupsWCommutePatterns_Percent_MU)
deleteIfExists(fname_TractsWCommutePatterns_Percent_MU     )
deleteIfExists(fname_SDWCommutePatterns_Percent_MU         )
deleteIfExists(fname_CitiesWCommutePatterns_Percent_MU     )

sdf_SLCommutePatterns_Percent_MU      .spatial.to_featureclass(fname_BlockGroupsWCommutePatterns_Percent_MU, sanitize_columns=False)
sdf_SLCommutePatterns_tract_Percent_MU.spatial.to_featureclass(fname_TractsWCommutePatterns_Percent_MU     , sanitize_columns=False)
sdf_SLCommutePatterns_sd_Percent_MU   .spatial.to_featureclass(fname_SDWCommutePatterns_Percent_MU         , sanitize_columns=False)
sdf_SLCommutePatterns_City_Percent_MU .spatial.to_featureclass(fname_CitiesWCommutePatterns_Percent_MU     , sanitize_columns=False)

'c:\\Users\\cday\\Documents\\projects\\Census-LEHD-Commute-Patterns\\results\\results2019\\SL\\SLCommutePatterns.gdb\\SL_City_CommutePatterns_Percent_MapUnit'

# Summarize by County

In [71]:
df_CityTownship_NameCode

NAME CODE3 zCOFIPS
0           Alpine   ALP     z49
1    American Fork   AFK     z49
2       Cedar Fort   CDF     z49
3      Cedar Hills   CHL     z49
4   Eagle Mountain   EAG     z49
..             ...   ...     ...
92      West Haven   WHV     z57
93     Grantsville   GRL     z45
94          Tooele   TOO     z45
95          Morgan   MRG     z29
96       Santaquin   SAQ     z23

[97 rows x 3 columns]

In [72]:
display(df_SLCommutePatterns_CityCalcsSum)
display(df_SLCommutePatterns_CityCalcsSum_Percent_SA)

index CODE3                        FIRST_NAME  AFK_o  ALA_o  ALP_o  \
0        0   AFK                     American Fork   4226      0    253   
1        1   ALA                              Alta      0      8      0   
2        2   ALP                            Alpine    282      0    366   
3        3   BDL                         Bluffdale     39      0     23   
4        4   BGM                      Brigham City      0      0      0   
..     ...   ...                               ...    ...    ...    ...   
121    121   z49        Utah County Unincorporated    953      0     88   
122    122   z51     Wasatch County Unincorporated      8      0      1   
123    123   z53  Washington County Unincorporated      0      0      0   
124    124   z55       Wayne County Unincorporated      0      0      0   
125    125   z57       Weber County Unincorporated      0      0      0   

     BDL_o  BGM_o  BNT_o  BRT_o  CDF_o  CEN_o  CHA_o  CHL_o  CLF_o  CLI_o  \
0       91      0      1      0      6      0      0    551      5      0   
1        0      0      0      3      0      0      0      0      0      0   
2       10      0      1      0      0      1      0    137      0      0   
3      636      5     13      0      0      4      0     16      5      3   
4        0   3345      2      0      0      1      0      0     39      1   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121     70      0      0      0     31      1      0    140      9      6   
122      0      0      1      0      0      0     97      0      1      0   
123      0      0      0      0      0      0      0      0      0      0   
124      0      0      0      0      0      0      0      0      0      0   
125      0     44     15      0      0      3      0      0    284     85   

     CMT_o  COA_o  CWH_o  DAN_o  DRA_o  EAG_o  ELK_o  EMT_o  FAR_o  FCS_o  \
0        0      0      6      0    376    506      4      0      4      0   
1        0      0     11      0      3      0      0      0      0      0   
2        0      0      4      0    161     29      0      0      0      0   
3        7      0     34      0    740     94      0      0      2      0   
4        0      0      3      0      0      0      0      0     10      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121      0      0     19      0    333    448    142      0      4      0   
122      6      7      2    161      5      2      1      1      0     54   
123      0      0      0      0      0      0      0      0      0      0   
124      0      0      0      0      0      0      0      0      0      0   
125      0      0      0      0      1      0      0      0     29      0   

     FFD_o  FRR_o  FTH_o  GLA_o  GOS_o  GRL_o  HAR_o  HDT_o  HEB_o  HER_o  \
0        6      0      3      3      0      0      0      0      3     82   
1        0      0      0      0      0      0      0      0      0      0   
2        0      0      0      0      1      0      0      0      0      0   
3        0      0      0      2      0      0      0      0      0    301   
4        0     58      5      0      0      0     48      0      0      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121     18      0      2    101     25      5      1      0      6     54   
122      0      0      0      0      0      0      0    103   1276      4   
123      0      0      0      0      0      0      0      0      0      0   
124      0      0      0      0      0      0      0      0      0      0   
125      0    233      6      0      0      0    220      0      0      0   

     HGH_o  HNF_o  HOL_o  HOO_o  HVL_o  IND_o  INT_o  KAY_o  KMS_o  KMT_o  \
0     1296      0      9      0      0      1      0      2      0      1   
1        0      0      4      0      0      0      0      0      0      0   
2      503      0      2      0      0      0      0      0      0      0   
3       88      0    

index CODE3                        FIRST_NAME         AFK_o     ALA_o  \
0        0   AFK                     American Fork  2.194439e+01  0.050433   
1        1   ALA                              Alta  2.916710e-05  1.655149   
2        2   ALP                            Alpine  1.489592e+00  0.070797   
3        3   BDL                         Bluffdale  2.249312e-01  0.042186   
4        4   BGM                      Brigham City  2.661305e-03  0.025033   
..     ...   ...                               ...           ...       ...   
121    121   z49        Utah County Unincorporated  5.274267e+00  0.588559   
122    122   z51     Wasatch County Unincorporated  6.699262e-02  0.029749   
123    123   z53  Washington County Unincorporated  9.414146e-03  0.000009   
124    124   z55       Wayne County Unincorporated  3.582034e-13  0.000000   
125    125   z57       Weber County Unincorporated  1.096366e-02  0.048185   

         ALP_o         BDL_o      BGM_o     BNT_o     BRT_o         CDF_o  \
0    10.216236  1.270656e+00   0.004621  0.046022  0.057180  4.737225e+00   
1     0.006039  7.022072e-04   0.000361  0.001686  1.373485  8.815033e-09   
2    14.317934  1.736442e-01   0.001274  0.010048  0.086801  1.421459e-01   
3     0.939282  7.751560e+00   0.070053  0.086359  0.028575  7.815384e-03   
4     0.000000  5.771513e-03  45.001026  0.026700  0.029207  4.015785e-04   
..         ...           ...        ...       ...       ...           ...   
121   4.492137  1.202491e+00   0.004192  0.032959  0.764364  1.709509e+01   
122   0.108537  2.980952e-02   0.001671  0.020139  0.004925  2.071192e-03   
123   0.017803  1.480598e-02   0.005080  0.012543  0.000020  0.000000e+00   
124   0.003547  5.602950e-08   0.000000  0.000000  0.000000  0.000000e+00   
125   0.001667  1.082886e-02   0.782198  0.145567  0.031240  9.542189e-07   

        CEN_o      CHA_o      CHL_o     CLF_o         CLI_o         CMT_o  \
0    0.067779   0.386504  15.052492  0.029645  8.962469e-03  3.137975e-02   
1    0.003692   0.000019   0.001707  0.000159  2.177564e-07  2.961122e-08   
2    0.023757   0.016668   3.769390  0.005761  1.382080e-09  4.005802e-02   
3    0.096164   0.138419   0.469253  0.027094  3.897352e-02  1.514221e+00   
4    0.054430   0.000252   0.001371  0.183000  5.067111e-02  5.424828e-11   
..        ...        ...        ...       ...           ...           ...   
121  0.082732   0.384827   4.435084  0.052384  7.441121e-02  2.820070e-01   
122  0.014293  20.984946   0.007804  0.007771  3.848076e-03  1.375365e+00   
123  0.013970   0.099749   0.026741  0.001491  9.270932e-03  3.134387e-03   
124  0.000000   0.000000   0.000000  0.000001  0.000000e+00  1.980873e-02   
125  0.144855   0.024686   0.000612  1.213563  1.154928e+00  3.513017e-03   

            COA_o         CWH_o      DAN_o         DRA_o     EAG_o  \
0    2.265570e-06  1.124670e-01   0.269484  1.339550e+00  4.653346   
1    1.788682e-07  1.046568e-01   0.000009  1.344183e-02  0.001214   
2    1.149345e-08  5.797904e-02   0.004628  5.745486e-01  0.299311   
3    2.237350e-03  3.066167e-01   0.022406  2.563970e+00  0.888885   
4    3.615213e-03  3.215724e-02   0.000641  3.752076e-03  0.001658   
..            ...           ...        ...           ...       ...   
121  1.564430e-02  3.036948e-01   0.169548  1.344440e+00  4.457412   
122  1.355726e+00  4.248438e-02  20.934281  2.821024e-02  0.047250   
123  5.493972e-02  1.521014e-02   0.032083  1.518456e-02  0.007487   
124  0.000000e+00  3.165068e-13   0.000000  7.968920e-09  0.000000   
125  1.466197e-01  1.627343e-02   0.034062  2.415121e-02  0.007429   

            ELK_o     EMT_o         FAR_o         FCS_o      FFD_o     FRR_o  \
0    9.704328e-01  0.045418  7.982506e-02  8.651033e-10   7.385884  0.023138   
1    3.344938e-04  0.008295  2.195284e-03  6.391057e-09   0.000000  0.000019   
2    8.497877e-03  0.345949  9.285979e-03  1.130721e-02   0.179241  0.000715   
3    4.213758e-02  0.199037  4.203262e-02  1.990007e-02  

In [73]:
df_CitySum_wCounty_Join            = pd.DataFrame.merge(df_SLCommutePatterns_CityCalcsSum           , df_CityTownship_NameCode, on="CODE3", how="left")
df_CitySum_wCounty_Join_Percent_SA = pd.DataFrame.merge(df_SLCommutePatterns_CityCalcsSum_Percent_SA, df_CityTownship_NameCode, on="CODE3", how="left")

df_CitySum_wCounty_Join           .loc[df_CitySum_wCounty_Join           .CODE3.str[0] == 'z', 'zCOFIPS'] = df_CitySum_wCounty_Join           .CODE3
df_CitySum_wCounty_Join_Percent_SA.loc[df_CitySum_wCounty_Join_Percent_SA.CODE3.str[0] == 'z', 'zCOFIPS'] = df_CitySum_wCounty_Join_Percent_SA.CODE3

display(df_CitySum_wCounty_Join)
display(df_CitySum_wCounty_Join_Percent_SA)

index CODE3                        FIRST_NAME  AFK_o  ALA_o  ALP_o  \
0        0   AFK                     American Fork   4226      0    253   
1        1   ALA                              Alta      0      8      0   
2        2   ALP                            Alpine    282      0    366   
3        3   BDL                         Bluffdale     39      0     23   
4        4   BGM                      Brigham City      0      0      0   
..     ...   ...                               ...    ...    ...    ...   
121    121   z49        Utah County Unincorporated    953      0     88   
122    122   z51     Wasatch County Unincorporated      8      0      1   
123    123   z53  Washington County Unincorporated      0      0      0   
124    124   z55       Wayne County Unincorporated      0      0      0   
125    125   z57       Weber County Unincorporated      0      0      0   

     BDL_o  BGM_o  BNT_o  BRT_o  CDF_o  CEN_o  CHA_o  CHL_o  CLF_o  CLI_o  \
0       91      0      1      0      6      0      0    551      5      0   
1        0      0      0      3      0      0      0      0      0      0   
2       10      0      1      0      0      1      0    137      0      0   
3      636      5     13      0      0      4      0     16      5      3   
4        0   3345      2      0      0      1      0      0     39      1   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121     70      0      0      0     31      1      0    140      9      6   
122      0      0      1      0      0      0     97      0      1      0   
123      0      0      0      0      0      0      0      0      0      0   
124      0      0      0      0      0      0      0      0      0      0   
125      0     44     15      0      0      3      0      0    284     85   

     CMT_o  COA_o  CWH_o  DAN_o  DRA_o  EAG_o  ELK_o  EMT_o  FAR_o  FCS_o  \
0        0      0      6      0    376    506      4      0      4      0   
1        0      0     11      0      3      0      0      0      0      0   
2        0      0      4      0    161     29      0      0      0      0   
3        7      0     34      0    740     94      0      0      2      0   
4        0      0      3      0      0      0      0      0     10      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121      0      0     19      0    333    448    142      0      4      0   
122      6      7      2    161      5      2      1      1      0     54   
123      0      0      0      0      0      0      0      0      0      0   
124      0      0      0      0      0      0      0      0      0      0   
125      0      0      0      0      1      0      0      0     29      0   

     FFD_o  FRR_o  FTH_o  GLA_o  GOS_o  GRL_o  HAR_o  HDT_o  HEB_o  HER_o  \
0        6      0      3      3      0      0      0      0      3     82   
1        0      0      0      0      0      0      0      0      0      0   
2        0      0      0      0      1      0      0      0      0      0   
3        0      0      0      2      0      0      0      0      0    301   
4        0     58      5      0      0      0     48      0      0      0   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
121     18      0      2    101     25      5      1      0      6     54   
122      0      0      0      0      0      0      0    103   1276      4   
123      0      0      0      0      0      0      0      0      0      0   
124      0      0      0      0      0      0      0      0      0      0   
125      0    233      6      0      0      0    220      0      0      0   

     HGH_o  HNF_o  HOL_o  HOO_o  HVL_o  IND_o  INT_o  KAY_o  KMS_o  KMT_o  \
0     1296      0      9      0      0      1      0      2      0      1   
1        0      0      4      0      0      0      0      0      0      0   
2      503      0      2      0      0      0      0      0      0      0   
3       88      0    

index CODE3                        FIRST_NAME         AFK_o     ALA_o  \
0        0   AFK                     American Fork  2.194439e+01  0.050433   
1        1   ALA                              Alta  2.916710e-05  1.655149   
2        2   ALP                            Alpine  1.489592e+00  0.070797   
3        3   BDL                         Bluffdale  2.249312e-01  0.042186   
4        4   BGM                      Brigham City  2.661305e-03  0.025033   
..     ...   ...                               ...           ...       ...   
121    121   z49        Utah County Unincorporated  5.274267e+00  0.588559   
122    122   z51     Wasatch County Unincorporated  6.699262e-02  0.029749   
123    123   z53  Washington County Unincorporated  9.414146e-03  0.000009   
124    124   z55       Wayne County Unincorporated  3.582034e-13  0.000000   
125    125   z57       Weber County Unincorporated  1.096366e-02  0.048185   

         ALP_o         BDL_o      BGM_o     BNT_o     BRT_o         CDF_o  \
0    10.216236  1.270656e+00   0.004621  0.046022  0.057180  4.737225e+00   
1     0.006039  7.022072e-04   0.000361  0.001686  1.373485  8.815033e-09   
2    14.317934  1.736442e-01   0.001274  0.010048  0.086801  1.421459e-01   
3     0.939282  7.751560e+00   0.070053  0.086359  0.028575  7.815384e-03   
4     0.000000  5.771513e-03  45.001026  0.026700  0.029207  4.015785e-04   
..         ...           ...        ...       ...       ...           ...   
121   4.492137  1.202491e+00   0.004192  0.032959  0.764364  1.709509e+01   
122   0.108537  2.980952e-02   0.001671  0.020139  0.004925  2.071192e-03   
123   0.017803  1.480598e-02   0.005080  0.012543  0.000020  0.000000e+00   
124   0.003547  5.602950e-08   0.000000  0.000000  0.000000  0.000000e+00   
125   0.001667  1.082886e-02   0.782198  0.145567  0.031240  9.542189e-07   

        CEN_o      CHA_o      CHL_o     CLF_o         CLI_o         CMT_o  \
0    0.067779   0.386504  15.052492  0.029645  8.962469e-03  3.137975e-02   
1    0.003692   0.000019   0.001707  0.000159  2.177564e-07  2.961122e-08   
2    0.023757   0.016668   3.769390  0.005761  1.382080e-09  4.005802e-02   
3    0.096164   0.138419   0.469253  0.027094  3.897352e-02  1.514221e+00   
4    0.054430   0.000252   0.001371  0.183000  5.067111e-02  5.424828e-11   
..        ...        ...        ...       ...           ...           ...   
121  0.082732   0.384827   4.435084  0.052384  7.441121e-02  2.820070e-01   
122  0.014293  20.984946   0.007804  0.007771  3.848076e-03  1.375365e+00   
123  0.013970   0.099749   0.026741  0.001491  9.270932e-03  3.134387e-03   
124  0.000000   0.000000   0.000000  0.000001  0.000000e+00  1.980873e-02   
125  0.144855   0.024686   0.000612  1.213563  1.154928e+00  3.513017e-03   

            COA_o         CWH_o      DAN_o         DRA_o     EAG_o  \
0    2.265570e-06  1.124670e-01   0.269484  1.339550e+00  4.653346   
1    1.788682e-07  1.046568e-01   0.000009  1.344183e-02  0.001214   
2    1.149345e-08  5.797904e-02   0.004628  5.745486e-01  0.299311   
3    2.237350e-03  3.066167e-01   0.022406  2.563970e+00  0.888885   
4    3.615213e-03  3.215724e-02   0.000641  3.752076e-03  0.001658   
..            ...           ...        ...           ...       ...   
121  1.564430e-02  3.036948e-01   0.169548  1.344440e+00  4.457412   
122  1.355726e+00  4.248438e-02  20.934281  2.821024e-02  0.047250   
123  5.493972e-02  1.521014e-02   0.032083  1.518456e-02  0.007487   
124  0.000000e+00  3.165068e-13   0.000000  7.968920e-09  0.000000   
125  1.466197e-01  1.627343e-02   0.034062  2.415121e-02  0.007429   

            ELK_o     EMT_o         FAR_o         FCS_o      FFD_o     FRR_o  \
0    9.704328e-01  0.045418  7.982506e-02  8.651033e-10   7.385884  0.023138   
1    3.344938e-04  0.008295  2.195284e-03  6.391057e-09   0.000000  0.000019   
2    8.497877e-03  0.345949  9.285979e-03  1.130721e-02   0.179241  0.000715   
3    4.213758e-02  0.199037  4.203262e-02  1.990007e-02  

In [74]:
dColCodesWCounty

['AFK_o',
 'ALA_o',
 'ALP_o',
 'BDL_o',
 'BGM_o',
 'BNT_o',
 'BRT_o',
 'CDF_o',
 'CEN_o',
 'CHA_o',
 'CHL_o',
 'CLF_o',
 'CLI_o',
 'CMT_o',
 'COA_o',
 'CWH_o',
 'DAN_o',
 'DRA_o',
 'EAG_o',
 'ELK_o',
 'EMT_o',
 'FAR_o',
 'FCS_o',
 'FFD_o',
 'FRR_o',
 'FTH_o',
 'GLA_o',
 'GOS_o',
 'GRL_o',
 'HAR_o',
 'HDT_o',
 'HEB_o',
 'HER_o',
 'HGH_o',
 'HNF_o',
 'HOL_o',
 'HOO_o',
 'HVL_o',
 'IND_o',
 'INT_o',
 'KAY_o',
 'KMS_o',
 'KMT_o',
 'LAY_o',
 'LEH_o',
 'LIN_o',
 'MAP_o',
 'MID_o',
 'MLC_o',
 'MMT_o',
 'MRG_o',
 'MSL_o',
 'MUR_o',
 'MWY_o',
 'NOG_o',
 'NSL_o',
 'OGD_o',
 'OKL_o',
 'ORM_o',
 'PAY_o',
 'PGR_o',
 'PLN_o',
 'PRK_o',
 'PRY_o',
 'PVO_o',
 'PVW_o',
 'ROY_o',
 'RVD_o',
 'RVT_o',
 'SAN_o',
 'SAQ_o',
 'SAR_o',
 'SFK_o',
 'SJC_o',
 'SLC_o',
 'SLM_o',
 'SOG_o',
 'SPV_o',
 'SSL_o',
 'SUN_o',
 'SWE_o',
 'SYR_o',
 'TAY_o',
 'TOO_o',
 'UIN_o',
 'VIN_o',
 'WAT_o',
 'WBG_o',
 'WDL_o',
 'WEB_o',
 'WHT_o',
 'WHV_o',
 'WIL_o',
 'WJC_o',
 'WPT_o',
 'WVC_o',
 'WXC_o',
 'TTL_o',
 'AFK_d',
 'ALA_d',


In [75]:
df_CountySum            = df_CitySum_wCounty_Join           .groupby(['zCOFIPS'])[dColCodesWCounty].apply(lambda x : x.astype(int  ).sum())
df_CountySum_Percent_SA = df_CitySum_wCounty_Join_Percent_SA.groupby(['zCOFIPS'])[dColCodesWCounty].apply(lambda x : x.astype(float).sum())

df_CountySum            = df_CountySum           .reset_index()
df_CountySum_Percent_SA = df_CountySum_Percent_SA.reset_index()

display(df_CountySum)
display(df_CountySum_Percent_SA)

zCOFIPS  AFK_o  ALA_o  ALP_o  BDL_o  BGM_o  BNT_o  BRT_o  CDF_o  CEN_o  \
0      z01      0      0      0      0      0      0      0      0      0   
1      z03      0      0      0      6   6035     16      0      0      8   
2      z05      0      0      0      1    252      2      0      0      0   
3      z07      0      0      0      0      0      0      0      0      0   
4      z09      0      0      0      0      0      0      0      0      0   
5      z11     42      0      2     58    132  13115      0      2   4187   
6      z13      0      0      0      0      0      0      0      0      0   
7      z15      0      0      0      0      0      0      0      0      0   
8      z17      0      0      0      0      0      0      0      0      0   
9      z19      0      0      0      0      0      0      0      0      0   
10     z21      0      0      0      0      0      0      0      0      0   
11     z23     33      0      0      1      0      0      0      0      0   
12     z25      0      0      0      0      0      0      0      0      0   
13     z27      0      0      0      0      0      0      0      0      0   
14     z29      0      0      0      0      0     14      0      0      1   
15     z31      0      0      0      0      0      0      0      0      0   
16     z33      0      0      0      0      0      0      0      0      0   
17     z35   1605    319    338   6110     45   4001    118     14   1147   
18     z37      0      0      0      0      0      0      0      0      0   
19     z39      1      0      0      0      0      0      0      0      0   
20     z41      1      0      0      0      0      0      0      0      0   
21     z43      2      0      3      4      2      8      0      0      4   
22     z45      7      0      0     10      0     26      0      0      1   
23     z47      0      0      0      0      0      0      0      0      0   
24     z49  16896      6   1923   1414      0     62      0    123     32   
25     z51     19      0      1      1      0      6      0      0      0   
26     z53      0      0      0      0      0      0      0      0      0   
27     z55      0      0      0      0      0      0      0      0      0   
28     z57     10      0      2     17    744    337      0      0    132   

    CHA_o  CHL_o  CLF_o  CLI_o  CMT_o  COA_o  CWH_o  DAN_o  DRA_o  EAG_o  \
0       0      0      0      0      0      0      0      0      0      0   
1       0      0    208     18      0      0      5      0     11      0   
2       0      0     69      1      0      0      1      0      2      0   
3       0      0      0      0      0      0      0      0      0      0   
4       0      0      0      0      0      0      0      0      0      0   
5       0      1  17911   5742      1      3    177      0    355     30   
6       0      0      0      0      0      0      0      1      0      0   
7       0      0      0      0      0      0      0      0      0      0   
8       0      0      0      0      0      0      0      0      0      0   
9       0      0      0      0      0      0      0      0      0      0   
10      0      0      0      0      0      0      0      0      0      0   
11      0      0      0      0      0      0      8      0     12      3   
12      0      0      0      0      0      0      0      0      0      0   
13      0      0      0      0      0      0      0      0      0      0   
14      0      0     85      2      0     14      0      0      9      0   
15      0      0      0      0      0      0      0      0      0      0   
16      0      0      0      0      0      0      0      0      0      0   
17     12    318   1348    673    300     16  10622     17  21965   2278   
18      0      0      0      0      0      0      0      0      0      0   
19      0      0      0      0      0      0      0      0      0      0   
20      0      0      0      0      0      0      0      0      0      0   
21     34      1    

zCOFIPS         AFK_o         ALA_o         ALP_o         BDL_o  \
0      z01  8.646107e-09  0.000000e+00  1.748631e-04  1.117098e-03   
1      z03  5.859127e-03  6.201182e-02  8.803472e-09  9.671171e-02   
2      z05  6.883026e-03  5.515573e-02  2.633893e-02  2.938722e-02   
3      z07  5.757124e-04  0.000000e+00  6.696568e-03  2.251203e-03   
4      z09  2.838629e-15  0.000000e+00  0.000000e+00  2.228187e-03   
5      z11  4.497793e-01  1.369261e+00  3.901007e-01  1.302436e+00   
6      z13  1.271664e-03  5.945875e-07  6.664653e-11  1.176536e-03   
7      z15  6.730276e-07  0.000000e+00  3.154000e-07  3.442715e-08   
8      z17  0.000000e+00  0.000000e+00  9.852255e-07  1.099806e-06   
9      z19  4.780630e-04  0.000000e+00  0.000000e+00  6.153620e-07   
10     z21  1.914688e-03  5.140368e-06  9.199713e-11  3.155978e-03   
11     z23  2.121968e-01  4.009135e-05  3.736134e-02  4.865395e-02   
12     z25  3.221947e-14  0.000000e+00  0.000000e+00  6.110278e-09   
13     z27  1.533926e-03  0.000000e+00  6.503541e-08  1.119852e-03   
14     z29  1.672676e-03  1.292610e-01  5.343492e-06  1.569796e-02   
15     z31  0.000000e+00  0.000000e+00  5.666953e-10  2.234718e-03   
16     z33  1.646858e-06  4.808404e-06  4.865452e-10  1.117749e-03   
17     z35  9.809071e+00  9.278025e+01  1.764755e+01  7.806164e+01   
18     z37  4.781486e-04  0.000000e+00  5.119436e-07  0.000000e+00   
19     z39  2.100697e-02  3.245493e-08  1.429383e-02  1.350357e-02   
20     z41  1.194134e-02  0.000000e+00  4.346870e-08  2.466438e-07   
21     z43  3.567241e-02  7.859700e-01  1.672895e-01  1.097201e-01   
22     z45  8.030070e-02  2.950399e-01  5.849195e-02  2.674386e-01   
23     z47  7.947773e-09  0.000000e+00  3.547794e-03  1.678888e-06   
24     z49  8.912087e+01  4.318936e+00  8.135575e+01  1.963012e+01   
25     z51  1.610661e-01  5.553053e-02  1.706598e-01  6.758099e-02   
26     z53  9.414146e-03  9.478834e-06  1.780254e-02  1.480598e-02   
27     z55  3.582034e-13  0.000000e+00  3.547094e-03  5.602950e-08   
28     z57  1.366888e-01  2.160209e-01  1.689572e-01  3.925808e-01   

           BGM_o         BNT_o         BRT_o         CDF_o         CEN_o  \
0   6.978619e-09  9.979220e-04  0.000000e+00  0.000000e+00  0.000000e+00   
1   8.129881e+01  1.410622e-01  4.579910e-02  4.015785e-04  2.837057e-01   
2   3.831139e+00  6.373370e-02  8.551230e-02  3.673876e-04  5.969232e-02   
3   0.000000e+00  1.515196e-03  0.000000e+00  0.000000e+00  0.000000e+00   
4   0.000000e+00  2.069216e-13  0.000000e+00  0.000000e+00  6.353191e-13   
5   2.573631e+00  7.265308e+01  1.501353e+00  2.344660e+00  7.276740e+01   
6   1.238897e-03  5.075268e-04  1.641645e-07  0.000000e+00  1.560721e-07   
7   0.000000e+00  1.525148e-07  0.000000e+00  0.000000e+00  1.750949e-11   
8   0.000000e+00  8.564700e-10  0.000000e+00  0.000000e+00  0.000000e+00   
9   0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
10  1.950370e-03  3.979738e-04  0.000000e+00  0.000000e+00  1.551599e-03   
11  1.708886e-03  3.006384e-03  8.284268e-05  7.131450e-04  1.897139e-03   
12  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
13  1.481208e-09  5.055854e-04  0.000000e+00  3.296585e-06  1.552331e-03   
14  1.262096e-02  9.649923e-02  2.557634e-01  4.486452e-10  4.981679e-02   
15  2.366094e-08  1.849682e-08  0.000000e+00  0.000000e+00  0.000000e+00   
16  3.396334e-07  4.942507e-04  9.803564e-06  0.000000e+00  1.553802e-03   
17  9.848515e-01  2.372337e+01  9.283303e+01  1.365807e+01  2.234096e+01   
18  0.000000e+00  5.045334e-04  0.000000e+00  0.000000e+00  0.000000e+00   
19  1.239125e-03  1.692190e-03  6.706318e-08  1.512250e-03  1.553656e-03   
20  1.238936e-03  5.057777e-04  0.000000e+00  0.000000e+00  1.552667e-03   
21  4.115895e-02  8.583177e-02  1.204019e+00  2.641963e-01  9.842350e-02   
22  1.284120e-02  2.103136e-01  4.498899e-01  6.063921e-01  1.184151e-01   
23  2.477871e-03  5.054641e-04  0.000000e+00  0.000000e+00  1.551663e-03   
24

In [76]:
df_CountySum           ['WFCounty'] = "Outside Wasatch Front"
df_CountySum_Percent_SA['WFCounty'] = "Outside Wasatch Front"

df_CountySum           .loc[df_CountySum.zCOFIPS == 'z11', 'WFCounty'] = "Davis County"
df_CountySum           .loc[df_CountySum.zCOFIPS == 'z57', 'WFCounty'] = "Weber County"
df_CountySum           .loc[df_CountySum.zCOFIPS == 'z35', 'WFCounty'] = "Salt Lake County"
df_CountySum           .loc[df_CountySum.zCOFIPS == 'z49', 'WFCounty'] = "Utah County"

df_CountySum_Percent_SA.loc[df_CountySum.zCOFIPS == 'z11', 'WFCounty'] = "Davis County"
df_CountySum_Percent_SA.loc[df_CountySum.zCOFIPS == 'z57', 'WFCounty'] = "Weber County"
df_CountySum_Percent_SA.loc[df_CountySum.zCOFIPS == 'z35', 'WFCounty'] = "Salt Lake County"
df_CountySum_Percent_SA.loc[df_CountySum.zCOFIPS == 'z49', 'WFCounty'] = "Utah County"

display(df_CountySum)
display(df_CountySum_Percent_SA)

zCOFIPS  AFK_o  ALA_o  ALP_o  BDL_o  BGM_o  BNT_o  BRT_o  CDF_o  CEN_o  \
0      z01      0      0      0      0      0      0      0      0      0   
1      z03      0      0      0      6   6035     16      0      0      8   
2      z05      0      0      0      1    252      2      0      0      0   
3      z07      0      0      0      0      0      0      0      0      0   
4      z09      0      0      0      0      0      0      0      0      0   
5      z11     42      0      2     58    132  13115      0      2   4187   
6      z13      0      0      0      0      0      0      0      0      0   
7      z15      0      0      0      0      0      0      0      0      0   
8      z17      0      0      0      0      0      0      0      0      0   
9      z19      0      0      0      0      0      0      0      0      0   
10     z21      0      0      0      0      0      0      0      0      0   
11     z23     33      0      0      1      0      0      0      0      0   
12     z25      0      0      0      0      0      0      0      0      0   
13     z27      0      0      0      0      0      0      0      0      0   
14     z29      0      0      0      0      0     14      0      0      1   
15     z31      0      0      0      0      0      0      0      0      0   
16     z33      0      0      0      0      0      0      0      0      0   
17     z35   1605    319    338   6110     45   4001    118     14   1147   
18     z37      0      0      0      0      0      0      0      0      0   
19     z39      1      0      0      0      0      0      0      0      0   
20     z41      1      0      0      0      0      0      0      0      0   
21     z43      2      0      3      4      2      8      0      0      4   
22     z45      7      0      0     10      0     26      0      0      1   
23     z47      0      0      0      0      0      0      0      0      0   
24     z49  16896      6   1923   1414      0     62      0    123     32   
25     z51     19      0      1      1      0      6      0      0      0   
26     z53      0      0      0      0      0      0      0      0      0   
27     z55      0      0      0      0      0      0      0      0      0   
28     z57     10      0      2     17    744    337      0      0    132   

    CHA_o  CHL_o  CLF_o  CLI_o  CMT_o  COA_o  CWH_o  DAN_o  DRA_o  EAG_o  \
0       0      0      0      0      0      0      0      0      0      0   
1       0      0    208     18      0      0      5      0     11      0   
2       0      0     69      1      0      0      1      0      2      0   
3       0      0      0      0      0      0      0      0      0      0   
4       0      0      0      0      0      0      0      0      0      0   
5       0      1  17911   5742      1      3    177      0    355     30   
6       0      0      0      0      0      0      0      1      0      0   
7       0      0      0      0      0      0      0      0      0      0   
8       0      0      0      0      0      0      0      0      0      0   
9       0      0      0      0      0      0      0      0      0      0   
10      0      0      0      0      0      0      0      0      0      0   
11      0      0      0      0      0      0      8      0     12      3   
12      0      0      0      0      0      0      0      0      0      0   
13      0      0      0      0      0      0      0      0      0      0   
14      0      0     85      2      0     14      0      0      9      0   
15      0      0      0      0      0      0      0      0      0      0   
16      0      0      0      0      0      0      0      0      0      0   
17     12    318   1348    673    300     16  10622     17  21965   2278   
18      0      0      0      0      0      0      0      0      0      0   
19      0      0      0      0      0      0      0      0      0      0   
20      0      0      0      0      0      0      0      0      0      0   
21     34      1    

zCOFIPS         AFK_o         ALA_o         ALP_o         BDL_o  \
0      z01  8.646107e-09  0.000000e+00  1.748631e-04  1.117098e-03   
1      z03  5.859127e-03  6.201182e-02  8.803472e-09  9.671171e-02   
2      z05  6.883026e-03  5.515573e-02  2.633893e-02  2.938722e-02   
3      z07  5.757124e-04  0.000000e+00  6.696568e-03  2.251203e-03   
4      z09  2.838629e-15  0.000000e+00  0.000000e+00  2.228187e-03   
5      z11  4.497793e-01  1.369261e+00  3.901007e-01  1.302436e+00   
6      z13  1.271664e-03  5.945875e-07  6.664653e-11  1.176536e-03   
7      z15  6.730276e-07  0.000000e+00  3.154000e-07  3.442715e-08   
8      z17  0.000000e+00  0.000000e+00  9.852255e-07  1.099806e-06   
9      z19  4.780630e-04  0.000000e+00  0.000000e+00  6.153620e-07   
10     z21  1.914688e-03  5.140368e-06  9.199713e-11  3.155978e-03   
11     z23  2.121968e-01  4.009135e-05  3.736134e-02  4.865395e-02   
12     z25  3.221947e-14  0.000000e+00  0.000000e+00  6.110278e-09   
13     z27  1.533926e-03  0.000000e+00  6.503541e-08  1.119852e-03   
14     z29  1.672676e-03  1.292610e-01  5.343492e-06  1.569796e-02   
15     z31  0.000000e+00  0.000000e+00  5.666953e-10  2.234718e-03   
16     z33  1.646858e-06  4.808404e-06  4.865452e-10  1.117749e-03   
17     z35  9.809071e+00  9.278025e+01  1.764755e+01  7.806164e+01   
18     z37  4.781486e-04  0.000000e+00  5.119436e-07  0.000000e+00   
19     z39  2.100697e-02  3.245493e-08  1.429383e-02  1.350357e-02   
20     z41  1.194134e-02  0.000000e+00  4.346870e-08  2.466438e-07   
21     z43  3.567241e-02  7.859700e-01  1.672895e-01  1.097201e-01   
22     z45  8.030070e-02  2.950399e-01  5.849195e-02  2.674386e-01   
23     z47  7.947773e-09  0.000000e+00  3.547794e-03  1.678888e-06   
24     z49  8.912087e+01  4.318936e+00  8.135575e+01  1.963012e+01   
25     z51  1.610661e-01  5.553053e-02  1.706598e-01  6.758099e-02   
26     z53  9.414146e-03  9.478834e-06  1.780254e-02  1.480598e-02   
27     z55  3.582034e-13  0.000000e+00  3.547094e-03  5.602950e-08   
28     z57  1.366888e-01  2.160209e-01  1.689572e-01  3.925808e-01   

           BGM_o         BNT_o         BRT_o         CDF_o         CEN_o  \
0   6.978619e-09  9.979220e-04  0.000000e+00  0.000000e+00  0.000000e+00   
1   8.129881e+01  1.410622e-01  4.579910e-02  4.015785e-04  2.837057e-01   
2   3.831139e+00  6.373370e-02  8.551230e-02  3.673876e-04  5.969232e-02   
3   0.000000e+00  1.515196e-03  0.000000e+00  0.000000e+00  0.000000e+00   
4   0.000000e+00  2.069216e-13  0.000000e+00  0.000000e+00  6.353191e-13   
5   2.573631e+00  7.265308e+01  1.501353e+00  2.344660e+00  7.276740e+01   
6   1.238897e-03  5.075268e-04  1.641645e-07  0.000000e+00  1.560721e-07   
7   0.000000e+00  1.525148e-07  0.000000e+00  0.000000e+00  1.750949e-11   
8   0.000000e+00  8.564700e-10  0.000000e+00  0.000000e+00  0.000000e+00   
9   0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
10  1.950370e-03  3.979738e-04  0.000000e+00  0.000000e+00  1.551599e-03   
11  1.708886e-03  3.006384e-03  8.284268e-05  7.131450e-04  1.897139e-03   
12  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00  0.000000e+00   
13  1.481208e-09  5.055854e-04  0.000000e+00  3.296585e-06  1.552331e-03   
14  1.262096e-02  9.649923e-02  2.557634e-01  4.486452e-10  4.981679e-02   
15  2.366094e-08  1.849682e-08  0.000000e+00  0.000000e+00  0.000000e+00   
16  3.396334e-07  4.942507e-04  9.803564e-06  0.000000e+00  1.553802e-03   
17  9.848515e-01  2.372337e+01  9.283303e+01  1.365807e+01  2.234096e+01   
18  0.000000e+00  5.045334e-04  0.000000e+00  0.000000e+00  0.000000e+00   
19  1.239125e-03  1.692190e-03  6.706318e-08  1.512250e-03  1.553656e-03   
20  1.238936e-03  5.057777e-04  0.000000e+00  0.000000e+00  1.552667e-03   
21  4.115895e-02  8.583177e-02  1.204019e+00  2.641963e-01  9.842350e-02   
22  1.284120e-02  2.103136e-01  4.498899e-01  6.063921e-01  1.184151e-01   
23  2.477871e-03  5.054641e-04  0.000000e+00  0.000000e+00  1.551663e-03   
24

In [77]:
df_CountySum_wOutWF            = df_CountySum           .groupby(['WFCounty'])[dColCodesWCounty].apply(lambda x : x.astype(int  ).sum())
df_CountySum_wOutWF_Percent_SA = df_CountySum_Percent_SA.groupby(['WFCounty'])[dColCodesWCounty].apply(lambda x : x.astype(float).sum())

df_CountySum_wOutWF            = df_CountySum_wOutWF.reset_index()
df_CountySum_wOutWF_Percent_SA = df_CountySum_wOutWF_Percent_SA.reset_index()

display(df_CountySum_wOutWF)
display(df_CountySum_wOutWF_Percent_SA)

WFCounty  AFK_o  ALA_o  ALP_o  BDL_o  BGM_o  BNT_o  BRT_o  \
0           Davis County     42      0      2     58    132  13115      0   
1  Outside Wasatch Front     63      0      4     23   6289     72      0   
2       Salt Lake County   1605    319    338   6110     45   4001    118   
3            Utah County  16896      6   1923   1414      0     62      0   
4           Weber County     10      0      2     17    744    337      0   

   CDF_o  CEN_o  CHA_o  CHL_o  CLF_o  CLI_o  CMT_o  COA_o  CWH_o  DAN_o  \
0      2   4187      0      1  17911   5742      1      3    177      0   
1      0     14    374      6    393     32     29    581    125    700   
2     14   1147     12    318   1348    673    300     16  10622     17   
3    123     32     29   3129     38     10      3      1    257     19   
4      0    132      0      1   5131   2131      0      0     37      0   

   DRA_o  EAG_o  ELK_o  EMT_o  FAR_o  FCS_o  FFD_o  FRR_o  FTH_o  GLA_o  \
0    355     30      0      2   7061      0      2    465   2604      0   
1    151     66     16      6     39    831      0    171     17     60   
2  21965   2278     43    165   1584     25     10     79    448     12   
3   5568   8170    856      4     39      7     66      4     19    368   
4     61     16      0      0    529      0      0   3196    171      0   

   GOS_o  GRL_o  HAR_o  HDT_o  HEB_o  HER_o  HGH_o  HNF_o  HOL_o  HOO_o  \
0      0     33    389      0      7     69     16      0    199   1027   
1      6   5435    145    487   4942     43      7    434    114     49   
2      3    877     55     51    176  14791   1316      6   9420    156   
3     46     24      5      6    139    843   6510      0    202      1   
4      0      3   3604      0      0      1      4     13     29   3284   

   HVL_o  IND_o  INT_o  KAY_o  KMS_o  KMT_o  LAY_o  LEH_o  LIN_o  MAP_o  \
0     24      0      0  11068      0    107  26629    110     16      0   
1     17    850    337     77   1028     65    250     88     66      0   
2     19     73     10   1997     38   9438   3209   5577    495     73   
3      0     26     13     47      7     90     72  21046   6869   2768   
4    300      0      0    867      0     12   4075     22      2      0   

   MID_o  MLC_o  MMT_o  MRG_o  MSL_o  MUR_o  MWY_o  NOG_o  NSL_o  OGD_o  \
0    279    558    189     87    859    907      4    573   7164   5842   
1     93    276    215   1169    247    325    874    185     88   1030   
2  12167  18228   8403     51     54  23308     32    214   3865    832   
3    477    334     83      1      4    747     41      2     51     22   
4     20     75     25    148   4218     98      0   6276    236  27341   

   OKL_o  ORM_o  PAY_o  PGR_o  PLN_o  PRK_o  PRY_o  PVO_o  PVW_o  ROY_o  \
0      1     54      1     13    361     16    164     19    350   4215   
1    331    221    550     56     64   3060   2432    267    141    179   
2     22   1797    124   1116     53    246     56   1432    121    698   
3      0  32107   7728  14042      0     28      1  36931      0     17   
4      0      3      0      5   2691      6    535      7   3549  10448   

   RVD_o  RVT_o  SAN_o  SAQ_o  SAR_o  SFK_o  SJC_o  SLC_o  SLM_o  SOG_o  \
0   1505    246    699      4     10      6    465   9249      0   1548   
1    188    104    307    613     55    267    200   2814     95    120   
2    162  21345  39186    120   2671    374  30077  73876     99    258   
3      9   2153   2763   2844   9984  15798   2520   2493   4747     19   
4   5153     31    112      0      7      8     38   1348      0   5752   

   SPV_o  SSL_o  SUN_o  SWE_o  SYR_o  TAY_o  TOO_o  UIN_o  VIN_o  WAT_o  \
0     10    694   4314   4512  10839    418     67    319     12    988   
1    235    262    204    213     48    103  11914     33     37     79   
2    523  10686    196    320   1117  19588   2234     56    263    137   
3  13714    287      1      1      7    329     66      0   3732      2   
4     10    123   217

WFCounty      AFK_o      ALA_o      ALP_o      BDL_o  \
0           Davis County   0.449779   1.369261   0.390101   1.302436   
1  Outside Wasatch Front   0.552268   1.383029   0.506212   0.677905   
2       Salt Lake County   9.809071  92.780249  17.647550  78.061639   
3            Utah County  89.120875   4.318936  81.355747  19.630116   
4           Weber County   0.136689   0.216021   0.168957   0.392581   

       BGM_o      BNT_o      BRT_o      CDF_o      CEN_o      CHA_o  \
0   2.573631  72.653084   1.501353   2.344660  72.767400   0.528401   
1  85.216515   0.684273   2.092215   1.149115   0.667194  81.288794   
2   0.984851  23.723366  92.833033  13.658073  22.340964   6.615099   
3   0.059064   0.683683   3.403611  82.867803   1.089175  11.491778   
4  11.227399   2.321218   0.237151   0.045424   3.200859   0.150946   

       CHL_o      CLF_o      CLI_o      CMT_o      COA_o      CWH_o  \
0   0.203447  71.153878  65.620303   1.400886   1.199578   2.254739   
1   0.420924   1.817477   0.623899   8.468884  93.356610   1.432409   
2  10.907100   6.082416   8.513508  86.604902   4.616530  92.663683   
3  88.424536   0.286953   0.190123   3.071157   0.389470   3.214711   
4   0.112912  20.721760  25.114242   0.516304   0.513371   0.500852   

       DAN_o      DRA_o      EAG_o      ELK_o      EMT_o      FAR_o  \
0   0.211737   1.598785   0.503738   0.106806   2.486734  73.536003   
1  90.985208   0.794084   0.916203   2.563467   3.688992   0.800378   
2   4.051034  77.151007  22.702973   5.985065  90.104227  18.512684   
3   4.704583  20.176240  75.726621  91.351178   3.704160   0.862451   
4   0.123499   0.345743   0.215516   0.064112   0.082751   6.353420   

       FCS_o      FFD_o      FRR_o      FTH_o      GLA_o      GOS_o  \
0   0.253750   3.642154  13.141796  76.597883   0.095597   0.000002   
1  93.534924   1.025294   5.153410   0.982301  12.661732  11.905081   
2   4.945005  14.436691   2.796036  15.041352   4.620564  10.233800   
3   1.313762  80.961159   0.258751   0.946662  82.565007  77.676252   
4   0.029652   0.000000  78.712335   6.496498   0.126341   0.252581   

       GRL_o      HAR_o      HDT_o      HEB_o      HER_o      HGH_o  \
0   0.879841  10.533006   0.906249   0.391333   0.688797   0.467984   
1  82.749069   4.023604  79.939663  90.136375   0.467950   0.333909   
2  15.553760   1.857327  15.005898   5.147085  92.666103  18.437424   
3   0.732091   0.214477   4.025349   4.324013   6.163133  80.698131   
4   0.133508  83.434583   0.197654   0.077146   0.077654   0.130863   

       HNF_o      HOL_o      HOO_o      HVL_o      IND_o      INT_o  \
0   0.752993   2.693463  23.454080  10.184730   0.571921   0.310320   
1  91.446505   1.498916   1.501223   5.566406  81.846552  83.133033   
2   3.772765  92.426415   4.153429   6.553262  11.749827   7.397299   
3   0.055607   2.991582   0.145572   0.145065   5.752853   8.961252   
4   4.047419   0.456107  70.807254  77.616574   0.153907   0.273338   

       KAY_o      KMS_o      KMT_o      LAY_o      LEH_o      LIN_o  \
0  76.807981   0.236310   1.525091  76.720430   0.646249   0.447574   
1   0.871229  93.040509   0.927490   0.915658   0.561379   1.233743   
2  15.058650   5.552300  95.824074   9.989320  21.570918   8.446455   
3   0.661021   1.146348   1.506474   0.404734  77.129848  89.825347   
4   6.665578   0.101539   0.280354  12.033276   0.158790   0.116610   

       MAP_o      MID_o      MLC_o      MMT_o      MRG_o      MSL_o  \
0   0.216576   2.653311   3.349799   2.714239   9.218102  16.767851   
1   0.314311   0.992596   1.684413   2.689151  73.212815   5.018710   
2   3.700189  91.550365  92.087889  92.652055   4.770301   1.779119   
3  95.808248   4.506761   2.329584   1.483761   0.189456   0.178319   
4   0.032944   0.362497   0.614370   0.523209  12.679683  76.318558   

       MUR_o      MWY_o      NOG_o      NSL_o      OGD_o      OKL_o  \
0   3.939772   0.664567   8.788342  60.514132  16.796384   0.497092   
1   1.510718  84.228046  

In [78]:
# bu map unit
# block group
df_CountySum_wOutWF_Percent_MU = df_CountySum_wOutWF.copy()

for x in dColCodesWCounty_x:   
    #display(x)
    df_CountySum_wOutWF_Percent_MU[x] = df_CountySum_wOutWF_Percent_MU[x] / df_CountySum_wOutWF_Percent_MU['TTL_o'] * 100

for y in dColCodesWCounty_y:   
    #display(y)
    df_CountySum_wOutWF_Percent_MU[y] = df_CountySum_wOutWF_Percent_MU[y] / df_CountySum_wOutWF_Percent_MU['TTL_d'] * 100

df_CountySum_wOutWF_Percent_MU

WFCounty     AFK_o     ALA_o     ALP_o     BDL_o     BGM_o  \
0           Davis County  0.020565  0.000000  0.000979  0.028399  0.064632   
1  Outside Wasatch Front  0.015268  0.000000  0.000969  0.005574  1.524166   
2       Salt Lake County  0.304639  0.060548  0.064155  1.159716  0.008541   
3            Utah County  5.661250  0.002010  0.644329  0.473781  0.000000   
4           Weber County  0.006950  0.000000  0.001390  0.011815  0.517083   

      BNT_o     BRT_o     CDF_o     CEN_o     CHA_o     CHL_o     CLF_o  \
0  6.421619  0.000000  0.000979  2.050119  0.000000  0.000490  8.769928   
1  0.017450  0.000000  0.000000  0.003393  0.090641  0.001454  0.095245   
2  0.759415  0.022397  0.002657  0.217708  0.002278  0.060358  0.255859   
3  0.020774  0.000000  0.041213  0.010722  0.009717  1.048417  0.012732   
4  0.234216  0.000000  0.000000  0.091741  0.000000  0.000695  3.566067   

      CLI_o     CMT_o     COA_o     CWH_o     DAN_o     DRA_o     EAG_o  \
0  2.811508  0.000490  0.001469  0.086666  0.000000  0.173822  0.014689   
1  0.007755  0.007028  0.140808  0.030294  0.169648  0.036596  0.015995   
2  0.127740  0.056942  0.003037  2.016122  0.003227  4.169095  0.432379   
3  0.003351  0.001005  0.000335  0.086112  0.006366  1.865639  2.737477   
4  1.481054  0.000000  0.000000  0.025715  0.000000  0.042395  0.011120   

      ELK_o     EMT_o     FAR_o     FCS_o     FFD_o     FRR_o     FTH_o  \
0  0.000000  0.000979  3.457343  0.000000  0.000979  0.227682  1.275021   
1  0.003878  0.001454  0.009452  0.201396  0.000000  0.041443  0.004120   
2  0.008162  0.031318  0.300653  0.004745  0.001898  0.014995  0.085033   
3  0.286815  0.001340  0.013068  0.002345  0.022114  0.001340  0.006366   
4  0.000000  0.000000  0.367657  0.000000  0.000000  2.221234  0.118846   

      GLA_o     GOS_o     GRL_o     HAR_o     HDT_o     HEB_o     HER_o  \
0  0.000000  0.000000  0.016158  0.190470  0.000000  0.003427  0.033785   
1  0.014541  0.001454  1.317196  0.035141  0.118027  1.197715  0.010421   
2  0.002278  0.000569  0.166460  0.010439  0.009680  0.033406  2.807424   
3  0.123304  0.015413  0.008042  0.001675  0.002010  0.046574  0.282459   
4  0.000000  0.000000  0.002085  2.504796  0.000000  0.000000  0.000695   

      HGH_o     HNF_o     HOL_o     HOO_o     HVL_o     IND_o     INT_o  \
0  0.007834  0.000000  0.097438  0.502859  0.011751  0.000000  0.000000   
1  0.001696  0.105182  0.027628  0.011875  0.004120  0.206001  0.081673   
2  0.249785  0.001139  1.787975  0.029610  0.003606  0.013856  0.001898   
3  2.181270  0.000000  0.067683  0.000335  0.000000  0.008712  0.004356   
4  0.002780  0.009035  0.020155  2.282394  0.208501  0.000000  0.000000   

      KAY_o     KMS_o     KMT_o      LAY_o     LEH_o     LIN_o     MAP_o  \
0  5.419327  0.000000  0.052391  13.038603  0.053860  0.007834  0.000000   
1  0.018661  0.249140  0.015753   0.060589  0.021327  0.015995  0.000000   
2  0.379043  0.007213  1.791392   0.609088  1.058550  0.093954  0.013856   
3  0.015748  0.002345  0.030156   0.024125  7.051767  2.301558  0.927459   
4  0.602569  0.000000  0.008340   2.832143  0.015290  0.001390  0.000000   

      MID_o     MLC_o     MMT_o     MRG_o     MSL_o     MUR_o     MWY_o  \
0  0.136609  0.273219  0.092542  0.042599  0.420600  0.444103  0.001959   
1  0.022539  0.066890  0.052106  0.283312  0.059862  0.078765  0.211818   
2  2.309373  3.459789  1.594942  0.009680  0.010250  4.424004  0.006074   
3  0.159826  0.111912  0.027810  0.000335  0.001340  0.250293  0.013738   
4  0.013900  0.052125  0.017375  0.102861  2.931528  0.068110  0.000000   

      NOG_o     NSL_o      OGD_o     OKL_o      ORM_o     PAY_o     PGR_o  \
0  0.280563  3.507775   2.860472  0.000490   0.026441  0.000490  0.006365   
1  0.044836  0.021327   0.249625  0.080219   0.053560  0.133295  0.013572   
2  0.040619  0.733601   0.157919  0.004176   0.341082  0.023536  0.211824   
3  0.000670  0.017088   0.007371  0.000000  10.757916  2.589378  4.704976   

In [79]:
df_CountySum_wOutWF           .to_json(os.path.join(dirResults, "sl_countydata_number.json"    ),orient='records')
df_CountySum_wOutWF_Percent_SA.to_json(os.path.join(dirResults, "sl_countydata_percent_sa.json"),orient='records')
df_CountySum_wOutWF_Percent_MU.to_json(os.path.join(dirResults, "sl_countydata_percent_mu.json"),orient='records')